In [1]:
import sys
sys.path.append('./library') # age_gender_predictor
sys.path.append('../.env/lib/python2.7/site-packages')
import os 
import pickle
import age_gender_predictor
from collections import defaultdict
import re
from tabulate import tabulate
from datetime import datetime, timedelta
import math
import numpy as np
from scipy.stats import spearmanr
import pandas as pd
import pytz
import json

In [2]:
import sklearn

## Load Regular User

In [3]:
def checkFolderFile(folder):
    return os.listdir(folder)

In [4]:
regular_clean = []
regular_folder = './Regular/'
for regular_file in checkFolderFile(regular_folder):
    regular_clean.append(pd.read_pickle(regular_folder+regular_file))

In [5]:
len(regular_clean)

268

In [6]:
long_regular_clean = []
regular_folder = './Regular_timeline/'
for regular_file in checkFolderFile(regular_folder):
    long_regular_clean.append(pd.read_pickle(regular_folder+regular_file))

In [7]:
len(long_regular_clean)

409

## Load Different Time Period

In [8]:
regular_month15,regular_month12, regular_month9,regular_month6, regular_month3, regular_month2 = [], [], [], [], [], []
regular_varable = [regular_month15,regular_month12, regular_month9,regular_month6, regular_month3, regular_month2]
regular_folder = ['./Regular_15month/','./Regular_12month/','./Regular_9month/','./Regular_6month/','./Regular_3month/','./Regular_2month/']
for i, folder in enumerate(regular_folder):
    for regular_file in checkFolderFile(folder):
        regular_varable[i].append(pd.read_pickle(folder+regular_file))

In [9]:
len(regular_month3)

257

## Load BD

In [10]:
bd_clean = []
bd_folder = './Bipolar/bd_shift2week/'
for bd_file in checkFolderFile(bd_folder):
    bd_clean.append(pd.read_pickle(bd_folder+bd_file))

In [11]:
long_bd_clean = []
bd_folder = './Bipolar_timeline/'
for bd_file in checkFolderFile(bd_folder):
    long_bd_clean.append(pd.read_pickle(bd_folder+bd_file))

## Load Different Time Period

In [12]:
bd_month15, bd_month12, bd_month9, bd_month6, bd_month3, bd_month2 = [], [], [], [], [], []
bd_varable = [bd_month15, bd_month12, bd_month9, bd_month6, bd_month3, bd_month2]
bd_folder = ['./Bipolar_15month/','./Bipolar_12month/','./Bipolar_9month/','./Bipolar_6month/','./Bipolar_3month/','./Bipolar_2month/']
for i, folder in enumerate(bd_folder):
    for bd_file in checkFolderFile(folder):
        bd_varable[i].append(pd.read_pickle(folder+bd_file))
        

In [13]:
len(bd_month2)

133

### Only Before Diagnosed BD Data

In [14]:
# Load bd diagnosed dict
def getDiagnosedDict(file_path):
    res_dict = {}
    with open(file_path) as bd:
        for line in bd.readlines():
            name, diag_time = line.strip().split('\t')
            seg_dia_time = diag_time.split('/')
            year = int(seg_dia_time[0])
            if len(seg_dia_time) == 2:
                res_dict[name] = datetime(year, int(seg_dia_time[1]), 1)
            elif len(seg_dia_time) ==3:
                res_dict[name] = datetime(year, int(seg_dia_time[1]), int(seg_dia_time[2]))
    return res_dict
dia_dict = getDiagnosedDict('./bipolar_list')

In [15]:
bd_month12_, bd_month9_, bd_month6_, bd_month3_, bd_month2_ = [], [], [], [], []
bd_variable = [bd_month12_, bd_month9_, bd_month6_, bd_month3_, bd_month2_]
bd_time = [12,9,6,3,2]
for timeSeries in long_bd_clean:
    username = timeSeries.name[0]
    for i in xrange(len(bd_time)):
        temp_ts = timeSeries[timeSeries.index <= dia_dict[username]]
        if temp_ts.shape[0] > 30 and ((temp_ts.index[-1] - temp_ts.index[0]).days)/25 >= bd_time[i]:
            bd_variable[i].append(temp_ts)

In [16]:
len(bd_month2_)

148

## Load Test Data (mention recently diagnosed people)

In [17]:
def load(folder, col = [ 'name', 'text', 'emotion','emotion_2','ambiguous', 'polarity', 'dt']):
#     return [pd.read_csv(folder + file_name, delimiter = '\t', names = col, parse_dates=True) for file_name in os.listdir(folder)]
    return_list = []
    for file_name in os.listdir(folder):
        try:
            return_list.append(pd.read_csv(folder+file_name, delimiter='\t', names=col, parse_dates=True, engine='python'))
        except:
            print(file_name)
    return return_list

In [18]:
recent_clean = load('recent_bipolar_test/')

print(len(recent_clean))

25


In [19]:
test_regular = load('normal_900/', col = [ 'name', 'text', 'polarity','emotion','emotion_2','ambiguous', 'dt'])

MarcyRubin
shelz1986
Johnnyboy_Kiing
mumsgonemental
KP_820
stupidinvisible
Insert_PenName
Brittneey_Lani
shmorderline
potd2014
HeidiElsokary


In [20]:
# del test_regular[776]

In [21]:
filtered_test_regular = []
for i, test in enumerate(test_regular):
#     print(i)
    begin_day = test.index[-1] - timedelta(days = 145)
    temp = test[test.index >= begin_day]
    if temp.shape[0] > 100:
        filtered_test_regular.append(temp)
print(len(filtered_test_regular))
# del test_regular

360


In [22]:
import random

In [23]:
test_regular50 = random.sample(filtered_test_regular, 50) 

In [24]:
def segmentPeriod(groups, day = 120, endday = 30):
    return_groups = []
    for timeSeries in groups:
#         period_range = timeSeries.index[-1] - timeSeries.index[0]
        begin = timeSeries.index[-1] - timedelta(days = day)
        end = timeSeries.index[-1] - timedelta(days = endday)
        temp = timeSeries[timeSeries.index >= begin]
        temp = temp[temp.index <= end]
        if temp.shape[0]>0:
            return_groups.append(temp)
    return return_groups

In [25]:
recent_month4x = segmentPeriod(recent_clean, day = 145, endday = 0)
recent_month4 = segmentPeriod(recent_clean, endday = 0)
recent_month3 = segmentPeriod(recent_clean, day = 90, endday = 0)
recent_month2 = segmentPeriod(recent_clean, day = 60, endday = 0)

In [26]:
test_regular_month4x = segmentPeriod(test_regular50, day = 145, endday = 0)
test_regular_month4 = segmentPeriod(test_regular50, endday = 0)
test_regular_month3 = segmentPeriod(test_regular50, day = 90, endday = 0)
test_regular_month2 = segmentPeriod(test_regular50, day = 60, endday = 0)

## Group together

In [27]:
groups = [regular_month2, bd_month2, regular_month3, bd_month3, regular_month6, bd_month6,
          regular_month9, bd_month9, regular_month12, bd_month12, regular_month15, bd_month15,
          recent_month2, recent_month3, recent_month4, recent_month4x,
          test_regular_month2, test_regular_month3, test_regular_month4, test_regular_month4x]
group_names = ["Regular_2", "Bipolar_2", "Regular_3", "Bipolar_3", "Regular_6", "Bipolar_6",
               "Regular_9", "Bipolar_9", "Regular_12", "Bipolar_12", "Regular_15", "Bipolar_15",
               "Recent2", "Recent3", "Recent4", "Recent4.x",
               "Test_Regular2", "Test_Regular3", "Test_Regular4","Test_Regular4.x"]

In [28]:
#Statistics facts of experimental data

headers = ["Group","Users", "Tweets", "Average tweets"]
contents = []
for i, group in enumerate(groups):
    group_name = group_names[i]
    tweets_num = sum([timeSeries.shape[0] for timeSeries in group])
    users_num = len(group)
    average_tweets_num = tweets_num / users_num
    contents.append([group_name, users_num, tweets_num, average_tweets_num])
    
print(tabulate(contents, headers=headers))

Group              Users    Tweets    Average tweets
---------------  -------  --------  ----------------
Regular_2            260     67485               259
Bipolar_2            133    136837              1028
Regular_3            257     89141               346
Bipolar_3            135    226460              1677
Regular_6            267    136481               511
Bipolar_6            124    353559              2851
Regular_9            289    170380               589
Bipolar_9            117    481392              4114
Regular_12           295    207008               701
Bipolar_12           111    586656              5285
Regular_15           278    213394               767
Bipolar_15           111    692941              6242
Recent2               25     34265              1370
Recent3               25     49248              1969
Recent4               25     65532              2621
Recent4.x             25     80694              3227
Test_Regular2         50     16102            

## Age Gender

In [27]:
#Age and gender Distribution
def getAgeGender(group):
    features = {"age":[],"gender":[]}
    for timeSeries in group:
        
        features["age"].append(getAge(timeSeries))
        features["gender"].append(getGender(timeSeries))

    return features
def getAge(timeSeries):
    texts = ""
    for text in timeSeries["text"].values:
        texts += text + "\n"
    return age_gender_predictor.get_age(texts)

def getGender(timeSeries):
    texts = ""
    for text in timeSeries["text"].values:
        texts += text + "\n"
    return age_gender_predictor.get_gender(texts)

In [30]:
headers = ["Group","Male users", "Female users", "Average age"]
contents = []
for i, group in enumerate(groups):
    group_name = group_names[i]
    users_num = float(len(group))
    try:
        users_gender = [getGender(timeSeries) for timeSeries in group]
    except:
        print(i)
        break
    users_age = [getAge(timeSeries) for timeSeries in group]
    male_ratio = len([gender for gender in users_gender if gender < 0]) / users_num
    female_ratio = 1 - male_ratio
    average_age = sum(users_age) / users_num
    contents.append([group_name, male_ratio, female_ratio, average_age])
print(tabulate(contents, headers=headers))

Group              Male users    Female users    Average age
---------------  ------------  --------------  -------------
Regular_2            0.503846        0.496154        29.8115
Bipolar_2            0.24812         0.75188         24.8592
Regular_3            0.478599        0.521401        30.1312
Bipolar_3            0.207407        0.792593        24.4102
Regular_6            0.453184        0.546816        30.6582
Bipolar_6            0.233871        0.766129        24.0319
Regular_9            0.477509        0.522491        30.4293
Bipolar_9            0.205128        0.794872        24.3903
Regular_12           0.471186        0.528814        29.7549
Bipolar_12           0.207207        0.792793        24.4096
Regular_15           0.467626        0.532374        30.2141
Bipolar_15           0.189189        0.810811        24.4064
Recent2              0.2             0.8             34.4881
Recent3              0.2             0.8             31.9946
Recent4              0.1

## Social

In [28]:
def getTweetRate(timeSeries):
    total_tweets = timeSeries.shape[0]
    if total_tweets == 0: return 0.0
    delta_time = np.max(timeSeries.index.values) - np.min(timeSeries.index.values)
    total_duration = (delta_time).astype('timedelta64[h]') / np.timedelta64(24, 'h')
    try:
        result = total_tweets / float(total_duration)
    except:
        result = total_tweets / 1.0
    return result

def getLateTweetRate(timeSeries):
    total_late = 0
    for index in timeSeries.index:
        if int(index.hour) <6:
            total_late += 1
    delta_time = np.max(timeSeries.index.values) - np.min(timeSeries.index.values)
    total_duration = (delta_time).astype('timedelta64[h]') / np.timedelta64(24, 'h')
    try:
        result = total_late / float(total_duration)
    except:
        result = total_late / 1.0
    return result

def getMentionRate(timeSeries):
    total_tweets = timeSeries.shape[0]
    total_mentions = np.sum(seriesContains(timeSeries))
    return total_mentions / float(total_tweets)

def thirdPronuonDetect(words, matcher=re.compile("@[a-z]+")):
    for word in words:
        if word == "@":
            continue
        elif matcher.search(word):
            return True
    return False

def seriesContains(timeSeries):
    match_function = np.vectorize(thirdPronuonDetect)
    return match_function(timeSeries["text"].str.lower().str.split().values)


def getUniqueMentions(timeSeries):
    total_tweets = timeSeries.shape[0]
    friends_set = set()
    texts = timeSeries["text"].values
    for text in texts:
        terms = text.strip().split()
        for word in terms:
            if word[0] == '@' and len(word) > 1:
                friends_set.add(word)
    return len(friends_set)

def getFrequentMentions(timeSeries, lowerbound = 3):
    total_tweets = timeSeries.shape[0]
    friends_mentions = {}
    texts = timeSeries["text"].values
    for text in texts:
        terms = text.strip().split()
        for word in terms:
            if word[0] == '@' and len(word) > 1:
                friends_mentions[word] = friends_mentions.get(word, 0) +1
    frequent_frients = [screen_name for screen_name, mentions in friends_mentions.items() if mentions >= lowerbound]
    return len(frequent_frients)
 

def getSocialFeature_group(group):
    social_features = {"tweets_rate": [],"mention_rate": [],"unique_mentions": [],"frequent_mentions": [], "late_tweets_rate": [], "long_tweets_rate": []}
    for timeSeries in group:
        social_features["tweets_rate"].append(getTweetRate(timeSeries))
        social_features["mention_rate"].append(getMentionRate(timeSeries))
        social_features["unique_mentions"].append(getUniqueMentions(timeSeries))
        social_features["frequent_mentions"].append(getFrequentMentions(timeSeries))
        social_features["late_tweets_rate"].append(getLateTweetRate(timeSeries))
        try:
            social_features["long_tweets_rate"].append(total_dict[str(timeSeries['name'][0])])
        except:
            print('No found in long_term ' + str(timeSeries['name'][0]))
            social_features["long_tweets_rate"].append(0.0)
    return social_features

def getGBSocialFeature_group(group):
    social_features = {"tweets_rate": [],"mention_rate": [],"unique_mentions": [],"frequent_mentions": []}
    for timeSeries in group:
        social_features["tweets_rate"].append(getTweetRate(timeSeries))
        social_features["mention_rate"].append(getMentionRate(timeSeries))
        social_features["unique_mentions"].append(getUniqueMentions(timeSeries))
        social_features["frequent_mentions"].append(getFrequentMentions(timeSeries))
        
    return social_features

def getNoLongSocialFeature_group(group):
    social_features = {"tweets_rate": [],"mention_rate": [],"unique_mentions": [],"frequent_mentions": [], "late_tweets_rate": []}
    for timeSeries in group:
        social_features["tweets_rate"].append(getTweetRate(timeSeries))
        social_features["mention_rate"].append(getMentionRate(timeSeries))
        social_features["unique_mentions"].append(getUniqueMentions(timeSeries))
        social_features["frequent_mentions"].append(getFrequentMentions(timeSeries))
        social_features["late_tweets_rate"].append(getLateTweetRate(timeSeries))
        
    return social_features

In [32]:
header = ["tweets_rate", "late_tweets_rate", "mention_rate", "unique_mentions", "frequent_mentions"]
contents = []
for i, group in enumerate(groups):
   
    group_name = group_names[i]
    content = [group_name]
    tweets_rate = np.mean([getTweetRate(timeSeries) for timeSeries in group])
    mention_rate = np.mean([getMentionRate(timeSeries) for timeSeries in group])
    unique_mentions = np.mean([getUniqueMentions(timeSeries) for timeSeries in group])
    frequent_mention = np.mean([getFrequentMentions(timeSeries) for timeSeries in group]) 
    late_tweets_rate = np.mean([getLateTweetRate(timeSeries) for timeSeries in group])
    content += [tweets_rate, late_tweets_rate, mention_rate, unique_mentions, frequent_mention]
    contents.append(content)


print("\n======Mean Distribution======\n")

print(tabulate(contents, headers=header,))


======Mean Distribution======

                   tweets_rate    late_tweets_rate    mention_rate    unique_mentions    frequent_mentions
---------------  -------------  ------------------  --------------  -----------------  -------------------
Regular_2              4.49298            0.414508        0.431381            53.6769              11.5
Bipolar_2             17.956              4.04942         0.396966           117.489               36.3308
Regular_3              3.99729            0.338119        0.421551            71.3307              15.7004
Bipolar_3             17.4618             3.85854         0.402067           169.622               54.1556
Regular_6              2.85013            0.310132        0.427669            92.4981              20.8989
Bipolar_6             15.2578             3.56412         0.409098           267.5                 84.9758
Regular_9              2.17571            0.256841        0.421164           103.239               23.8062
Bipolar_

In [33]:
# header = ["tweets_rate", "late_tweets_rate", "mention_rate", "unique_mentions", "frequent_mentions"]
# contents = []
# for i, timeSeries in enumerate(regular_clean):
# #     content = [i]
#     content = [str(timeSeries['name'][0])]
#     tweets_rate = getTweetRate(timeSeries)
#     mention_rate = getMentionRate(timeSeries)
#     unique_mentions = getUniqueMentions(timeSeries)
#     frequent_mention = getFrequentMentions(timeSeries)
#     late_tweets_rate = getLateTweetRate(timeSeries)
#     content += [tweets_rate, late_tweets_rate, mention_rate, unique_mentions, frequent_mention]
#     contents.append(content)
# print("\n======Mean Distribution======\n")
# print(tabulate(contents, headers=header,))

## Polarity Feature

In [29]:
def getFlipsCount(timeSeries, upperbound=120, lowerbound = 0):
    flips = getFlips(timeSeries)
    durations = getFlipsDuration(timeSeries, flips)
    return np.sum((durations > lowerbound) & (durations < upperbound) )

def getFlips(timeSeries, attribute= 'polarity'):
    flips = np.zeros(timeSeries.shape[0],dtype=bool)
    polarity = timeSeries[attribute].values[:-1]
    right_elements = timeSeries[attribute].values[1:]
    flips[:-1] = (polarity * right_elements) < 0
    return flips

def getFlipsDuration(timeSeries, flips):
    filtered_timeSeries = timeSeries['dt'][flips].index.values
    dt = np.zeros(filtered_timeSeries.shape[0],dtype=float)
    dt[:-1] = (filtered_timeSeries[1:] - filtered_timeSeries[:-1]).astype('timedelta64[s]') / np.timedelta64(60, 's')
    return dt

def getCombosCount(timeSeries, matcher = -1, lowerbound = 2):
    combos = comboTracker(timeSeries)
    combos_count = sum([hit for element, hit in combos if element == matcher and hit > lowerbound])
    return combos_count

def getNegativeRatio(timeSeries):
    total_tweets = timeSeries.shape[0]
    return np.sum(timeSeries["polarity"].values == -1) / float(total_tweets)

def getPositiveRatio(timeSeries):
    total_tweets = timeSeries.shape[0]
    return np.sum(timeSeries["polarity"].values == 1) / float(total_tweets)

def getPolarity(group):
    polarity = {"flips":[],"negative_combos":[],"positive_combos":[], "positive_ratio":[], "negative_ratio":[]}
    for timeSeries in group:
        try:
            tweets_length = float(timeSeries.shape[0])
        except:
            print 'error'
            print timeSeries
            break
        flips_ratio = getFlipsCount(timeSeries) / tweets_length
        negative_combos_ratio = getCombosCount(timeSeries,matcher=-1) / tweets_length
        positive_combos_ratio = getCombosCount(timeSeries,matcher=1) / tweets_length
        positive_ratio = getPositiveRatio(timeSeries)
        negative_ratio = getNegativeRatio(timeSeries)
        
        polarity["flips"].append(flips_ratio)
        polarity["negative_combos"].append(negative_combos_ratio)
        polarity["positive_combos"].append(positive_combos_ratio)
        polarity["positive_ratio"].append(positive_ratio)
        polarity["negative_ratio"].append(negative_ratio)
        
    return polarity

def comboTracker(timeSeries, attribute= "polarity", lowerbound = 120):
    array = timeSeries[attribute]
#     the polarity of starter
    starter = array[0]
    combo = 1
    result = []
    i = 0 
#     begin from second one in the array
    for cursor in array[1:]:
        i += 1
        if starter == cursor and timeSeries["dt"][i-1] < lowerbound:
            combo += 1
        else:
            if combo > 1:
                result.append((starter, combo))
            starter = cursor
            combo = 1
    if combo > 1:
         result.append((starter, combo))
    return result

In [35]:
headers = ["Group","Positive Ratio","Negative Ratio", "Flip Ratio", "Positive Combos", "Negative Combos"]
contents = []
for i, group in enumerate(groups):
    group_name = group_names[i]
   
    positive_ratio_mean = np.mean([getPositiveRatio(timeSeries) for timeSeries in group])
    negative_ratio_mean = np.mean([getNegativeRatio(timeSeries) for timeSeries in group])
    flips_ratio_mean = np.mean([getFlipsCount(timeSeries) / float(len(timeSeries)) for timeSeries in group])
    negative_combos_ratio = np.mean([getCombosCount(timeSeries,matcher=-1) / float(len(timeSeries)) for timeSeries in group])
    positive_combos_ratio = np.mean([getCombosCount(timeSeries,matcher=1) / float(len(timeSeries)) for timeSeries in group])
    
    contents.append([group_name, positive_ratio_mean, negative_ratio_mean, flips_ratio_mean, positive_combos_ratio, negative_combos_ratio])
print("\n=========\n")
print(tabulate(contents, headers=headers))



Group              Positive Ratio    Negative Ratio    Flip Ratio    Positive Combos    Negative Combos
---------------  ----------------  ----------------  ------------  -----------------  -----------------
Regular_2               0.223811           0.108312    0.00432236         0.0332145          0.00439527
Bipolar_2               0.0982161          0.172691    0.00578583         0.00643929         0.0186712
Regular_3               0.214817           0.109222    0.00470779         0.030426           0.0031437
Bipolar_3               0.097095           0.173152    0.00561589         0.00620796         0.0191976
Regular_6               0.223818           0.112794    0.00440139         0.0323001          0.00564947
Bipolar_6               0.100064           0.167476    0.00546895         0.00615428         0.0177763
Regular_9               0.225617           0.115473    0.00429804         0.0266098          0.00338021
Bipolar_9               0.100268           0.16423     0.0052977  

In [36]:
headers = ["Group","Positive Ratio Mean","Positive Ratio STD", "Negative Ratio Mean", "Negative Ratio STD"]
contents = []
for i, group in enumerate(groups):
    group_name = group_names[i]
   
    positive_ratios = [getPositiveRatio(timeSeries) for timeSeries in group]
    negative_ratios = [getNegativeRatio(timeSeries) for timeSeries in group]
    positive_ratio_mean = np.mean(positive_ratios)
    negative_ratio_mean = np.mean(negative_ratios)
    positive_ratio_std = np.std(positive_ratios)
    negative_ratio_std = np.std(negative_ratios)

    contents.append([group_name, positive_ratio_mean, positive_ratio_std, negative_ratio_mean, negative_ratio_std])
print("\n=========\n")
print(tabulate(contents, headers=headers))



Group              Positive Ratio Mean    Positive Ratio STD    Negative Ratio Mean    Negative Ratio STD
---------------  ---------------------  --------------------  ---------------------  --------------------
Regular_2                    0.223811              0.158477                0.108312             0.0823516
Bipolar_2                    0.0982161             0.0590432               0.172691             0.0754925
Regular_3                    0.214817              0.145268                0.109222             0.0795563
Bipolar_3                    0.097095              0.0570975               0.173152             0.0747214
Regular_6                    0.223818              0.144994                0.112794             0.0837599
Bipolar_6                    0.100064              0.0644627               0.167476             0.0670088
Regular_9                    0.225617              0.142528                0.115473             0.0817134
Bipolar_9                    0.100268       

## Emotion

In [30]:
def getUsersEmotions(timeSeries):
    non_ambiguous = np.invert(timeSeries["ambiguous"].values)
    
    filtered_emotions = timeSeries["emotion"][non_ambiguous].values
    emotions_count = {"joy":0,"sadness": 0,"fear":0,\
                "anticipation": 0, "anger":0, "trust": 0, "disgust": 0 ,"surprise" : 0}
    if float(filtered_emotions.shape[0]) == 0:
        divider = 1.0
    else:
        divider = float(filtered_emotions.shape[0])
    for emotion in emotions_count:
        emotions_count[emotion] = np.sum(filtered_emotions == emotion) / divider
    return emotions_count

def getGroupEmotions(group):
    emotions_counts = {"joy":[],"sadness": [],"fear":[],\
                "anticipation": [], "anger":[], "trust": [], "disgust": [] ,"surprise" : []}
    for timeSeries in group:
        emotions_count = getUsersEmotions(timeSeries)
        for emotion, count in emotions_count.items():
            emotions_counts[emotion].append(count)
    return emotions_counts



In [38]:
emotions = ["joy","sadness","fear", "anticipation", "anger", "trust", "disgust" ,"surprise"]

headers = ["Group"] + emotions
contents = []
for i, group in enumerate(groups):
   
    group_name = group_names[i]
    content = [group_name]
    emotions_counts = getGroupEmotions(group)
    for emotion in emotions:
        emotion_ratio = "{}%".format(round(np.mean(emotions_counts[emotion])*100, 2))
        
        content.append(emotion_ratio)
    contents.append(content)
    
print("\n======Eight Emotional Features======\n")

print("\n======Distribution======\n")

print(tabulate(contents, headers=headers,))



======Eight Emotional Features======


======Distribution======

Group            joy     sadness    fear    anticipation    anger    trust    disgust    surprise
---------------  ------  ---------  ------  --------------  -------  -------  ---------  ----------
Regular_2        16.17%  26.27%     6.67%   13.84%          6.98%    15.14%   11.69%     3.25%
Bipolar_2        13.73%  28.14%     4.09%   14.27%          13.26%   5.62%    16.5%      4.39%
Regular_3        15.99%  26.33%     6.78%   14.04%          7.08%    14.58%   11.92%     3.29%
Bipolar_3        13.69%  28.46%     4.21%   14.02%          13.15%   5.39%    16.67%     4.42%
Regular_6        16.48%  26.13%     6.88%   13.61%          7.03%    14.9%    11.8%      3.18%
Bipolar_6        13.81%  28.0%      4.07%   14.31%          13.21%   5.41%    16.7%      4.51%
Regular_9        16.87%  25.81%     6.62%   13.84%          7.14%    14.57%   11.96%     3.19%
Bipolar_9        14.15%  27.34%     4.19%   14.38%          13.05%   5.

## Long Term Feature

In [31]:
# 8 weeks sliding windows, move 1 week per time
def slideWindows(timeline, start):
    
    limit = start + timedelta(weeks=8)
    
    status = False
    if timeline.index[-1] < limit: status = True
    
    new_start = start + timedelta(weeks=1)
    
    return timeline[timeline.index < limit], new_start, timeline[timeline.index > new_start],status
    
        
def getTimeSeries(timeline):
    timeSeries_list = []
    start = timeline.index[0]
    
    while True:
        timeSeries, start, timeline, status = slideWindows(timeline, start)
        timeSeries_list.append(timeSeries)
        if status: break
            
    return timeSeries_list

In [32]:
bd_dict = {}
regular_dict = {}
for i, bd_timeline in enumerate(long_bd_clean):
    try:
        tweets_rate_array = np.asarray([getTweetRate(timeSeries) for timeSeries in getTimeSeries(bd_timeline)])
    except:
        tweets_rate_array = np.asarray([0.0, 0.0])
    bd_dict[str(bd_timeline['name'][0])] = np.ptp(tweets_rate_array)
    
for i, regular_timeline in enumerate(long_regular_clean):
    try:
        tweets_rate_array = np.asarray([getTweetRate(timeSeries) for timeSeries in getTimeSeries(regular_timeline)])
    except:
        tweets_rate_array = np.asarray([0.0, 0.0])
    regular_dict[str(regular_timeline['name'][0])] = np.ptp(tweets_rate_array)

total_dict = {}
total_dict.update(bd_dict)
total_dict.update(regular_dict)
del bd_dict
del regular_dict

In [33]:
len(total_dict)

574

In [34]:
recent_dict = {}
for i, timeline in enumerate(recent_clean):
    try:
        tweets_rate_array = np.asarray([getTweetRate(timeSeries) for timeSeries in getTimeSeries(regular_timeline)])
    except:
        tweets_rate_array = np.asarray([0.0, 0.0])
    recent_dict[str(timeline['name'][0])] = np.ptp(tweets_rate_array)
    
print(len(recent_dict))
total_dict.update(recent_dict)
print((len(total_dict)))
del recent_dict

25
599


In [35]:
tresult_dict = {}
for i, timeline in enumerate(test_regular):
    try:
        tweets_rate_array = np.asarray([getTweetRate(timeSeries) for timeSeries in getTimeSeries(regular_timeline)])
    except:
        tweets_rate_array = np.asarray([0.0, 0.0])
    tresult_dict[str(timeline['name'][0])] = np.ptp(tweets_rate_array)
print(len(tresult_dict))
total_dict.update(tresult_dict)
print((len(total_dict)))
del tresult_dict

920
1519


### LIWC

In [36]:
#Functions for LIWC and POL features extraction:
def loads_LIWC():
    f = open("LIWC/categories.json", 'r')
    categories = json.load(f)
    f = open("LIWC/words.json", 'r')
    words = json.load(f)
    patterns_categories = {}
    for word, category in words.items():
        if word[-1] == '*':
            current_dict = patterns_categories
            for char in word:
                if char == '*':
                    #current_dict = category
                    pre_dict[word[-2]] = category
                    break
                
                elif char not in current_dict:
                    current_dict[char] = {}
                pre_dict = current_dict
                current_dict = current_dict[char]
                
    return categories, words, patterns_categories

LIWC_categories, LIWC_words, LIWC_patterns_categories = loads_LIWC()

def getLIWC_user(timeSeries):
    LIWC_counts = {}
    features = np.zeros(len(LIWC_categories),dtype=int)
    
    texts= timeSeries["text"].values
    for text in texts:
        words = text.strip().split()
        for word in words:
            category_indices = LIWC_words.get(word,[])
            if category_indices == []:
                current_dict = LIWC_patterns_categories
                for char in word[:-1]:
                    current_dict = current_dict.get(char,[])
                    if isinstance(current_dict,list):
                        category_indices = current_dict                            
                        break

            for category_index in category_indices:
                category_name = LIWC_categories[category_index]
                LIWC_counts[category_name] = LIWC_counts.get(category_name,0) + 1

    for category_name in LIWC_counts:
        LIWC_counts[category_name] /= timeSeries.shape[0]
    
    return LIWC_counts

def getLIWC_group(group):
    LIWC_counts = {}
    users_num = len(group)
    for category in LIWC_categories.values():
        LIWC_counts[category] = []
    for timeSeries in group:
        user_LIWC_count = getLIWC_user(timeSeries)
      
        for category in LIWC_categories.values():
            LIWC_counts[category].append(user_LIWC_count.get(category,0))
            
    return LIWC_counts

## Phonology Feature
Construct the phonetic dictionary

In [37]:
sys.path.append('./library/English_to_IPA/src/')

In [38]:
from nltk import TweetTokenizer

In [39]:
import conversion as cv

In [40]:
tknzr = TweetTokenizer()

In [262]:
print(cv.convert('some'))


('s ah1 m', 's\xca\x8c m')


In [41]:
eSPEDictV2 = dict()
with open('./library/eSPEPhonologicalTableV2.txt') as openFile:
    for line in openFile.readlines():
        line = line.strip().split('\t')
        eSPEDictV2[line[0]] = np.array([eval(x) for x in line[1:]])

In [80]:
### (8 classes + 1 class:#(words))
def getTweetScoreV2(tweet):
    wordCount = 0.0
    words = tknzr.tokenize(re.sub('\W|\_' ,' ' ,tweet).lower())
    score = np.zeros((8,))
    for word in words:
        # 字典裡找不到這個字
        try:
            cmu, ipa = cv.convert(word.encode('ascii'))
        except:
            continue
        ipa = re.sub('[ˌ\ˈ ]' ,'' ,ipa)
        if '*' in ipa:
            continue
        wordCount += 1
        i = 0
        while i < len(ipa):
            # 最後一個音標
            if i == len(ipa)-1:
                sym = ipa[i]
                if sym in eSPEDictV2:
                    score += eSPEDictV2[sym]
                i += 1
            # 非最後一個音標
            else:
                try:
                    sym = ipa[i] + ipa[i+1]
                    score += eSPEDictV2[sym]
                    i += 2
                except KeyError:
                    sym = ipa[i]
                    if sym in eSPEDictV2:
                        score += eSPEDictV2.get(sym)
                    i += 1

    score = np.append(score, wordCount)
    return score

In [78]:
getTweetScoreV2("Hi how are you~~~ Q？")

array([ 14.,   7.,  12.,   3.,   7.,   5.,   5.,   3.,   5.])

In [43]:
def getPhonology_group(group):
    phono_dict = {'OC':[],'MO':[],'Obs':[],'TP':[],'Res':[],'Vow':[],'Rou':[],'Ten':[],'WC':[]}
    
    for timeSeries in group:
        score = np.zeros((9,))
        tweets= timeSeries["text"].values
        for tweet in tweets:
            score += getTweetScoreV2(tweet)
        score[:8] /= score[8]
        phono_dict['OC'].append(score[0])
        phono_dict['MO'].append(score[1])
        phono_dict['Obs'].append(score[2])
        phono_dict['TP'].append(score[3])
        phono_dict['Res'].append(score[4])
        phono_dict['Vow'].append(score[5])
        phono_dict['Rou'].append(score[6])
        phono_dict['Ten'].append(score[7])
        phono_dict['WC'].append(score[8])
        
    return phono_dict

In [81]:
compare_set = [(bd2_group,regular2_group),(bd3_group,regular3_group),(bd6_group,regular6_group),(bd9_group,regular9_group),(bd12_group,regular12_group)]
headers = ["2 months", "3 months", "6 months", "9 months", "12 months"]
contents = []

for h, header in enumerate(headers):
#     print(header)
    groupScoresV2 = []
    SCORES = np.array([])
    LABELS = np.array([])
    for i, person in enumerate(compare_set[h][0].getTexts()):# Type of groupTextCase1: List
        tweets = person.split('\n')
        score = np.zeros((9,))
        for tweet in tweets:
            score += getTweetScoreV2(tweet)
        score[:8] /= score[8]
        groupScoresV2.append(list(score))

#     print('')
    ## Ordinary People
    baseScoresV2 = []
    for i, person in enumerate(compare_set[h][1].getTexts()):
        tweets = person.split('\n')
        score = np.zeros((9,))
        for tweet in tweets:
            score += getTweetScoreV2(tweet)
        score[:8] /= score[8]
        baseScoresV2.append(list(score))
#     print('')
    ### RandomForest Classifier

    classifierV2 = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
    X = np.array(baseScoresV2 + groupScoresV2)
    Y = np.array([0] * len(baseScoresV2) + [1]*len(groupScoresV2), dtype=int)
    sss = StratifiedShuffleSplit(Y, 10, random_state=randint(0,65536))
    precisionsV2 = []
    accuracyV2 = []
    for train_index, test_index in sss:
        X_train, X_test = X[train_index], X[test_index]
        Y_train, Y_test = Y[train_index], Y[test_index]
        classifierV2 = classifierV2.fit(X_train, Y_train)
        score = classifierV2.predict_proba(X_test)[:,1]
        SCORES = np.concatenate((SCORES, score))
        LABELS = np.concatenate((LABELS, Y_test))
        
        accuracyV2.append(classifierV2.score(X_test, Y_test))
#         precisionsV2.append(precision)

    average_precision = average_precision_score(LABELS, SCORES)
    contents.append(average_precision)
    contents.append(np.array(accuracyV2).mean())
#     print(np.array(precisionsV2).mean())
    
print("Average Precision of Phonology Performance\n")
print(tabulate([contents], headers=headers))


Average Precision of Phonology Performance

  2 months    3 months
----------  ----------
  0.886424    0.873171


## Group Class

In [44]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cross_validation import StratifiedShuffleSplit
from sklearn.metrics import precision_recall_curve
from sklearn.metrics import average_precision_score
from sklearn.metrics import roc_curve, auc
from sklearn.preprocessing import Imputer
from sklearn.externals import joblib
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import SGDClassifier 
from sklearn.svm import SVC
from sklearn.naive_bayes import GaussianNB
from sklearn.naive_bayes import MultinomialNB
from sklearn import preprocessing

import matplotlib.pyplot as plt
from matplotlib import rcParams
from random import randint
from operator import itemgetter 
import time
rcParams['figure.figsize'] = 12, 8

/media/yenhao/blue/research/tweets_server/local/lib/python2.7/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [45]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from plotly.graph_objs import Scatter, Layout
init_notebook_mode(connected=True)

In [46]:
# function to delete url
# def del_url(line):
def replace_by_symbols(txt):
    txt = re.sub(r"https?\S+", '', txt)
    txt = re.sub(r"pic.twitter.com\S+", '', txt)
    txt = re.sub(r"twitter.com/\S+", '', txt)
    txt = re.sub(r"\S+/\S+", '', txt)
    txt = re.sub(r"@\S+", '', txt)
    txt = re.sub(r"#\S+", '', txt)
    txt = re.sub(r"idk", 'i do not know', txt)   # idk: i don't know
    txt = re.sub(r"tbh", 'to be honest', txt)   # tbh: to be honest
    txt = re.sub(r"tho", 'though', txt)   # tho
    txt = re.sub(r"i\'m", 'i am', txt)
    txt = re.sub(r"you\'re", 'you are', txt)
    txt = re.sub(r"he\'s", 'he is', txt)
    txt = re.sub(r"she\'s", 'she is', txt)
    txt = re.sub(r"it\'s", 'it is', txt)
    txt = re.sub(r"we\'re", 'we are', txt)
    txt = re.sub(r"they\'re", 'they are', txt)
    txt = re.sub(r"isn\'t", 'is not', txt)
    txt = re.sub(r"don\'t", 'do not', txt)
    txt = re.sub(r"doesn\'t", 'does not', txt)
    txt = re.sub(r"didn\'t", 'did not', txt)
    txt = re.sub(r"wasn\'t", 'was not', txt)
    txt = re.sub(r"weren\'t", 'were not', txt)
    txt = re.sub(r"haven\'t", 'have not', txt)
    txt = re.sub(r"can\'t", 'can not', txt)
    txt = re.sub(r"couldn\'t", 'could not', txt)
    txt = re.sub(r"wouldn\'t", 'would not', txt)
    txt = re.sub(r"shouldn\'t", 'should not', txt)
    txt = re.sub(r"&amp", '', txt)
    return txt

In [47]:
#Wrap group to be object
class Group(object):
    def __init__(self, group_name, group_data_list):
        self.name = group_name
        self.timeSerieses_list = group_data_list
        
    def getName(self):
        return self.name
    
    def getSize(self):
        return len(self.timeSerieses_list)
    
    def getTexts(self, tail_k = "all"):
        if tail_k == "all":
            return ["\n".join(map(replace_by_symbols, timeSeries["text"].values)) for timeSeries in self.timeSerieses_list]
        else:
            return ["\n".join(map(replace_by_symbols, timeSeries["text"].tail(tail_k).values)) for timeSeries in self.timeSerieses_list]
    
    def getGroup(self, tail_k="all"):
        if tail_k =="all":
#             return [timeSeries for timeSeries in self.timeSerieses_list if str(timeSeries['name'][0]) in total_dict]
            
            return self.timeSerieses_list
        else:
            return [timeSeries.tail(tail_k) for timeSeries in self.group]

In [412]:
# for g in regular12_group.getGroup():
# #     print g.name.values[0]
#     if g.name.values[0] == 1252843136:
#         reg_gro = g
# reg_gro = reg_gro[reg_gro.index > datetime(2015,3,25)]
# reg_gro = reg_gro[reg_gro.index < datetime(2015,6,25)]
# reg_gro.to_csv('reg_10_3', date_format='%Y-%m-%d %H:%M-%S', columns=['name','text','polarity','emotion','emotion_2','ambiguous'], header=False, sep='\t',encoding='utf-8')
# reg_gro

In [59]:
# bipolar_group = Group("Bipolar", bd_clean)
# regular_group = Group("Regular", regular_clean)

# long_bipolar_group = Group("Long_Bipolar", long_bd_clean)
# long_regular_group = Group("Long_Regular", long_regular_clean)

In [48]:
bd2_group = Group("Bd_2", bd_month2_)
bd3_group = Group("Bd_3", bd_month3_)
bd6_group = Group("Bd_6", bd_month6_)
bd9_group = Group("Bd_9", bd_month9_)
bd12_group = Group("Bd_12", bd_month12_)


In [49]:
bipolar2_group = Group("Bipolar_2", bd_month2)
regular2_group = Group("Regular_2", regular_month2)

bipolar3_group = Group("Bipolar_3", bd_month3)
regular3_group = Group("Regular_3", regular_month3)

bipolar6_group = Group("Bipolar_6", bd_month6)
regular6_group = Group("Regular_6", regular_month6)

bipolar9_group = Group("Bipolar_9", bd_month9)
regular9_group = Group("Regular_9", regular_month9)

bipolar12_group = Group("Bipolar_12", bd_month12)
regular12_group = Group("Regular_12", regular_month12)

# bipolar15_group = Group("Bipolar_15", bd_month15)
# regular15_group = Group("Regular_15", regular_month15)

In [62]:
del bd_month2, regular_month2, bd_month3, regular_month3, bd_month6, regular_month6, bd_month9, regular_month9, bd_month12, regular_month12, bd_month15, regular_month15

In [50]:
recent_group5 = Group("Recent_5", recent_month4x)
recent_group4 = Group("Recent_4", recent_month4)
recent_group3 = Group("Recent_3", recent_month3)
recent_group2 = Group("Recent_2", recent_month2)

In [51]:
test_regular_group5 = Group("TRegular_5", test_regular_month4x)
test_regular_group4 = Group("TRegular_4", test_regular_month4)
test_regular_group3 = Group("TRegular_3", test_regular_month3)
test_regular_group2 = Group("TRegular_2", test_regular_month2)

In [52]:
def getCategories(group):
    '''
    Input  : the group (Class) of user
    Output : Dictionary of feature name and feature's group pairs

    e.g.
    'tweets_rate': 'GBSocial'
    'unique_mentions': 'GBSocial'
    '''
    name2category = {}
    names = ["Emotions", "Polarity", "AgeGender", "LIWC",
             "LongSocial", "lateSocial", "GBSocial","Phonology"]
    methods = [getGroupEmotions, getPolarity, getAgeGender, getLIWC_group, 
               getSocialFeature_group,  getNoLongSocialFeature_group, getGBSocialFeature_group,getPhonology_group]
    for i, method in enumerate(methods):
        if method == getLIWC_group:
            feature = {"LIWC_"+key: value for key, value in method(group.getGroup()).items()}
        else:
            feature = method(group.getGroup())
        for key in feature:
            name2category[key] = names[i]
    return name2category

def getAllFeature(group, tail_k = "all"):
    feature_set = {}
    methods = [getGroupEmotions, getPolarity, getAgeGender, getLIWC_group, 
               getSocialFeature_group,  getNoLongSocialFeature_group, getGBSocialFeature_group, getPhonology_group]
    for method in methods:
        if method == getLIWC_group:
            LIWC_feature_set = {"LIWC_"+key: value for key, value in method(group.getGroup(tail_k)).items()}
            feature_set.update(LIWC_feature_set)
        else:
            feature_set.update(method(group.getGroup()))
    return feature_set

## Classifier

### The TF-IDF models are trained in the following class

In [115]:
banwords = [u'mania', u'meds', u'mental illness', u'bipolardisorder', u'disorder', u'bipolarblogger', u'psych', u'health', u'bipolarus', u'ptsd', u'coping', u'bpd', u'treatment', u'natasha_tracy', u'help', u'hypomania', u'energy', u'illness', u'mental', u'insomnia', u'bipolar disorder', u'triggered', u'med', u'pill', u'dr', u'psychcentral', u'mentalillness', u'lamictal', u'anxiety', u'mentalhealth', u'guilty', u'supportive', u'having hard', u'disorder', u'hubby', u'induce', u'happy birthday', u'cause', u'know bipolar', u'triggering', u'hug', u'experience', u'severe', u'marriage', u'hoes', u'symptom', u'mentalillness bipolar', u'psychiatrist', u'harm', u'reading', u'self']

re_pattern = re.compile("\\b("+'|'.join(banwords)+")\\W*", re.I)
def RemoveBannedWords(toPrint):
#     print(type(toPrint))
    if type(toPrint) ==list:
        return [re_pattern.sub("", line) for line in toPrint]
    else:
        return re_pattern.sub("", toPrint)

toPrint = 'Hello, I have mental disorder, or mental illness I need help'

print RemoveBannedWords(toPrint)

Hello, I have or I need 


In [116]:
#A TF-IDF class to implement TF-IDF extraction and model training.
class TextFeatureGroups(object):
    def __init__(self, base, groups, model = "Tf-iDF"):
        self.base = base
        self.groups = groups
        self.name_to_index = {group.getName(): index for index, group in enumerate(groups)}
       
        base_texts = RemoveBannedWords(base.getTexts())
        self.text_models = []
        self.classifiers = []
        pairs_num = len(groups)/2
#         for i in range(pairs_num):
#             group_texts = group.getTexts()
#             total_texts = base_texts  + group_texts
#             text_model = TfidfVectorizer(stop_words="english", ngram_range = (1,2))
#             text_model.fit(total_texts)    
#             X = text_model.fit_transform(total_texts)  
#             Y = np.array([0] * base.getSize() + [1]*group.getSize(), dtype=int)
#             classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
#             classifier.fit(X,Y)
#             self.classifiers.append(classifier)
#             self.text_models.append(text_model)
        for group in groups:
            group_texts = RemoveBannedWords(group.getTexts())
            total_texts = base_texts  + group_texts
            text_model = TfidfVectorizer(stop_words="english", ngram_range = (1,2))
            text_model.fit(total_texts)    
            X = text_model.fit_transform(total_texts)  
            Y = np.array([0] * base.getSize() + [1]*group.getSize(), dtype=int)
            classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
            classifier.fit(X,Y)
            self.classifiers.append(classifier)
            self.text_models.append(text_model)
            
        self.groups_user_name = []
        for group in groups:
            group_user_name = []
            for timeSeries in group.getGroup():
                group_user_name.append(timeSeries['name'][0])
            self.groups_user_name.append(group_user_name)
        
    
    def getTopFeatures(self, name, k=50):
        index = self.name_to_index[name]
        text_model = self.text_models[index]
        classifier = self.classifiers[index]
        feature_indicies = np.argsort(classifier.feature_importances_)
        vector2word = text_model.get_feature_names()
        top_words = []
        for i in range(k):
            vector = feature_indicies[-i-1]
            word = vector2word[vector]
            top_words.append(word)
        return top_words

    def getGroup(self,name):
        index = self.name_to_index[name]
        return self.groups[index]
            
    def classify(self,name, group):
        index = self.name_to_index[name]
        classifier = self.classifiers[index]
        text_model = self.text_models[index]
        X = text_model.transform(group.getTexts())
        return classifier.predict(X) 
    
    def getPrecision(self,name, tail_k="all", classifier = "default", n_fold=10):
        index = self.name_to_index[name]
        group = self.groups[index]
        if classifier == "default":
            classifier = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
        #classifier = SVC(probability=True)
        #X = self.text_models[index].transform(self.base.getTexts(tail_k)+group.getTexts(tail_k))
        text_model = self.text_models[index]
        raw_X = self.base.group + group.group
        Y =  np.array([0] * self.base.getSize() + [1] * group.getSize())
        precisions = []
        
        complete_X = text_model.transform(self.base.getTexts()+group.getTexts())
        tailed_X =  text_model.transform(self.base.getTexts(tail_k)+group.getTexts(tail_k))
        
        sss = StratifiedShuffleSplit(Y, n_fold, test_size = 0.2, random_state=randint(0,65536) )

        for train_index, test_index in sss:
            
            X_train, X_test = complete_X[train_index], tailed_X[test_index]
            Y_train, Y_test = Y[train_index], Y[test_index]
            classifier.fit(X_train, Y_train)
            score = classifier.score(X_test,Y_test)
            precisions.append(score)

        return np.mean(precisions)
        
    
    def getLabelsScores(self, name, classifier, n_fold, consider_time = "short"):
        index = self.name_to_index[name]
        group = self.groups[index]

        SCORES = np.array([])
        LABELS = np.array([])
        
#         Based may change by situation
        if consider_time == "short":
            X = self.text_models[index].transform(self.base.getTexts()+group.getTexts())
            Y =  np.array([0] * self.base.getSize() + [1] * group.getSize())  
        elif consider_time == "long":
            X = self.text_models[index].transform(self.groups[0].getTexts()+group.getTexts())
            Y =  np.array([0] * self.groups[0].getSize() + [1] * group.getSize())  
        else:
            X = self.text_models[index].transform(self.groups[self.name_to_index["Regular_" + str(consider_time)]].getTexts()+group.getTexts())
            Y =  np.array([0] * self.groups[self.name_to_index["Regular_" + str(consider_time)]].getSize() + [1] * group.getSize())  

        sss = StratifiedShuffleSplit(Y, n_fold, test_size = 0.1, random_state=randint(0,65536))

        for train_index, test_index in sss:
            X_train, X_test = X[train_index], X[test_index]
            Y_train, Y_test = Y[train_index], Y[test_index]

            classifier.fit(X_train, Y_train)
            score = classifier.predict_proba(X_test)[:,1]
            SCORES = np.concatenate((SCORES, score))
            LABELS = np.concatenate((LABELS, Y_test))

        return SCORES, LABELS, (X_train, X_test,Y_train, Y_test)
        
    def renderPrecisionRecall(self, colors=['r','g','b',"y","c","m","#f4b642","#777777"], n_fold = 10):
        classifier = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
        fig, ax = plt.subplots()
        ax.spines['bottom'].set_color('white')
        ax.spines['top'].set_color('white') 
        ax.spines['right'].set_color('white')
        ax.spines['left'].set_color('white')
        ax.tick_params(axis='x', colors='white')
        ax.tick_params(axis='y', colors='white')
        ax.title.set_color('white')
        ax.yaxis.label.set_color('white')
        ax.xaxis.label.set_color('white')
        plt.xlim([0.0, 1.0])
        plt.ylim([0.0, 1.05])
        plt.xlabel('Recall')
        plt.ylabel('Precision')
        plt.title('Precision Recall Curve')

        for g, group in enumerate(self.groups):
            SCORES, LABELS,(X_train, X_test,Y_train, Y_test) = self.getLabelsScores(group.getName(), classifier ,n_fold)

            precision, recall, _ = precision_recall_curve(LABELS, SCORES, pos_label=1)
            average_precision = average_precision_score(LABELS, SCORES)

            positive_train = np.count_nonzero(Y_train)
            positive_test = np.count_nonzero(Y_test)
            normal_train = Y_train.shape[0] - positive_train
            normal_test = Y_test.shape[0] - positive_test

            print("{} Normal and {} {} in Training Data".format(normal_train,positive_train,group.getName()))
            print("{} Normal and {} {} in Test Data\n".format(normal_test,positive_test,group.getName()))
            plt.plot(recall, precision, label=group.getName() , color=colors[g],linewidth=3)

        plt.legend(loc="lower right")
        plt.show()
        
    def getGroupUserName(self,group_num = 0):
        return self.groups_user_name[group_num]


In [117]:
# Build the TF-IDF class
tfidf_groups = TextFeatureGroups(regular2_group, [regular2_group, regular3_group, regular6_group, regular9_group, regular12_group,  
                                                  bipolar2_group, bipolar3_group, bipolar6_group, bipolar9_group, bipolar12_group])

# Extract Top 10 keywords by TF-IDF model for Bipolar and BPD
print(tfidf_groups.getTopFeatures("Bipolar_2"))
print("\n\n")
print(tfidf_groups.getTopFeatures("Bipolar_3"))
print("\n\n")
print(tfidf_groups.getTopFeatures("Bipolar_6"))
print("\n\n")
print(tfidf_groups.getTopFeatures("Bipolar_9"))
print("\n\n")
print(tfidf_groups.getTopFeatures("Bipolar_12"))
print("\n\n")
# print(tfidf_groups.getTopFeatures("Bipolar_15"))

[u'head', u'mean', u'im', u'depression', u'sucks', u'makeup', u'met', u'weed', u'really need', u'inside', u'suicide', u'green', u'asking', u'song', u'thing', u'dead', u'killed', u'means', u'bitch', u'loved', u'said', u'telling', u'better', u'type', u'best friend', u'year', u'dick', u'angel', u'just realized', u'bipolar', u'facebook', u'bieber', u'im sorry', u'refuse', u'christmas', u'today diagnosed', u'lazy', u'really', u'nerd', u'suicidal', u'thinks', u'diagnosed', u'fuck', u'moment', u'like', u'allow', u'awkward', u'rude', u'little', u'says']



[u'eat', u'diagnosed bipolar', u'best friend', u'crying', u'sleeping', u'told', u'eam', u'blood', u'tweets', u'constantly', u'feel like', u'adult', u'aren', u'cute', u'eyes', u'okay', u'kept', u'just say', u'pain', u'ago', u'lazy', u'loved', u'diagnosed', u'say', u'think', u'listen', u'millions', u'reasons', u'fucking hate', u'twitter', u'people just', u'just said', u'gets', u'threw', u'peace', u'nasty', u'shitty', u'wake', u'inside', u'murd

In [118]:
tfidf_groups_ = TextFeatureGroups(regular2_group, [regular2_group, regular3_group, regular6_group, regular9_group, regular12_group, 
                                                  bd2_group, bd3_group, bd6_group, bd9_group, bd12_group])


In [119]:
print(tfidf_groups_.getTopFeatures("Bd_2"))
print("\n\n")
print(tfidf_groups_.getTopFeatures("Bd_3"))
print("\n\n")
print(tfidf_groups_.getTopFeatures("Bd_6"))
print("\n\n")
print(tfidf_groups_.getTopFeatures("Bd_9"))
print("\n\n")
print(tfidf_groups_.getTopFeatures("Bd_12"))

[u'felt', u'spell', u'ill', u'born', u'past', u'smile', u'yeah know', u'loud', u'stupid', u'inking', u'people want', u'turned', u'kiss', u'ear', u'stress', u'hands', u'21', u'fat', u'teach', u'sex', u'relate', u'saying', u'followers', u'bunch', u'end', u'14', u'knew', u'child', u'sound', u'exist', u'just know', u'wrong', u'hi', u'wondering', u'weeks', u'hello', u'bones', u'hoping', u'green', u'needs', u'happy', u'weed', u'gonna make', u'losing', u'blow', u'beauty', u'legs', u'did', u'bet', u'december']



[u'lie', u'fat', u'annoying', u'sad', u'earth', u'pounds', u'church', u'really need', u'oh', u'bright', u'best day', u'meant', u'learned', u'boyfriend', u'throw', u'twice', u'window', u'extra', u'tumblr', u'lot', u'finally got', u'just got', u'far', u'upset', u'idea', u'deleted', u'air', u'online', u'nope', u'quote', u'present', u'boy', u'ove', u'emotional', u'okay', u'artist', u'thanksgiving', u'crush', u'heart', u'fault', u'funny', u'moments', u'really like', u'jealous', u'skin', u'

In [ ]:
bd2_word_set =  [u'asleep', u'halloween', u'longer', u'lucky', u'nah', u'don let', u'scream', u'air', u'hanging', u'jump', u'rock', u'control', u'broken', u'hurts', u'month', u'tattoo', u'anymore', u'keyboard', u'fly', u'surprised', u'admit', u'care', u'word', u'talked', u'screen', u'known', u'kill', u'hand', u'months', u'profile', u'fact', u'bet', u'looking', u'creepy', u'tweeting', u'don care', u'lot', u'changed', u'state', u'omg', u'burning', u'watched', u'pride', u'throw', u'therapy', u'singing', u'know don', u'childhood', u'teeth', u'weeks']
bd3_word_set =  [u'trust', u'2013', u'feels', u'keeps', u'tweeting', u'scream', u'valentine', u'twice', u'asleep', u'cream', u'tries', u'best friend', u'tweets', u'just like', u'calm', u'alcohol', u'shoot', u'pink', u'ones', u'taken', u'gone', u'reading', u'alright', u'followers', u'mama', u'uncle', u'spend', u'hates', u'difference', u'fast', u'need help', u'feel good', u'makes sense', u'complete', u'high school', u'12', u'prayers', u'midnight', u'chose', u'camera', u'bell', u'cousin', u'expect', u'make feel', u'mirror', u'think like', u'light', u'don remember', u'knows', u'needed']
bd6_word_set =  [u'laugh', u'liked', u'hands', u'posted', u'laughing', u'grow', u'dear', u'french', u'anxiety', u'regret', u'young', u'thoughts', u'hair', u'tree', u'remind', u'didn think', u'eat', u'tweets', u'stupid', u'need help', u'told', u'alive', u'dream', u'skin', u'know ve', u'died', u'earth', u'characters', u'damn', u'profile', u'tear', u'worst', u'simple', u'words', u'paid', u'right just', u'pregnant', u'lonely', u'mini', u'hold', u'pure', u'like', u'reason', u'bright', u'women', u'kills', u'bar', u'joke', u'hand', u'easy']
bd9_word_set =  [u'mini', u'bipolar', u'freak', u'joke', u'lived', u'cat', u'felt', u'broken', u'test', u'breath', u'boyfriend', u'hugs', u'feelings', u'wear', u'love people', u'october', u'meet', u'yes love', u'changed', u'voice', u'lay', u'song', u'worth', u'evil', u'scared', u'saved', u'guess', u'bones', u'people love', u'computer', u'dancing', u'id', u'like shit', u'huh', u'justin bieber', u'perfectly', u'really love', u'went', u'hate people', u'opinion', u'car', u'lyrics', u'dogs', u'ice', u'meds', u'wondering', u'killer', u'dead', u'bed', u'just want']
bd12_word_set = [u'weeks', u'pretend', u'fat', u'sleeping', u'stone', u'just say', u'example', u'lives', u'tree', u'twice', u'sitting', u'apart', u'express', u'moved', u'don really', u'save', u'type', u'wearing', u'ruined', u'feels', u'sense', u'knowing', u'years', u'realized', u'hanging', u'point', u'wondering', u'lucky', u'suddenly', u'know feel', u'afraid', u'princess', u'funniest', u'clothes', u'taking', u'true love', u'afford', u'woke', u'oh wait', u'half', u'liked', u'opposite', u'true', u'surrounded', u'act', u'lyrics', u'didn want', u'addiction', u'reminds', u'hand']
word_set_list = [bd2_word_set, bd3_word_set, bd6_word_set, bd9_word_set, bd12_word_set]

In [60]:
for i, aset in enumerate(word_set_list):
    print
    tempset = aset
    for j, bset in enumerate(word_set_list):
#         print(list(aset & bset))
        if i==j:continue
        tempset = [word for word in tempset if word not in bset]
    print(list(tempset))


[u'halloween', u'longer', u'nah', u'don let', u'air', u'jump', u'rock', u'control', u'hurts', u'month', u'tattoo', u'anymore', u'keyboard', u'fly', u'surprised', u'admit', u'care', u'word', u'talked', u'screen', u'known', u'kill', u'months', u'fact', u'bet', u'looking', u'creepy', u'don care', u'lot', u'state', u'omg', u'burning', u'watched', u'pride', u'throw', u'therapy', u'singing', u'know don', u'childhood', u'teeth']

[u'trust', u'2013', u'keeps', u'valentine', u'cream', u'tries', u'best friend', u'just like', u'calm', u'alcohol', u'shoot', u'pink', u'ones', u'taken', u'gone', u'reading', u'alright', u'followers', u'mama', u'uncle', u'spend', u'hates', u'difference', u'fast', u'feel good', u'makes sense', u'complete', u'high school', u'12', u'prayers', u'midnight', u'chose', u'camera', u'bell', u'cousin', u'expect', u'make feel', u'mirror', u'think like', u'light', u'don remember', u'knows', u'needed']

[u'laugh', u'hands', u'posted', u'laughing', u'grow', u'dear', u'french', u'a

In [57]:
class POLFeaturerGroups(object):
    
    @staticmethod
    def transform(self, ):
        features_dict = getAllFeature(group)
        
    
    def __init__(self, base, groups):
        feature2categories = getCategories(base)
        self.groups = groups
        self.base = base
        self.categories = set(feature2categories.values())
        self.name_to_index = {group.getName(): index for index, group in enumerate(groups)}
        self.base_name = base.getName()
        self.index2feature = []
        base_feature_dict = getAllFeature(base)
        self.base_feature = np.zeros((base.getSize(),len(base_feature_dict)), dtype = float)
#         
        for name, values in base_feature_dict.items():
            cursor = len(self.index2feature)
            self.base_feature[:,cursor] = values
            category = feature2categories[name]
            self.index2feature.append((name, category))
        
        self.features = [self.group2feature(group) for group in groups]
#         user_name
        self.groups_user_name = []
        for group in groups:
            group_user_name = []
            for timeSeries in group.getGroup():
                group_user_name.append(timeSeries['name'][0])
            self.groups_user_name.append(group_user_name)
        
        self.base_user_name = []
        for timeSeries in base.getGroup():
            self.base_user_name.append(timeSeries['name'][0])
            
    def addgroup(self, group):
        group_user_name = []
        for timeSeries in group.getGroup():
            group_user_name.append(timeSeries['name'][0])
        self.groups_user_name.append(group_user_name)
        
        self.name_to_index = {group.getName(): len(name_to_index)}
        print(group.getName() + ' is added!')
        return True
        
    def group2feature(self, group, tail_k="all", selection = "all"):
        features_dict = getAllFeature(group, tail_k)
        feature = np.zeros((group.getSize(),len(self.index2feature)),dtype=float)
        for cursor, (name,category) in enumerate(self.index2feature):
            value = features_dict[name]
            feature[:,cursor] = value
        if selection == "all":
            return feature
        else:
            return feature[:,selection]   

    def getPrecision(self,name,selection="all",tail_k="all",n_fold=10,classifier = "forest"):
        complete_X, Y = self.getLabeledData(name, selection)
        index = self.name_to_index[name]
        group = self.groups[index]
        tailed_X = preprocessing.scale(self.group2feature(self.base + group, tail_k=tail_k, selection = selection))
        complete_X = preprocessing.scale(complete_X)
        
        tailed_X[np.isinf(tailed_X)] = 0
        tailed_X[np.isnan(tailed_X)] = 0
        
        precisions = []
        if classifier == "forest":
            classifier = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
  
        sss = StratifiedShuffleSplit(Y, n_fold, test_size = 0.1, random_state=randint(0,65536) )

        for train_index, test_index in sss:
            X_train, X_test = complete_X[train_index], tailed_X[test_index]
            Y_train, Y_test = Y[train_index], Y[test_index]
            imputer = Imputer()
            classifier.fit(X_train, Y_train)
            score = classifier.score(X_test,Y_test)
            precisions.append(score)
            
        return np.mean(precisions)
            
    def getLabeledData(self,name, selection = "all", consider_time = "short"):
#         print('Get Label Data - Name: {}, Consider Time: {}, Selection: {}'.format(name, consider_time, selection))
        if selection is "all":
            selection = xrange(len(self.index2feature))
            
        if consider_time == "short":        
            base_feature = self.base_feature[:,selection]
            base_length = base_feature.shape[0]
            index = self.name_to_index[name]
            feature = self.features[index][:,selection]
            X = np.zeros((base_length  + feature.shape[0],len(selection)),dtype=float)
            X[0:base_length ,:] = base_feature
            X[base_length:,:] = feature
    #         Y = np.array([(0,-1)]*base_length + [(1,i) for i,_ in enumerate(self.getGroupUserName())])
            Y = np.array([(0,i) for i,_ in enumerate(self.getBaseUserName())] + [(1,i) for i,_ in enumerate(self.getGroupUserName(1))])
            return X, Y
        elif consider_time == "long":
            base_index = self.name_to_index["Regular_15"]
            base_feature = self.features[base_index][:,selection]
            base_length = base_feature.shape[0]
            index = self.name_to_index[name]
            feature = self.features[index][:,selection]

            X = np.zeros((base_length  + feature.shape[0],len(selection)),dtype=float)
            X[0:base_length ,:] = base_feature
            X[base_length:,:] = feature
            Y = np.array([(0,i) for i,_ in enumerate(self.getGroupUserName(base_index))] + [(1,i) for i,_ in enumerate(self.getGroupUserName(index))])
            return X, Y
        else:
            base_index = self.name_to_index["Regular_"+str(consider_time)]
            base_feature = self.features[base_index][:,selection]
            base_length = base_feature.shape[0]
            index = self.name_to_index[name]
            feature = self.features[index][:,selection]

            X = np.zeros((base_length  + feature.shape[0],len(selection)),dtype=float)
            X[0:base_length ,:] = base_feature
            X[base_length:,:] = feature
#             Y = np.array([(0,name) for i,name in enumerate(self.getGroupUserName(base_index))] + [(1,name) for i,name in enumerate(self.getGroupUserName(index))], dtype = [("label", np.int32), ("name", '|S21')])
            Y = np.array([(0,i) for i,name in enumerate(self.getGroupUserName(base_index))] + [(1,i) for i,name in enumerate(self.getGroupUserName(index))])
            return X, Y 

    def getLabeledDataWithName(self,name, selection = "all", consider_time = 2):
#         print('Get Label Data - Name: {}, Consider Time: {}, Selection: {}'.format(name, consider_time, selection))
        if selection is "all":
            selection = xrange(len(self.index2feature))
            

        base_index = self.name_to_index["Regular_"+str(consider_time)]
        base_feature = self.features[base_index][:,selection]
        base_length = base_feature.shape[0]
        index = self.name_to_index[name]
        feature = self.features[index][:,selection]

        X = np.zeros((base_length  + feature.shape[0],len(selection)),dtype=float)
        X[0:base_length ,:] = base_feature
        X[base_length:,:] = feature
        Y = np.array([(0,name) for i,name in enumerate(self.getGroupUserName(base_index))] + [(1,name) for i,name in enumerate(self.getGroupUserName(index))], dtype = [("label", np.int32), ("name", '|S21')])
    
        return X, Y 

    def getFeatureImportance_all(self,name):
        X, Y = self.getLabeledData(name)
        classifier = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
        classifier.fit(X,Y)
        features_indicies = np.argsort(classifier.feature_importances_)
        feature_names = [self.index2feature[i] for i in features_indicies ]
        return feature_names[::-1]
    
    def getFeature(self, name, selection="all"):
        if selection is "all":
            selection = list(range(len(self.index2feature)))
        index = self.name_to_index[name]
        feature =  self.features[index]
        return feature[:, selection]
    
    def classify(self,name, target_name, selection="all"):
        X, Y = self.getLabeledData(name, selection)
        classifier = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
        classifier.fit(X,Y)
        test_x = self.getFeature(target_name,selection)
        return classifier.predict(test_x)
       
    def getLabelsScores(self, name, classifier, n_fold, selection, consider_time = "short"):
        SCORES = np.array([])
        LABELS = np.zeros(shape=(0,2))
        
        X, Y = self.getLabeledData(name, selection, consider_time)
        sss = StratifiedShuffleSplit(Y[:,0], n_fold, test_size = 0.1, random_state=randint(0,65536) )

        for train_index, test_index in sss:
            X_train, X_test           = X[train_index], X[test_index]
            Y_train, Y_test           = Y[train_index][:,0], Y[test_index][:,0]
            Y_train_name, Y_test_name = Y[train_index][:,1], Y[test_index][:,1]

            classifier.fit(X_train, Y_train)
            score = classifier.predict_proba(X_test)[:,1]
            SCORES = np.concatenate((SCORES, score))
            LABELS = np.concatenate((LABELS, Y[test_index]))
        return SCORES, LABELS, (X_train, X_test,Y_train, Y_test, Y_train_name, Y_test_name)
    
    def renderPrecisionRecall_all(self, name, colors=['r','g','b',"y","c","m","#f4b642","#777777"], n_fold = 100, consider_time = "short"):
        classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
        fig, ax = plt.subplots()
        ax.spines['bottom'].set_color('white')
        ax.spines['top'].set_color('white') 
        ax.spines['right'].set_color('white')
        ax.spines['left'].set_color('white')
        ax.tick_params(axis='x')
        ax.tick_params(axis='y')
        ax.title.set_color('white')
        plt.xlim([0.0, 1.0])
        plt.ylim([0.0, 1.05])
        plt.xlabel('Recall')
        plt.ylabel('Precision')
        plt.title('Precision Recall Curve: {}'.format(name))
        
        categories = list(self.categories) + ["All"]
        graph_data = [] # For plotly
        for g,category in enumerate(categories):
            if category == "All":
                selection = range(len(self.index2feature))
            else:
                selection = [i for i, (feature_name, feature_category) in enumerate(self.index2feature) if category == feature_category]
            
            SCORES, LABELS, (X_train, X_test,Y_train, Y_test, Y_train_name, Y_test_name) = self.getLabelsScores(name, classifier,n_fold, selection, consider_time)
            precision, recall, _ = precision_recall_curve(LABELS[:,0], SCORES, pos_label=1)
            average_precision = average_precision_score(LABELS[:,0], SCORES)
            print("Average Percision of {} : {}".format(category, average_precision))
            positive_train = np.count_nonzero(Y_train)
            positive_test = np.count_nonzero(Y_test)
            normal_train = Y_train.shape[0] - positive_train
            normal_test = Y_test.shape[0] - positive_test
           
            graph_data.append(Scatter( x=recall, y=precision, name=category))

#             plt.plot(recall, precision, label=category , color=colors[g],linewidth=2)
            
        print("{} Normal and {} {} in Training Data".format(normal_train,positive_train,name))
        print("{} Normal and {} {} in Test Data\n".format(normal_test,positive_test,name))
        
        iplot(graph_data)
#         plt.legend(loc="lower right")
#         plt.show()

    def getSeperateScores(self, name, classifier, n_fold, selection):
        SCORES = np.array([])
        LABELS = np.array([])

        X, Y = self.getLabeledData(name, selection)

        sss = StratifiedShuffleSplit(Y, n_fold, test_size = 0.1, random_state=randint(0,65536) )

        for train_index, test_index in sss:

            X_train, X_test = X[train_index], X[test_index]
            Y_train, Y_test = Y[train_index], Y[test_index]

            classifier.fit(X_train, Y_train)
            score = classifier.predict_proba(X_test)[:,1]
            SCORES = np.concatenate((SCORES, score))
            LABELS = np.concatenate((LABELS, Y_test))

        return SCORES, LABELS, (X_train, X_test,Y_train, Y_test)
    
    def getGroupUserName(self,group_num = 0):
        return self.groups_user_name[group_num]
    
    def getIndex2Feature(self):
        return self.index2feature
    
    def getBaseUserName(self):
        return self.base_user_name
    
    def getName2Index(self):
        return self.name_to_index

In [60]:
# pol_groups = POLFeaturerGroups(regular_group, [long_regular_group, bipolar_group, long_bipolar_group])

In [82]:
pol_groups = POLFeaturerGroups(regular2_group, [regular2_group, regular3_group, regular6_group, regular9_group, regular12_group,
                                                  bipolar2_group, bipolar3_group, bipolar6_group, bipolar9_group, bipolar12_group])

No found in long_term 327166736
No found in long_term 424640736
No found in long_term 46838244
No found in long_term 1937246714
No found in long_term 351640670
No found in long_term 2963451509
No found in long_term 2905542613
No found in long_term 226849732
No found in long_term 289918462
No found in long_term 3046722590
No found in long_term 2361039959
No found in long_term 477388137
No found in long_term 50771326
No found in long_term 2273179067
No found in long_term 2316052422
No found in long_term 2560010215
No found in long_term 341644925
No found in long_term 423932461
No found in long_term 454023220
No found in long_term 1012152937
No found in long_term 327166736
No found in long_term 424640736
No found in long_term 46838244
No found in long_term 1937246714
No found in long_term 351640670
No found in long_term 2963451509
No found in long_term 2905542613
No found in long_term 226849732
No found in long_term 289918462
No found in long_term 3046722590
No found in long_term 23610399

In [83]:
pol_groups_ = POLFeaturerGroups(regular2_group, [regular2_group, regular3_group, regular6_group, regular9_group, regular12_group, 
                                                  bd2_group, bd3_group, bd6_group, bd9_group, bd12_group])


No found in long_term 327166736
No found in long_term 424640736
No found in long_term 46838244
No found in long_term 1937246714
No found in long_term 351640670
No found in long_term 2963451509
No found in long_term 2905542613
No found in long_term 226849732
No found in long_term 289918462
No found in long_term 3046722590
No found in long_term 2361039959
No found in long_term 477388137
No found in long_term 50771326
No found in long_term 2273179067
No found in long_term 2316052422
No found in long_term 2560010215
No found in long_term 341644925
No found in long_term 423932461
No found in long_term 454023220
No found in long_term 1012152937
No found in long_term 327166736
No found in long_term 424640736
No found in long_term 46838244
No found in long_term 1937246714
No found in long_term 351640670
No found in long_term 2963451509
No found in long_term 2905542613
No found in long_term 226849732
No found in long_term 289918462
No found in long_term 3046722590
No found in long_term 23610399

In [84]:
#Compare the performance of each Pattern of Life components and LIWC
pol_groups.renderPrecisionRecall_all("Bipolar_2", n_fold=10, consider_time = 2)
pol_groups.renderPrecisionRecall_all("Bipolar_3", n_fold=10, consider_time = 3)
pol_groups.renderPrecisionRecall_all("Bipolar_6", n_fold=10, consider_time = 6)
pol_groups.renderPrecisionRecall_all("Bipolar_9", n_fold=10, consider_time = 9)
pol_groups.renderPrecisionRecall_all("Bipolar_12", n_fold=10, consider_time = 12)
# pol_groups.renderPrecisionRecall_all("Bipolar_15", n_fold=10, consider_time = 15)

Average Percision of Polarity : 0.760067384827
Average Percision of GBSocial : 0.772201467216
Average Percision of AgeGender : 0.389504875665
Average Percision of Phonology : 0.747777638913
Average Percision of Emotions : 0.731610648738
Average Percision of LIWC : 0.379867665883
Average Percision of LongSocial : 0.572838396081
Average Percision of lateSocial : 0.696639633411
Average Percision of All : 0.867006346342
234 Normal and 119 Bipolar_2 in Training Data
26 Normal and 14 Bipolar_2 in Test Data



Average Percision of Polarity : 0.827074529685
Average Percision of GBSocial : 0.707227993412
Average Percision of AgeGender : 0.503757094903
Average Percision of Phonology : 0.76919859229
Average Percision of Emotions : 0.794163745493
Average Percision of LIWC : 0.458543393486
Average Percision of LongSocial : 0.57883924059
Average Percision of lateSocial : 0.789335391513
Average Percision of All : 0.917654686786
231 Normal and 121 Bipolar_3 in Training Data
26 Normal and 14 Bipolar_3 in Test Data



Average Percision of Polarity : 0.781344547106
Average Percision of GBSocial : 0.75035956795
Average Percision of AgeGender : 0.42003865567
Average Percision of Phonology : 0.833850090818
Average Percision of Emotions : 0.777571855457
Average Percision of LIWC : 0.401160968429
Average Percision of LongSocial : 0.589312818192
Average Percision of lateSocial : 0.760297158088
Average Percision of All : 0.897261591274
240 Normal and 111 Bipolar_6 in Training Data
27 Normal and 13 Bipolar_6 in Test Data



Average Percision of Polarity : 0.76052647376
Average Percision of GBSocial : 0.788553976694
Average Percision of AgeGender : 0.408074265921
Average Percision of Phonology : 0.794004501533
Average Percision of Emotions : 0.741465580383
Average Percision of LIWC : 0.39299783781
Average Percision of LongSocial : 0.551716068254
Average Percision of lateSocial : 0.715436681659
Average Percision of All : 0.882837164577
260 Normal and 105 Bipolar_9 in Training Data
29 Normal and 12 Bipolar_9 in Test Data



Average Percision of Polarity : 0.735770430304
Average Percision of GBSocial : 0.753514847511
Average Percision of AgeGender : 0.440877264437
Average Percision of Phonology : 0.760519795511
Average Percision of Emotions : 0.657052139134
Average Percision of LIWC : 0.348371282565
Average Percision of LongSocial : 0.549178685921
Average Percision of lateSocial : 0.756810795699
Average Percision of All : 0.872817945736
265 Normal and 100 Bipolar_12 in Training Data
30 Normal and 11 Bipolar_12 in Test Data



In [151]:
pol_groups_.renderPrecisionRecall_all("Bd_2", n_fold=50, consider_time = 2)
pol_groups_.renderPrecisionRecall_all("Bd_3", n_fold=50, consider_time = 3)
pol_groups_.renderPrecisionRecall_all("Bd_6", n_fold=50, consider_time = 6)
pol_groups_.renderPrecisionRecall_all("Bd_9", n_fold=50, consider_time = 9)
pol_groups_.renderPrecisionRecall_all("Bd_12", n_fold=50, consider_time = 12)

Average Percision of Polarity : 0.889071014122
Average Percision of GBSocial : 0.945758330797
Average Percision of AgeGender : 0.475882354852
Average Percision of Phonology : 0.900371160106
Average Percision of Emotions : 0.891854826641
Average Percision of LIWC : 0.431133413908
Average Percision of LongSocial : 0.588567816559
Average Percision of lateSocial : 0.654034704183
Average Percision of All : 0.976304034154
234 Normal and 133 Bd_2 in Training Data
26 Normal and 15 Bd_2 in Test Data



Average Percision of Polarity : 0.874044110834
Average Percision of GBSocial : 0.921664669908
Average Percision of AgeGender : 0.496472297874
Average Percision of Phonology : 0.902501610583
Average Percision of Emotions : 0.899060204939
Average Percision of LIWC : 0.412317108355
Average Percision of LongSocial : 0.576058890434
Average Percision of lateSocial : 0.667771349517
Average Percision of All : 0.978692068041
231 Normal and 125 Bd_3 in Training Data
26 Normal and 14 Bd_3 in Test Data



Average Percision of Polarity : 0.824811782845
Average Percision of GBSocial : 0.823885145201
Average Percision of AgeGender : 0.401957502587
Average Percision of Phonology : 0.839965601581
Average Percision of Emotions : 0.907726352978
Average Percision of LIWC : 0.388644117935
Average Percision of LongSocial : 0.546982837062
Average Percision of lateSocial : 0.619685840473
Average Percision of All : 0.952656376876
240 Normal and 120 Bd_6 in Training Data
27 Normal and 13 Bd_6 in Test Data



Average Percision of Polarity : 0.836353297489
Average Percision of GBSocial : 0.837860674157
Average Percision of AgeGender : 0.390959642264
Average Percision of Phonology : 0.819309343217
Average Percision of Emotions : 0.91686049893
Average Percision of LIWC : 0.429204003517
Average Percision of LongSocial : 0.559906586393
Average Percision of lateSocial : 0.603012788258
Average Percision of All : 0.971249964903
260 Normal and 115 Bd_9 in Training Data
29 Normal and 13 Bd_9 in Test Data



Average Percision of Polarity : 0.797864542397
Average Percision of GBSocial : 0.799558456554
Average Percision of AgeGender : 0.407126402794
Average Percision of Phonology : 0.773995117502
Average Percision of Emotions : 0.884117935681
Average Percision of LIWC : 0.406881009992
Average Percision of LongSocial : 0.53542855162
Average Percision of lateSocial : 0.666369090205
Average Percision of All : 0.964642642217
265 Normal and 106 Bd_12 in Training Data
30 Normal and 12 Bd_12 in Test Data



# Precission Recall Chart on 10-fold cross-validation

In [141]:
for i in range(len(index2feature)):
    name,category =  index2feature[i]
    if category == 'Polarity':
        print(i)
        print(name)

5
flips
16
positive_ratio
23
negative_ratio
26
positive_combos
73
negative_combos


In [86]:
index2feature = pol_groups_.index2feature

def getSelection(excluded_categories=[], excluded_index=[]):
    selection = []
    for i in range(len(index2feature)):
        name,category =  index2feature[i]
        if any(category == x for x in excluded_categories):
            #removed_features.append(name)
            pass
        elif any(name == x for x in excluded_index):
            #removed_features.append(name)
            pass

        else:                   
            selection.append(i)
    return selection


#ROC chart of three models:
# def renderROC(scores, labels,disorder ,names, linestyle=['solid','dashed','dotted','solid','dashdot','--','dashed','dotted']):
def renderROC(scores, labels,disorder ,names,
              linestyle=['solid','solid','solid','solid','dashdot','dashdot','dashdot','dashdot'],
              colors = None,
              linewidth = 3,
              transparent = 1):
    
#     fig, ax = plt.subplots()
    print("Under curve area")
    for i,(score, label) in enumerate(zip(scores, labels)):
        fpr, tpr, _ = roc_curve(label,score, pos_label=1)
        roc_auc = auc(fpr, tpr)
        
#         if colors:
#             plt.plot(fpr, tpr, label=names[i], ls=linestyle[i],linewidth=linewidth, color=colors[i], alpha=transparent)
#         else:
#             plt.plot(fpr, tpr, label=names[i], ls=linestyle[i],linewidth=linewidth, alpha=transparent)

        print("\t{:15} : {}".format(names[i],roc_auc))
        graph_data.append(Scatter( x=fpr, y=tpr, name=names[i]))
        
#     plt.plot([0, 1], [0, 1], 'k--')
#     plt.xlim([0.0, 1.0])
#     plt.ylim([0.0, 1.05])
#     plt.xlabel('False Positive Rate')
#     plt.ylabel('True Positive Rate')
#     plt.title('{} ROC chart'.format(disorder))
#     plt.legend(loc="lower right")

#     plt.show()
    iplot(graph_data)

# , linestyle=['solid','dashed','dotted','solid','dashdot','--','dashed','dotted'], colors = ['r','g','b',"y","c","m","#f4b642","#777777"]
# def renderPRC(scores, labels, disorder ,names, linestyle=['solid','dashed','dotted','solid','dashdot','--','dashed','dotted'], colors = None):
def renderPRC(scores, labels, disorder ,names,
              linestyle=['solid','solid','solid','solid','dashdot','dashdot','dashdot','dashdot'],
              colors = None,
              linewidth = 3,
              transparent = 1):
    
#     fig, ax = plt.subplots()
    print("Average Precision")
    graph_data = []
    for i,(score, label) in enumerate(zip(scores, labels)):        
        precision, recall, _ = precision_recall_curve(label, score, pos_label=1)
        average_precision = average_precision_score(label, score)
        
#         if colors:
#             plt.plot(recall, precision, label=names[i], ls=linestyle[i],linewidth=linewidth, color=colors[i], alpha=transparent)
#         else:
#             plt.plot(recall, precision, label=names[i], ls=linestyle[i],linewidth=linewidth, alpha=transparent)
            
        print("\t{:15} : {}".format(names[i],average_precision))
        graph_data.append(Scatter( x=recall, y=precision, name=names[i]))

#     plt.xlim([0.0, 1.0])
#     plt.ylim([0.0, 1.05])
#     plt.xlabel('False Positive Rate')
#     plt.ylabel('True Positive Rate')
#     plt.title('{} Precision Recall Chart'.format(disorder))
#     plt.legend(loc="lower right")
#     plt.show()
    iplot(graph_data)
   

In [192]:
GBPOL_selection = getSelection(excluded_categories=["LIWC", "lateSocial", "LongSocial","Phonology"])
latePOL_selection = getSelection(excluded_categories=["LIWC", "LongSocial","Phonology"])
LongPOL_selection = getSelection(excluded_categories=["LIWC", "lateSocial","Phonology"])
LLPOL_selection = getSelection(excluded_categories=["LIWC","Phonology"])
LIWC_selection = getSelection(excluded_categories=["AgeGender", "Social", "Polarity", "Emotions","GBSocial", "lateSocial", "LongSocial","Phonology"])
Phon_selection = getSelection(excluded_categories=["LIWC","AgeGender", "Social", "Polarity", "Emotions","GBSocial", "lateSocial", "LongSocial"])
PhonPOL_selection = getSelection(excluded_categories=["LIWC", "lateSocial", "LongSocial"])
PhonlatePOL_selection = getSelection(excluded_categories=["LIWC", "LongSocial"])
PhonLongPOL_selection = getSelection(excluded_categories=["LIWC", "lateSocial"])
PhonLLPOL_selection = getSelection(excluded_categories=["LIWC"])
CommToget_selection = getSelection(excluded_categories     =["LIWC", "Social","GBSocial", "lateSocial", "LongSocial", "Polarity"])
CommTogetnag_selection = getSelection(excluded_categories  =["LIWC", "Social","GBSocial", "lateSocial", "LongSocial", "Polarity","AgeGender"])
CommTogetnph_selection = getSelection(excluded_categories  =["LIWC", "Social","GBSocial", "lateSocial", "LongSocial", "Polarity","Phonology"])
CommTogetnphag_selection = getSelection(excluded_categories=["LIWC", "Social","GBSocial", "lateSocial", "LongSocial", "Polarity","Phonology","AgeGender"])


classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
name = "Bipolar"
n_fold = 100


In [193]:
len(Phon_selection)

9

In [170]:
for i in set(CommToget_selection)-set(CommTogetnphag_selection):
    print(index2feature[i])

('TP', 'Phonology')
('WC', 'Phonology')
('Ten', 'Phonology')
('gender', 'AgeGender')
('OC', 'Phonology')
('Vow', 'Phonology')
('MO', 'Phonology')
('Obs', 'Phonology')
('Res', 'Phonology')
('age', 'AgeGender')
('Rou', 'Phonology')


## Prepare all Needed Value for Chart

In [88]:
from sklearn import metrics

### Before + After Diagnosed Time

In [136]:
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL12_scores, POL12_labels, _ = pol_groups.getLabelsScores(name+"_12", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL9_scores, POL9_labels, _ = pol_groups.getLabelsScores(name+"_9", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL6_scores, POL6_labels, _ = pol_groups.getLabelsScores(name+"_6", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL3_scores, POL3_labels, _ = pol_groups.getLabelsScores(name+"_3", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL2_scores, POL2_labels, _ = pol_groups.getLabelsScores(name+"_2", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL12_scores, latePOL12_labels, _ = pol_groups.getLabelsScores(name+"_12", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL9_scores, latePOL9_labels, _ = pol_groups.getLabelsScores(name+"_9", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL6_scores, latePOL6_labels, _ = pol_groups.getLabelsScores(name+"_6", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL3_scores, latePOL3_labels, _ = pol_groups.getLabelsScores(name+"_3", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL2_scores, latePOL2_labels, _ = pol_groups.getLabelsScores(name+"_2", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL12_scores, longPOL12_labels, _ = pol_groups.getLabelsScores(name+"_12", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL9_scores, longPOL9_labels, _ = pol_groups.getLabelsScores(name+"_9", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL6_scores, longPOL6_labels, _ = pol_groups.getLabelsScores(name+"_6", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL3_scores, longPOL3_labels, _ = pol_groups.getLabelsScores(name+"_3", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL2_scores, longPOL2_labels, _ = pol_groups.getLabelsScores(name+"_2", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL12_scores, llPOL12_labels, _ = pol_groups.getLabelsScores(name+"_12", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL9_scores, llPOL9_labels, _ = pol_groups.getLabelsScores(name+"_9", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL6_scores, llPOL6_labels, _ = pol_groups.getLabelsScores(name+"_6", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL3_scores, llPOL3_labels, _ = pol_groups.getLabelsScores(name+"_3", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL2_scores, llPOL2_labels, _ = pol_groups.getLabelsScores(name+"_2", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC12_scores, LIWC12_labels, _ = pol_groups.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC9_scores, LIWC9_labels, _ = pol_groups.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC6_scores, LIWC6_labels, _ = pol_groups.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC3_scores, LIWC3_labels, _ = pol_groups.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC2_scores, LIWC2_labels, _ = pol_groups.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf12_scores, tfidf12_labels, _ = tfidf_groups.getLabelsScores(name +"_12", classifier,n_fold=n_fold, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf9_scores, tfidf9_labels, _ = tfidf_groups.getLabelsScores(name +"_9", classifier,n_fold=n_fold, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf6_scores, tfidf6_labels, _ = tfidf_groups.getLabelsScores(name +"_6", classifier,n_fold=n_fold, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf3_scores, tfidf3_labels, _ = tfidf_groups.getLabelsScores(name +"_3", classifier,n_fold=n_fold, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf2_scores, tfidf2_labels, _ = tfidf_groups.getLabelsScores(name +"_2", classifier,n_fold=n_fold, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# Phon12_scores, Phon12_labels, _ = pol_groups.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# Phon9_scores, Phon9_labels, _ = pol_groups.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# Phon6_scores, Phon6_labels, _ = pol_groups.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# Phon3_scores, Phon3_labels, _ = pol_groups.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# Phon2_scores, Phon2_labels, _ = pol_groups.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL12_scores, PhonPOL12_labels, _ = pol_groups.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL9_scores, PhonPOL9_labels, _ = pol_groups.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL6_scores, PhonPOL6_labels, _ = pol_groups.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL3_scores, PhonPOL3_labels, _ = pol_groups.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL2_scores, PhonPOL2_labels, _ = pol_groups.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL12_scores, PhonlatePOL12_labels, _ = pol_groups.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL9_scores, PhonlatePOL9_labels, _ = pol_groups.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL6_scores, PhonlatePOL6_labels, _ = pol_groups.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL3_scores, PhonlatePOL3_labels, _ = pol_groups.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL2_scores, PhonlatePOL2_labels, _ = pol_groups.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL12_scores, PhonLongPOL12_labels, _ = pol_groups.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL9_scores, PhonLongPOL9_labels, _ = pol_groups.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL6_scores, PhonLongPOL6_labels, _ = pol_groups.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL3_scores, PhonLongPOL3_labels, _ = pol_groups.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL2_scores, PhonLongPOL2_labels, _ = pol_groups.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL12_scores, PhonLLPOL12_labels, _ = pol_groups.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL9_scores, PhonLLPOL9_labels, _ = pol_groups.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL6_scores, PhonLLPOL6_labels, _ = pol_groups.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL3_scores, PhonLLPOL3_labels, _ = pol_groups.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL2_scores, PhonLLPOL2_labels, _ = pol_groups.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 2)


# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget12_scores, CommToget12_labels, _ = pol_groups.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget9_scores, CommToget9_labels, _ = pol_groups.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget6_scores, CommToget6_labels, _ = pol_groups.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget3_scores, CommToget3_labels, _ = pol_groups.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget2_scores, CommToget2_labels, _ = pol_groups.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 2)


In [129]:
headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol", "Phon", "Phon Pol", "Phon Late Pol", "Phon Long Pol","Phon Mix Pol", "Common Get"]

LIWC = [(LIWC2_labels,LIWC2_scores),(LIWC3_labels,LIWC3_scores),(LIWC6_labels, LIWC6_scores),(LIWC9_labels, LIWC9_scores),(LIWC12_labels, LIWC12_scores)]
tfidf = [(tfidf2_labels,tfidf2_scores),(tfidf3_labels,tfidf3_scores),(tfidf6_labels, tfidf6_scores),(tfidf9_labels, tfidf9_scores),(tfidf12_labels, tfidf12_scores)]
pol = [(POL2_labels,POL2_scores),(POL3_labels,POL3_scores),(POL6_labels, POL6_scores),(POL9_labels, POL9_scores),(POL12_labels, POL12_scores)]
latePol = [(latePOL2_labels,latePOL2_scores),(latePOL3_labels,latePOL3_scores),(latePOL6_labels, latePOL6_scores),(latePOL9_labels, latePOL9_scores),(latePOL12_labels, latePOL12_scores)]
longPol = [(longPOL2_labels,longPOL2_scores),(longPOL3_labels,longPOL3_scores),(longPOL6_labels, longPOL6_scores),(longPOL9_labels, longPOL9_scores),(longPOL12_labels, longPOL12_scores)]
llPol = [(llPOL2_labels,llPOL2_scores),(llPOL3_labels,llPOL3_scores),(llPOL6_labels, llPOL6_scores),(llPOL9_labels, llPOL9_scores),(llPOL12_labels, llPOL12_scores)]

Phon = [(Phon2_labels,Phon2_scores),(Phon3_labels,Phon3_scores),(Phon6_labels, Phon6_scores),(Phon9_labels, Phon9_scores),(Phon12_labels, Phon12_scores)]
PhonPOL = [(PhonPOL2_labels,PhonPOL2_scores),(PhonPOL3_labels,PhonPOL3_scores),(PhonPOL6_labels, PhonPOL6_scores),(PhonPOL9_labels, PhonPOL9_scores),(PhonPOL12_labels, PhonPOL12_scores)]
PhonlatePOL = [(PhonlatePOL2_labels,PhonlatePOL2_scores),(PhonlatePOL3_labels,PhonlatePOL3_scores),(PhonlatePOL6_labels, PhonlatePOL6_scores),(PhonlatePOL9_labels, PhonlatePOL9_scores),(PhonlatePOL12_labels, PhonlatePOL12_scores)]
PhonLongPOL = [(PhonLongPOL2_labels,PhonLongPOL2_scores),(PhonLongPOL3_labels,PhonLongPOL3_scores),(PhonLongPOL6_labels, PhonLongPOL6_scores),(PhonLongPOL9_labels, PhonLongPOL9_scores),(PhonLongPOL12_labels, PhonLongPOL12_scores)]
PhonLLPOL = [(PhonLLPOL2_labels,PhonLLPOL2_scores),(PhonLLPOL3_labels,PhonLLPOL3_scores),(PhonLLPOL6_labels, PhonLLPOL6_scores),(PhonLLPOL9_labels, PhonLLPOL9_scores),(PhonLLPOL12_labels, PhonLLPOL12_scores)]

CommToget = [(CommToget2_labels,CommToget2_scores),(CommToget3_labels,CommToget3_scores),(CommToget6_labels, CommToget6_scores),(CommToget9_labels, CommToget9_scores),(CommToget12_labels, CommToget12_scores)]


Total_feature_group = [LIWC, tfidf, pol, latePol, longPol, llPol, Phon, PhonPOL, PhonlatePOL, PhonLongPOL, PhonLLPOL, CommToget]


for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features         2 months    3 months    6 months    9 months    12 months    Average
-------------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC             0.422345    0.431228    0.416931    0.360244     0.347298   0.395609
TF-IDF           0.825947    0.850749    0.836148    0.840373     0.837846   0.838213
Pol              0.845211    0.906644    0.889446    0.894535     0.896789   0.886525
Late Pol         0.863892    0.918032    0.905997    0.897363     0.896775   0.896412
Long Pol         0.883179    0.91152     0.898506    0.881562     0.895069   0.893967
Mixed Pol        0.898297    0.929697    0.904004    0.907076     0.891099   0.906035
Phon             0.724042    0.811204    0.781218    0.801424     0.803554   0.784288
Phon Pol         0.839275    0.912218    0.899462    0.877628     0.875783   0.880873
Phon Late Pol    0.846284    0.912513    0.903729    0.908209     0.890606   0.892268
Phon Long Pol   

## Before TFIDF change word

In [120]:
headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol", "Phon", "Phon Pol", "Phon Late Pol", "Phon Long Pol","Phon Mix Pol"]

LIWC = [(LIWC2_labels,LIWC2_scores),(LIWC3_labels,LIWC3_scores),(LIWC6_labels, LIWC6_scores),(LIWC9_labels, LIWC9_scores),(LIWC12_labels, LIWC12_scores)]
tfidf = [(tfidf2_labels,tfidf2_scores),(tfidf3_labels,tfidf3_scores),(tfidf6_labels, tfidf6_scores),(tfidf9_labels, tfidf9_scores),(tfidf12_labels, tfidf12_scores)]
pol = [(POL2_labels,POL2_scores),(POL3_labels,POL3_scores),(POL6_labels, POL6_scores),(POL9_labels, POL9_scores),(POL12_labels, POL12_scores)]
latePol = [(latePOL2_labels,latePOL2_scores),(latePOL3_labels,latePOL3_scores),(latePOL6_labels, latePOL6_scores),(latePOL9_labels, latePOL9_scores),(latePOL12_labels, latePOL12_scores)]
longPol = [(longPOL2_labels,longPOL2_scores),(longPOL3_labels,longPOL3_scores),(longPOL6_labels, longPOL6_scores),(longPOL9_labels, longPOL9_scores),(longPOL12_labels, longPOL12_scores)]
llPol = [(llPOL2_labels,llPOL2_scores),(llPOL3_labels,llPOL3_scores),(llPOL6_labels, llPOL6_scores),(llPOL9_labels, llPOL9_scores),(llPOL12_labels, llPOL12_scores)]

Phon = [(Phon2_labels,Phon2_scores),(Phon3_labels,Phon3_scores),(Phon6_labels, Phon6_scores),(Phon9_labels, Phon9_scores),(Phon12_labels, Phon12_scores)]
PhonPOL = [(PhonPOL2_labels,PhonPOL2_scores),(PhonPOL3_labels,PhonPOL3_scores),(PhonPOL6_labels, PhonPOL6_scores),(PhonPOL9_labels, PhonPOL9_scores),(PhonPOL12_labels, PhonPOL12_scores)]
PhonlatePOL = [(PhonlatePOL2_labels,PhonlatePOL2_scores),(PhonlatePOL3_labels,PhonlatePOL3_scores),(PhonlatePOL6_labels, PhonlatePOL6_scores),(PhonlatePOL9_labels, PhonlatePOL9_scores),(PhonlatePOL12_labels, PhonlatePOL12_scores)]
PhonLongPOL = [(PhonLongPOL2_labels,PhonLongPOL2_scores),(PhonLongPOL3_labels,PhonLongPOL3_scores),(PhonLongPOL6_labels, PhonLongPOL6_scores),(PhonLongPOL9_labels, PhonLongPOL9_scores),(PhonLongPOL12_labels, PhonLongPOL12_scores)]
PhonLLPOL = [(PhonLLPOL2_labels,PhonLLPOL2_scores),(PhonLLPOL3_labels,PhonLLPOL3_scores),(PhonLLPOL6_labels, PhonLLPOL6_scores),(PhonLLPOL9_labels, PhonLLPOL9_scores),(PhonLLPOL12_labels, PhonLLPOL12_scores)]

Total_feature_group = [LIWC, tfidf, pol, latePol, longPol, llPol, Phon, PhonPOL, PhonlatePOL, PhonLongPOL, PhonLLPOL]


for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features         2 months    3 months    6 months    9 months    12 months    Average
-------------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC             0.422345    0.431228    0.416931    0.360244     0.347298   0.395609
TF-IDF           0.82688     0.8582      0.847223    0.84701      0.841065   0.844076
Pol              0.845211    0.906644    0.889446    0.894535     0.896789   0.886525
Late Pol         0.863892    0.918032    0.905997    0.897363     0.896775   0.896412
Long Pol         0.883179    0.91152     0.898506    0.881562     0.895069   0.893967
Mixed Pol        0.898297    0.929697    0.904004    0.907076     0.891099   0.906035
Phon             0.724042    0.811204    0.781218    0.801424     0.803554   0.784288
Phon Pol         0.839275    0.912218    0.899462    0.877628     0.875783   0.880873
Phon Late Pol    0.846284    0.912513    0.903729    0.908209     0.890606   0.892268
Phon Long Pol   

### Before Diagnosed time

In [194]:
name = 'Bd'
n_fold = 100

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL12_scores_, POL12_labels_, _ = pol_groups_.getLabelsScores(name+"_12", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL9_scores_, POL9_labels_, _ = pol_groups_.getLabelsScores(name+"_9", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL6_scores_, POL6_labels_, _ = pol_groups_.getLabelsScores(name+"_6", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL3_scores_, POL3_labels_, _ = pol_groups_.getLabelsScores(name+"_3", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# POL2_scores_, POL2_labels_, _ = pol_groups_.getLabelsScores(name+"_2", classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL12_scores_, latePOL12_labels_, _ = pol_groups_.getLabelsScores(name+"_12", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL9_scores_, latePOL9_labels_, _ = pol_groups_.getLabelsScores(name+"_9", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL6_scores_, latePOL6_labels_, _ = pol_groups_.getLabelsScores(name+"_6", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL3_scores_, latePOL3_labels_, _ = pol_groups_.getLabelsScores(name+"_3", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# latePOL2_scores_, latePOL2_labels_, _ = pol_groups_.getLabelsScores(name+"_2", classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL12_scores_, longPOL12_labels_, _ = pol_groups_.getLabelsScores(name+"_12", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL9_scores_, longPOL9_labels_, _ = pol_groups_.getLabelsScores(name+"_9", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL6_scores_, longPOL6_labels_, _ = pol_groups_.getLabelsScores(name+"_6", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL3_scores_, longPOL3_labels_, _ = pol_groups_.getLabelsScores(name+"_3", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# longPOL2_scores_, longPOL2_labels_, _ = pol_groups_.getLabelsScores(name+"_2", classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL12_scores_, llPOL12_labels_, _ = pol_groups_.getLabelsScores(name+"_12", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL9_scores_, llPOL9_labels_, _ = pol_groups_.getLabelsScores(name+"_9", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL6_scores_, llPOL6_labels_, _ = pol_groups_.getLabelsScores(name+"_6", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL3_scores_, llPOL3_labels_, _ = pol_groups_.getLabelsScores(name+"_3", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# llPOL2_scores_, llPOL2_labels_, _ = pol_groups_.getLabelsScores(name+"_2", classifier,n_fold=n_fold, selection=LLPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC12_scores_, LIWC12_labels_, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC9_scores_, LIWC9_labels_, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC6_scores_, LIWC6_labels_, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC3_scores_, LIWC3_labels_, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# LIWC2_scores_, LIWC2_labels_, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf12_scores_, tfidf12_labels_, _ = tfidf_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf9_scores_, tfidf9_labels_, _ = tfidf_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf6_scores_, tfidf6_labels_, _ = tfidf_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf3_scores_, tfidf3_labels_, _ = tfidf_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# tfidf2_scores_, tfidf2_labels_, _ = tfidf_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, consider_time = 2)

classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
Phon12_scores_, Phon12_labels_, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 12)
classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
Phon9_scores_, Phon9_labels_, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 9)
classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
Phon6_scores_, Phon6_labels_, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 6)
classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
Phon3_scores_, Phon3_labels_, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 3)
classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
Phon2_scores_, Phon2_labels_, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=Phon_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL12_scores_, PhonPOL12_labels_, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL9_scores_, PhonPOL9_labels_, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL6_scores_, PhonPOL6_labels_, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL3_scores_, PhonPOL3_labels_, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonPOL2_scores_, PhonPOL2_labels_, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=PhonPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL12_scores_, PhonlatePOL12_labels_, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL9_scores_, PhonlatePOL9_labels_, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL6_scores_, PhonlatePOL6_labels_, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL3_scores_, PhonlatePOL3_labels_, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonlatePOL2_scores_, PhonlatePOL2_labels_, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=PhonlatePOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL12_scores_, PhonLongPOL12_labels_, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL9_scores_, PhonLongPOL9_labels_, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL6_scores_, PhonLongPOL6_labels_, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL3_scores_, PhonLongPOL3_labels_, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLongPOL2_scores_, PhonLongPOL2_labels_, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=PhonLongPOL_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL12_scores_, PhonLLPOL12_labels_, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL9_scores_, PhonLLPOL9_labels_, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL6_scores_, PhonLLPOL6_labels_, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL3_scores_, PhonLLPOL3_labels_, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# PhonLLPOL2_scores_, PhonLLPOL2_labels_, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=PhonLLPOL_selection, consider_time = 2)


# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget_12_scores, CommToget_12_labels, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget_9_scores, CommToget_9_labels, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget_6_scores, CommToget_6_labels, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget_3_scores, CommToget_3_labels, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommToget_2_scores, CommToget_2_labels, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=CommToget_selection, consider_time = 2)


# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnph_12_scores, CommTogetnph_12_labels, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=CommTogetnph_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnph_9_scores, CommTogetnph_9_labels, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=CommTogetnph_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnph_6_scores, CommTogetnph_6_labels, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=CommTogetnph_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnph_3_scores, CommTogetnph_3_labels, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=CommTogetnph_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnph_2_scores, CommTogetnph_2_labels, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=CommTogetnph_selection, consider_time = 2)

# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnag_12_scores, CommTogetnag_12_labels, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=CommTogetnag_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnag_9_scores, CommTogetnag_9_labels, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=CommTogetnag_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnag_6_scores, CommTogetnag_6_labels, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=CommTogetnag_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnag_3_scores, CommTogetnag_3_labels, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=CommTogetnag_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnag_2_scores, CommTogetnag_2_labels, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=CommTogetnag_selection, consider_time = 2)



# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnphag_12_scores, CommTogetnphag_12_labels, _ = pol_groups_.getLabelsScores(name +"_12", classifier,n_fold=n_fold, selection=CommTogetnphag_selection, consider_time = 12)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnphag_9_scores, CommTogetnphag_9_labels, _ = pol_groups_.getLabelsScores(name +"_9", classifier,n_fold=n_fold, selection=CommTogetnphag_selection, consider_time = 9)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnphag_6_scores, CommTogetnphag_6_labels, _ = pol_groups_.getLabelsScores(name +"_6", classifier,n_fold=n_fold, selection=CommTogetnphag_selection, consider_time = 6)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnphag_3_scores, CommTogetnphag_3_labels, _ = pol_groups_.getLabelsScores(name +"_3", classifier,n_fold=n_fold, selection=CommTogetnphag_selection, consider_time = 3)
# classifier  = RandomForestClassifier(n_jobs= -1, max_features="sqrt", n_estimators=128)
# CommTogetnphag_2_scores, CommTogetnphag_2_labels, _ = pol_groups_.getLabelsScores(name +"_2", classifier,n_fold=n_fold, selection=CommTogetnphag_selection, consider_time = 2)



In [195]:

headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol", "Phon", "Phon Pol", "Phon Late Pol", "Phon Long Pol","Phon Mix Pol", "Common", "Common no ag", "Common No Pho", "Common no PhoAg"]
LIWC_ = [(LIWC2_labels_,LIWC2_scores_),(LIWC3_labels_,LIWC3_scores_),(LIWC6_labels_, LIWC6_scores_),(LIWC9_labels_, LIWC9_scores_),(LIWC12_labels_, LIWC12_scores_)]
tfidf_ = [(tfidf2_labels_,tfidf2_scores_),(tfidf3_labels_,tfidf3_scores_),(tfidf6_labels_, tfidf6_scores_),(tfidf9_labels_, tfidf9_scores_),(tfidf12_labels_, tfidf12_scores_)]
pol_ = [(POL2_labels_,POL2_scores_),(POL3_labels_,POL3_scores_),(POL6_labels_, POL6_scores_),(POL9_labels_, POL9_scores_),(POL12_labels_, POL12_scores_)]
latePol_ = [(latePOL2_labels_,latePOL2_scores_),(latePOL3_labels_,latePOL3_scores_),(latePOL6_labels_, latePOL6_scores_),(latePOL9_labels_, latePOL9_scores_),(latePOL12_labels_, latePOL12_scores_)]
longPol_ = [(longPOL2_labels_,longPOL2_scores_),(longPOL3_labels_,longPOL3_scores_),(longPOL6_labels_, longPOL6_scores_),(longPOL9_labels_, longPOL9_scores_),(longPOL12_labels_, longPOL12_scores_)]
llPol_ = [(llPOL2_labels_,llPOL2_scores_),(llPOL3_labels_,llPOL3_scores_),(llPOL6_labels_, llPOL6_scores_),(llPOL9_labels_, llPOL9_scores_),(llPOL12_labels_, llPOL12_scores_)]

Phon_ = [(Phon2_labels_,Phon2_scores_),(Phon3_labels_,Phon3_scores_),(Phon6_labels_, Phon6_scores_),(Phon9_labels_, Phon9_scores_),(Phon12_labels_, Phon12_scores_)]
PhonPOL_ = [(PhonPOL2_labels_,PhonPOL2_scores_),(PhonPOL3_labels_,PhonPOL3_scores_),(PhonPOL6_labels_, PhonPOL6_scores_),(PhonPOL9_labels_, PhonPOL9_scores_),(PhonPOL12_labels_, PhonPOL12_scores_)]
PhonlatePOL_ = [(PhonlatePOL2_labels_,PhonlatePOL2_scores_),(PhonlatePOL3_labels_,PhonlatePOL3_scores_),(PhonlatePOL6_labels_, PhonlatePOL6_scores_),(PhonlatePOL9_labels_, PhonlatePOL9_scores_),(PhonlatePOL12_labels_, PhonlatePOL12_scores_)]
PhonLongPOL_ = [(PhonLongPOL2_labels_,PhonLongPOL2_scores_),(PhonLongPOL3_labels_,PhonLongPOL3_scores_),(PhonLongPOL6_labels_, PhonLongPOL6_scores_),(PhonLongPOL9_labels_, PhonLongPOL9_scores_),(PhonLongPOL12_labels_, PhonLongPOL12_scores_)]
PhonLLPOL_ = [(PhonLLPOL2_labels_,PhonLLPOL2_scores_),(PhonLLPOL3_labels_,PhonLLPOL3_scores_),(PhonLLPOL6_labels_, PhonLLPOL6_scores_),(PhonLLPOL9_labels_, PhonLLPOL9_scores_),(PhonLLPOL12_labels_, PhonLLPOL12_scores_)]

CommToget_ = [(CommToget_2_labels,CommToget_2_scores),(CommToget_3_labels,CommToget_3_scores),(CommToget_6_labels, CommToget_6_scores),(CommToget_9_labels, CommToget_9_scores),(CommToget_12_labels, CommToget_12_scores)]
CommTogetnph_ = [(CommTogetnph_2_labels,CommTogetnph_2_scores),(CommTogetnph_3_labels,CommTogetnph_3_scores),(CommTogetnph_6_labels, CommTogetnph_6_scores),(CommTogetnph_9_labels, CommTogetnph_9_scores),(CommTogetnph_12_labels, CommTogetnph_12_scores)]
CommTogetnag_ = [(CommTogetnag_2_labels,CommTogetnag_2_scores),(CommTogetnag_3_labels,CommTogetnag_3_scores),(CommTogetnag_6_labels, CommTogetnag_6_scores),(CommTogetnag_9_labels, CommTogetnag_9_scores),(CommTogetnag_12_labels, CommTogetnag_12_scores)]
CommTogetnphag_ = [(CommTogetnphag_2_labels,CommTogetnphag_2_scores),(CommTogetnphag_3_labels,CommTogetnphag_3_scores),(CommTogetnphag_6_labels, CommTogetnphag_6_scores),(CommTogetnphag_9_labels, CommTogetnphag_9_scores),(CommTogetnphag_12_labels, CommTogetnphag_12_scores)]

Total_feature_group = [LIWC_, tfidf_, pol_, latePol_, longPol_, llPol_, Phon_, PhonPOL_, PhonlatePOL_, PhonLongPOL_, PhonLLPOL_, CommToget_, CommTogetnag_, CommTogetnph_, CommTogetnphag_]

for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features           2 months    3 months    6 months    9 months    12 months    Average
---------------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC               0.43842     0.382789    0.379245    0.417005     0.38612    0.400715
TF-IDF             0.936451    0.920352    0.864826    0.850732     0.802966   0.875065
Pol                0.978121    0.981332    0.965821    0.974411     0.962323   0.972401
Late Pol           0.977614    0.977482    0.963338    0.969916     0.96332    0.970334
Long Pol           0.980614    0.980416    0.968322    0.975449     0.972049   0.97537
Mixed Pol          0.978494    0.981227    0.972317    0.971717     0.964656   0.973682
Phon               0.891203    0.898079    0.817514    0.813887     0.806228   0.845382
Phon Pol           0.978242    0.982673    0.968596    0.974862     0.96649    0.974173
Phon Late Pol      0.980543    0.984568    0.969164    0.970431     0.95944    0.97

In [176]:

headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol", "Phon", "Phon Pol", "Phon Late Pol", "Phon Long Pol","Phon Mix Pol", "Emo+Age+Gender+Phono", "Emo+Phono", "Emo+Age + Gender", "Emotion"]
LIWC_ = [(LIWC2_labels_,LIWC2_scores_),(LIWC3_labels_,LIWC3_scores_),(LIWC6_labels_, LIWC6_scores_),(LIWC9_labels_, LIWC9_scores_),(LIWC12_labels_, LIWC12_scores_)]
tfidf_ = [(tfidf2_labels_,tfidf2_scores_),(tfidf3_labels_,tfidf3_scores_),(tfidf6_labels_, tfidf6_scores_),(tfidf9_labels_, tfidf9_scores_),(tfidf12_labels_, tfidf12_scores_)]
pol_ = [(POL2_labels_,POL2_scores_),(POL3_labels_,POL3_scores_),(POL6_labels_, POL6_scores_),(POL9_labels_, POL9_scores_),(POL12_labels_, POL12_scores_)]
latePol_ = [(latePOL2_labels_,latePOL2_scores_),(latePOL3_labels_,latePOL3_scores_),(latePOL6_labels_, latePOL6_scores_),(latePOL9_labels_, latePOL9_scores_),(latePOL12_labels_, latePOL12_scores_)]
longPol_ = [(longPOL2_labels_,longPOL2_scores_),(longPOL3_labels_,longPOL3_scores_),(longPOL6_labels_, longPOL6_scores_),(longPOL9_labels_, longPOL9_scores_),(longPOL12_labels_, longPOL12_scores_)]
llPol_ = [(llPOL2_labels_,llPOL2_scores_),(llPOL3_labels_,llPOL3_scores_),(llPOL6_labels_, llPOL6_scores_),(llPOL9_labels_, llPOL9_scores_),(llPOL12_labels_, llPOL12_scores_)]

Phon_ = [(Phon2_labels_,Phon2_scores_),(Phon3_labels_,Phon3_scores_),(Phon6_labels_, Phon6_scores_),(Phon9_labels_, Phon9_scores_),(Phon12_labels_, Phon12_scores_)]
PhonPOL_ = [(PhonPOL2_labels_,PhonPOL2_scores_),(PhonPOL3_labels_,PhonPOL3_scores_),(PhonPOL6_labels_, PhonPOL6_scores_),(PhonPOL9_labels_, PhonPOL9_scores_),(PhonPOL12_labels_, PhonPOL12_scores_)]
PhonlatePOL_ = [(PhonlatePOL2_labels_,PhonlatePOL2_scores_),(PhonlatePOL3_labels_,PhonlatePOL3_scores_),(PhonlatePOL6_labels_, PhonlatePOL6_scores_),(PhonlatePOL9_labels_, PhonlatePOL9_scores_),(PhonlatePOL12_labels_, PhonlatePOL12_scores_)]
PhonLongPOL_ = [(PhonLongPOL2_labels_,PhonLongPOL2_scores_),(PhonLongPOL3_labels_,PhonLongPOL3_scores_),(PhonLongPOL6_labels_, PhonLongPOL6_scores_),(PhonLongPOL9_labels_, PhonLongPOL9_scores_),(PhonLongPOL12_labels_, PhonLongPOL12_scores_)]
PhonLLPOL_ = [(PhonLLPOL2_labels_,PhonLLPOL2_scores_),(PhonLLPOL3_labels_,PhonLLPOL3_scores_),(PhonLLPOL6_labels_, PhonLLPOL6_scores_),(PhonLLPOL9_labels_, PhonLLPOL9_scores_),(PhonLLPOL12_labels_, PhonLLPOL12_scores_)]

CommToget_ = [(CommToget_2_labels,CommToget_2_scores),(CommToget_3_labels,CommToget_3_scores),(CommToget_6_labels, CommToget_6_scores),(CommToget_9_labels, CommToget_9_scores),(CommToget_12_labels, CommToget_12_scores)]
CommTogetnph_ = [(CommTogetnph_2_labels,CommTogetnph_2_scores),(CommTogetnph_3_labels,CommTogetnph_3_scores),(CommTogetnph_6_labels, CommTogetnph_6_scores),(CommTogetnph_9_labels, CommTogetnph_9_scores),(CommTogetnph_12_labels, CommTogetnph_12_scores)]
CommTogetnag_ = [(CommTogetnag_2_labels,CommTogetnag_2_scores),(CommTogetnag_3_labels,CommTogetnag_3_scores),(CommTogetnag_6_labels, CommTogetnag_6_scores),(CommTogetnag_9_labels, CommTogetnag_9_scores),(CommTogetnag_12_labels, CommTogetnag_12_scores)]
CommTogetnphag_ = [(CommTogetnphag_2_labels,CommTogetnphag_2_scores),(CommTogetnphag_3_labels,CommTogetnphag_3_scores),(CommTogetnphag_6_labels, CommTogetnphag_6_scores),(CommTogetnphag_9_labels, CommTogetnphag_9_scores),(CommTogetnphag_12_labels, CommTogetnphag_12_scores)]

Total_feature_group = [LIWC_, tfidf_, pol_, latePol_, longPol_, llPol_, Phon_, PhonPOL_, PhonlatePOL_, PhonLongPOL_, PhonLLPOL_, CommToget_, CommTogetnag_, CommTogetnph_, CommTogetnphag_]

for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features                2 months    3 months    6 months    9 months    12 months    Average
--------------------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC                    0.43842     0.382789    0.379245    0.417005     0.38612    0.400715
TF-IDF                  0.936451    0.920352    0.864826    0.850732     0.802966   0.875065
Pol                     0.978121    0.981332    0.965821    0.974411     0.962323   0.972401
Late Pol                0.977614    0.977482    0.963338    0.969916     0.96332    0.970334
Long Pol                0.980614    0.980416    0.968322    0.975449     0.972049   0.97537
Mixed Pol               0.978494    0.981227    0.972317    0.971717     0.964656   0.973682
Phon                    0.882757    0.897765    0.810457    0.832712     0.816563   0.848051
Phon Pol                0.978242    0.982673    0.968596    0.974862     0.96649    0.974173
Phon Late Pol           0.980543 

## Before taking out the polarity

In [132]:

headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol", "Phon", "Phon Pol", "Phon Late Pol", "Phon Long Pol","Phon Mix Pol", "Common Get", "Common No Phon"]
LIWC_ = [(LIWC2_labels_,LIWC2_scores_),(LIWC3_labels_,LIWC3_scores_),(LIWC6_labels_, LIWC6_scores_),(LIWC9_labels_, LIWC9_scores_),(LIWC12_labels_, LIWC12_scores_)]
tfidf_ = [(tfidf2_labels_,tfidf2_scores_),(tfidf3_labels_,tfidf3_scores_),(tfidf6_labels_, tfidf6_scores_),(tfidf9_labels_, tfidf9_scores_),(tfidf12_labels_, tfidf12_scores_)]
pol_ = [(POL2_labels_,POL2_scores_),(POL3_labels_,POL3_scores_),(POL6_labels_, POL6_scores_),(POL9_labels_, POL9_scores_),(POL12_labels_, POL12_scores_)]
latePol_ = [(latePOL2_labels_,latePOL2_scores_),(latePOL3_labels_,latePOL3_scores_),(latePOL6_labels_, latePOL6_scores_),(latePOL9_labels_, latePOL9_scores_),(latePOL12_labels_, latePOL12_scores_)]
longPol_ = [(longPOL2_labels_,longPOL2_scores_),(longPOL3_labels_,longPOL3_scores_),(longPOL6_labels_, longPOL6_scores_),(longPOL9_labels_, longPOL9_scores_),(longPOL12_labels_, longPOL12_scores_)]
llPol_ = [(llPOL2_labels_,llPOL2_scores_),(llPOL3_labels_,llPOL3_scores_),(llPOL6_labels_, llPOL6_scores_),(llPOL9_labels_, llPOL9_scores_),(llPOL12_labels_, llPOL12_scores_)]

Phon_ = [(Phon2_labels_,Phon2_scores_),(Phon3_labels_,Phon3_scores_),(Phon6_labels_, Phon6_scores_),(Phon9_labels_, Phon9_scores_),(Phon12_labels_, Phon12_scores_)]
PhonPOL_ = [(PhonPOL2_labels_,PhonPOL2_scores_),(PhonPOL3_labels_,PhonPOL3_scores_),(PhonPOL6_labels_, PhonPOL6_scores_),(PhonPOL9_labels_, PhonPOL9_scores_),(PhonPOL12_labels_, PhonPOL12_scores_)]
PhonlatePOL_ = [(PhonlatePOL2_labels_,PhonlatePOL2_scores_),(PhonlatePOL3_labels_,PhonlatePOL3_scores_),(PhonlatePOL6_labels_, PhonlatePOL6_scores_),(PhonlatePOL9_labels_, PhonlatePOL9_scores_),(PhonlatePOL12_labels_, PhonlatePOL12_scores_)]
PhonLongPOL_ = [(PhonLongPOL2_labels_,PhonLongPOL2_scores_),(PhonLongPOL3_labels_,PhonLongPOL3_scores_),(PhonLongPOL6_labels_, PhonLongPOL6_scores_),(PhonLongPOL9_labels_, PhonLongPOL9_scores_),(PhonLongPOL12_labels_, PhonLongPOL12_scores_)]
PhonLLPOL_ = [(PhonLLPOL2_labels_,PhonLLPOL2_scores_),(PhonLLPOL3_labels_,PhonLLPOL3_scores_),(PhonLLPOL6_labels_, PhonLLPOL6_scores_),(PhonLLPOL9_labels_, PhonLLPOL9_scores_),(PhonLLPOL12_labels_, PhonLLPOL12_scores_)]

CommToget_ = [(CommToget_2_labels,CommToget_2_scores),(CommToget_3_labels,CommToget_3_scores),(CommToget_6_labels, CommToget_6_scores),(CommToget_9_labels, CommToget_9_scores),(CommToget_12_labels, CommToget_12_scores)]
CommTogetnph_ = [(CommTogetnph_2_labels,CommTogetnph_2_scores),(CommTogetnph_3_labels,CommTogetnph_3_scores),(CommTogetnph_6_labels, CommTogetnph_6_scores),(CommTogetnph_9_labels, CommTogetnph_9_scores),(CommTogetnph_12_labels, CommTogetnph_12_scores)]

Total_feature_group = [LIWC_, tfidf_, pol_, latePol_, longPol_, llPol_, Phon_, PhonPOL_, PhonlatePOL_, PhonLongPOL_, PhonLLPOL_, CommToget_, CommTogetnph_]

for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features         2 months    3 months    6 months    9 months    12 months    Average
-------------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC             0.425121    0.384562    0.381148    0.417154     0.381866   0.39797
TF-IDF           0.93404     0.927151    0.866328    0.839719     0.808775   0.875203
Pol              0.977496    0.981243    0.966278    0.970922     0.965762   0.97234
Late Pol         0.977784    0.979808    0.960108    0.972295     0.968722   0.971744
Long Pol         0.976042    0.980644    0.966645    0.973922     0.968189   0.973088
Mixed Pol        0.979684    0.980028    0.965326    0.971705     0.968719   0.973092
Phon             0.866033    0.887253    0.821076    0.810936     0.824139   0.841887
Phon Pol         0.978941    0.984816    0.962934    0.977591     0.969448   0.974746
Phon Late Pol    0.973537    0.984647    0.964734    0.971568     0.96487    0.971871
Phon Long Pol    0

## before tfidf word change

In [416]:
headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol", "Phon", "Phon Pol", "Phon Late Pol", "Phon Long Pol","Phon Mix Pol"]
LIWC_ = [(LIWC2_labels_,LIWC2_scores_),(LIWC3_labels_,LIWC3_scores_),(LIWC6_labels_, LIWC6_scores_),(LIWC9_labels_, LIWC9_scores_),(LIWC12_labels_, LIWC12_scores_)]
tfidf_ = [(tfidf2_labels_,tfidf2_scores_),(tfidf3_labels_,tfidf3_scores_),(tfidf6_labels_, tfidf6_scores_),(tfidf9_labels_, tfidf9_scores_),(tfidf12_labels_, tfidf12_scores_)]
pol_ = [(POL2_labels_,POL2_scores_),(POL3_labels_,POL3_scores_),(POL6_labels_, POL6_scores_),(POL9_labels_, POL9_scores_),(POL12_labels_, POL12_scores_)]
latePol_ = [(latePOL2_labels_,latePOL2_scores_),(latePOL3_labels_,latePOL3_scores_),(latePOL6_labels_, latePOL6_scores_),(latePOL9_labels_, latePOL9_scores_),(latePOL12_labels_, latePOL12_scores_)]
longPol_ = [(longPOL2_labels_,longPOL2_scores_),(longPOL3_labels_,longPOL3_scores_),(longPOL6_labels_, longPOL6_scores_),(longPOL9_labels_, longPOL9_scores_),(longPOL12_labels_, longPOL12_scores_)]
llPol_ = [(llPOL2_labels_,llPOL2_scores_),(llPOL3_labels_,llPOL3_scores_),(llPOL6_labels_, llPOL6_scores_),(llPOL9_labels_, llPOL9_scores_),(llPOL12_labels_, llPOL12_scores_)]

Phon_ = [(Phon2_labels_,Phon2_scores_),(Phon3_labels_,Phon3_scores_),(Phon6_labels_, Phon6_scores_),(Phon9_labels_, Phon9_scores_),(Phon12_labels_, Phon12_scores_)]
PhonPOL_ = [(PhonPOL2_labels_,PhonPOL2_scores_),(PhonPOL3_labels_,PhonPOL3_scores_),(PhonPOL6_labels_, PhonPOL6_scores_),(PhonPOL9_labels_, PhonPOL9_scores_),(PhonPOL12_labels_, PhonPOL12_scores_)]
PhonlatePOL_ = [(PhonlatePOL2_labels_,PhonlatePOL2_scores_),(PhonlatePOL3_labels_,PhonlatePOL3_scores_),(PhonlatePOL6_labels_, PhonlatePOL6_scores_),(PhonlatePOL9_labels_, PhonlatePOL9_scores_),(PhonlatePOL12_labels_, PhonlatePOL12_scores_)]
PhonLongPOL_ = [(PhonLongPOL2_labels_,PhonLongPOL2_scores_),(PhonLongPOL3_labels_,PhonLongPOL3_scores_),(PhonLongPOL6_labels_, PhonLongPOL6_scores_),(PhonLongPOL9_labels_, PhonLongPOL9_scores_),(PhonLongPOL12_labels_, PhonLongPOL12_scores_)]
PhonLLPOL_ = [(PhonLLPOL2_labels_,PhonLLPOL2_scores_),(PhonLLPOL3_labels_,PhonLLPOL3_scores_),(PhonLLPOL6_labels_, PhonLLPOL6_scores_),(PhonLLPOL9_labels_, PhonLLPOL9_scores_),(PhonLLPOL12_labels_, PhonLLPOL12_scores_)]

Total_feature_group = [LIWC_, tfidf_, pol_, latePol_, longPol_, llPol_, Phon_, PhonPOL_, PhonlatePOL_, PhonLongPOL_, PhonLLPOL_]

for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features         2 months    3 months    6 months    9 months    12 months    Average
-------------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC             0.430009    0.391035    0.376955    0.403267     0.37193    0.394639
TF-IDF           0.943798    0.930274    0.872979    0.849256     0.817855   0.882832
Pol              0.977398    0.979192    0.966807    0.975372     0.966768   0.973107
Late Pol         0.976021    0.980859    0.965351    0.971038     0.959931   0.97064
Long Pol         0.979906    0.978198    0.970837    0.97739      0.961335   0.973533
Mixed Pol        0.980584    0.980583    0.968381    0.972768     0.970396   0.974543
Phon             0.889465    0.879761    0.801523    0.8383       0.820669   0.845943
Phon Pol         0.976657    0.984543    0.965955    0.973915     0.960614   0.972337
Phon Late Pol    0.975865    0.98195     0.964447    0.971769     0.962314   0.971269
Phon Long Pol    

In [359]:
headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol", "Phon", "Phon Pol", "Phon Late Pol", "Phon Long Pol","Phon Mix Pol"]
LIWC_ = [(LIWC2_labels_,LIWC2_scores_),(LIWC3_labels_,LIWC3_scores_),(LIWC6_labels_, LIWC6_scores_),(LIWC9_labels_, LIWC9_scores_),(LIWC12_labels_, LIWC12_scores_)]
tfidf_ = [(tfidf2_labels_,tfidf2_scores_),(tfidf3_labels_,tfidf3_scores_),(tfidf6_labels_, tfidf6_scores_),(tfidf9_labels_, tfidf9_scores_),(tfidf12_labels_, tfidf12_scores_)]
pol_ = [(POL2_labels_,POL2_scores_),(POL3_labels_,POL3_scores_),(POL6_labels_, POL6_scores_),(POL9_labels_, POL9_scores_),(POL12_labels_, POL12_scores_)]
latePol_ = [(latePOL2_labels_,latePOL2_scores_),(latePOL3_labels_,latePOL3_scores_),(latePOL6_labels_, latePOL6_scores_),(latePOL9_labels_, latePOL9_scores_),(latePOL12_labels_, latePOL12_scores_)]
longPol_ = [(longPOL2_labels_,longPOL2_scores_),(longPOL3_labels_,longPOL3_scores_),(longPOL6_labels_, longPOL6_scores_),(longPOL9_labels_, longPOL9_scores_),(longPOL12_labels_, longPOL12_scores_)]
llPol_ = [(llPOL2_labels_,llPOL2_scores_),(llPOL3_labels_,llPOL3_scores_),(llPOL6_labels_, llPOL6_scores_),(llPOL9_labels_, llPOL9_scores_),(llPOL12_labels_, llPOL12_scores_)]

Phon_ = [(Phon2_labels_,Phon2_scores_),(Phon3_labels_,Phon3_scores_),(Phon6_labels_, Phon6_scores_),(Phon9_labels_, Phon9_scores_),(Phon12_labels_, Phon12_scores_)]
PhonPOL_ = [(PhonPOL2_labels_,PhonPOL2_scores_),(PhonPOL3_labels_,PhonPOL3_scores_),(PhonPOL6_labels_, PhonPOL6_scores_),(PhonPOL9_labels_, PhonPOL9_scores_),(PhonPOL12_labels_, PhonPOL12_scores_)]
PhonlatePOL_ = [(PhonlatePOL2_labels_,PhonlatePOL2_scores_),(PhonlatePOL3_labels_,PhonlatePOL3_scores_),(PhonlatePOL6_labels_, PhonlatePOL6_scores_),(PhonlatePOL9_labels_, PhonlatePOL9_scores_),(PhonlatePOL12_labels_, PhonlatePOL12_scores_)]
PhonLongPOL_ = [(PhonLongPOL2_labels_,PhonLongPOL2_scores_),(PhonLongPOL3_labels_,PhonLongPOL3_scores_),(PhonLongPOL6_labels_, PhonLongPOL6_scores_),(PhonLongPOL9_labels_, PhonLongPOL9_scores_),(PhonLongPOL12_labels_, PhonLongPOL12_scores_)]
PhonLLPOL_ = [(PhonLLPOL2_labels_,PhonLLPOL2_scores_),(PhonLLPOL3_labels_,PhonLLPOL3_scores_),(PhonLLPOL6_labels_, PhonLLPOL6_scores_),(PhonLLPOL9_labels_, PhonLLPOL9_scores_),(PhonLLPOL12_labels_, PhonLLPOL12_scores_)]

Total_feature_group = [LIWC_, tfidf_, pol_, latePol_, longPol_, llPol_, Phon_, PhonPOL_, PhonlatePOL_, PhonLongPOL_, PhonLLPOL_]

for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features         2 months    3 months    6 months    9 months    12 months    Average
-------------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC             0.438061    0.372668    0.384509    0.412877     0.404411   0.402505
TF-IDF           0.951101    0.926041    0.856932    0.849181     0.799452   0.876542
Pol              0.97798     0.979089    0.971508    0.974856     0.961214   0.972929
Late Pol         0.972485    0.980349    0.967574    0.969107     0.967506   0.971404
Long Pol         0.982929    0.98249     0.968635    0.978332     0.970294   0.976536
Mixed Pol        0.975391    0.977627    0.973033    0.968322     0.963989   0.971672
Phon             0.874824    0.89409     0.838169    0.829617     0.805297   0.848399
Phon Pol         0.979886    0.986389    0.975368    0.973029     0.957949   0.974524
Phon Late Pol    0.976729    0.975757    0.96022     0.968415     0.962389   0.968702
Phon Long Pol   

In [362]:
print(metrics.classification_report(PhonLLPOL3_labels_[:,0],map(lambda val: 0 if val <0.5 else 1, PhonLLPOL3_scores_)))

             precision    recall  f1-score   support

        0.0       0.94      0.98      0.96      1300
        1.0       0.96      0.89      0.92       700

avg / total       0.95      0.95      0.95      2000



## Train : Test - 9 : 1

In [116]:
headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol", "Phon", "Phon Pol", "Phon Late Pol", "Phon Long Pol","Phon Mix Pol"]
LIWC_ = [(LIWC2_labels_,LIWC2_scores_),(LIWC3_labels_,LIWC3_scores_),(LIWC6_labels_, LIWC6_scores_),(LIWC9_labels_, LIWC9_scores_),(LIWC12_labels_, LIWC12_scores_)]
tfidf_ = [(tfidf2_labels_,tfidf2_scores_),(tfidf3_labels_,tfidf3_scores_),(tfidf6_labels_, tfidf6_scores_),(tfidf9_labels_, tfidf9_scores_),(tfidf12_labels_, tfidf12_scores_)]
pol_ = [(POL2_labels_,POL2_scores_),(POL3_labels_,POL3_scores_),(POL6_labels_, POL6_scores_),(POL9_labels_, POL9_scores_),(POL12_labels_, POL12_scores_)]
latePol_ = [(latePOL2_labels_,latePOL2_scores_),(latePOL3_labels_,latePOL3_scores_),(latePOL6_labels_, latePOL6_scores_),(latePOL9_labels_, latePOL9_scores_),(latePOL12_labels_, latePOL12_scores_)]
longPol_ = [(longPOL2_labels_,longPOL2_scores_),(longPOL3_labels_,longPOL3_scores_),(longPOL6_labels_, longPOL6_scores_),(longPOL9_labels_, longPOL9_scores_),(longPOL12_labels_, longPOL12_scores_)]
llPol_ = [(llPOL2_labels_,llPOL2_scores_),(llPOL3_labels_,llPOL3_scores_),(llPOL6_labels_, llPOL6_scores_),(llPOL9_labels_, llPOL9_scores_),(llPOL12_labels_, llPOL12_scores_)]

Phon_ = [(Phon2_labels_,Phon2_scores_),(Phon3_labels_,Phon3_scores_),(Phon6_labels_, Phon6_scores_),(Phon9_labels_, Phon9_scores_),(Phon12_labels_, Phon12_scores_)]
PhonPOL_ = [(PhonPOL2_labels_,PhonPOL2_scores_),(PhonPOL3_labels_,PhonPOL3_scores_),(PhonPOL6_labels_, PhonPOL6_scores_),(PhonPOL9_labels_, PhonPOL9_scores_),(PhonPOL12_labels_, PhonPOL12_scores_)]
PhonlatePOL_ = [(PhonlatePOL2_labels_,PhonlatePOL2_scores_),(PhonlatePOL3_labels_,PhonlatePOL3_scores_),(PhonlatePOL6_labels_, PhonlatePOL6_scores_),(PhonlatePOL9_labels_, PhonlatePOL9_scores_),(PhonlatePOL12_labels_, PhonlatePOL12_scores_)]
PhonLongPOL_ = [(PhonLongPOL2_labels_,PhonLongPOL2_scores_),(PhonLongPOL3_labels_,PhonLongPOL3_scores_),(PhonLongPOL6_labels_, PhonLongPOL6_scores_),(PhonLongPOL9_labels_, PhonLongPOL9_scores_),(PhonLongPOL12_labels_, PhonLongPOL12_scores_)]
PhonLLPOL_ = [(PhonLLPOL2_labels_,PhonLLPOL2_scores_),(PhonLLPOL3_labels_,PhonLLPOL3_scores_),(PhonLLPOL6_labels_, PhonLLPOL6_scores_),(PhonLLPOL9_labels_, PhonLLPOL9_scores_),(PhonLLPOL12_labels_, PhonLLPOL12_scores_)]

Total_feature_group = [LIWC_, tfidf_, pol_, latePol_, longPol_, llPol_, Phon_, PhonPOL_, PhonlatePOL_, PhonLongPOL_, PhonLLPOL_]

for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features      2 months    3 months    6 months    9 months    12 months    Average
----------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC          0.402386    0.378065    0.400493    0.382338     0.392371   0.391131
TF-IDF        0.943943    0.94025     0.87572     0.88444      0.844918   0.897854
Pol           0.975766    0.979155    0.973336    0.977153     0.957718   0.972626
Late Pol      0.977653    0.975766    0.977605    0.976152     0.971932   0.975821
Long Pol      0.983474    0.979451    0.963386    0.972583     0.966022   0.972983
Mixed Pol     0.976513    0.979526    0.964145    0.977929     0.966804   0.972983


In [117]:
print(metrics.classification_report(llPOL3_labels_[:,0],map(lambda val: 0 if val <0.5 else 1, llPOL3_scores_)))

             precision    recall  f1-score   support

        0.0       0.93      0.99      0.96      1300
        1.0       0.97      0.86      0.91       700

avg / total       0.94      0.94      0.94      2000



## Train:Test - 7:3

In [207]:
headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol"]
LIWC_ = [(LIWC2_labels_,LIWC2_scores_),(LIWC3_labels_,LIWC3_scores_),(LIWC6_labels_, LIWC6_scores_),(LIWC9_labels_, LIWC9_scores_),(LIWC12_labels_, LIWC12_scores_)]
tfidf_ = [(tfidf2_labels_,tfidf2_scores_),(tfidf3_labels_,tfidf3_scores_),(tfidf6_labels_, tfidf6_scores_),(tfidf9_labels_, tfidf9_scores_),(tfidf12_labels_, tfidf12_scores_)]
pol_ = [(POL2_labels_,POL2_scores_),(POL3_labels_,POL3_scores_),(POL6_labels_, POL6_scores_),(POL9_labels_, POL9_scores_),(POL12_labels_, POL12_scores_)]
latePol_ = [(latePOL2_labels_,latePOL2_scores_),(latePOL3_labels_,latePOL3_scores_),(latePOL6_labels_, latePOL6_scores_),(latePOL9_labels_, latePOL9_scores_),(latePOL12_labels_, latePOL12_scores_)]
longPol_ = [(longPOL2_labels_,longPOL2_scores_),(longPOL3_labels_,longPOL3_scores_),(longPOL6_labels_, longPOL6_scores_),(longPOL9_labels_, longPOL9_scores_),(longPOL12_labels_, longPOL12_scores_)]
llPol_ = [(llPOL2_labels_,llPOL2_scores_),(llPOL3_labels_,llPOL3_scores_),(llPOL6_labels_, llPOL6_scores_),(llPOL9_labels_, llPOL9_scores_),(llPOL12_labels_, llPOL12_scores_)]

Total_feature_group = [LIWC_, tfidf_, pol_, latePol_, longPol_, llPol_]

for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Average Precision Recall Performance

Features      2 months    3 months    6 months    9 months    12 months    Average
----------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC          0.414234    0.395033    0.386851    0.414452     0.362435   0.394601
TF-IDF        0.930859    0.924246    0.881205    0.852544     0.823561   0.882483
Pol           0.972529    0.978279    0.969301    0.970687     0.960747   0.970309
Late Pol      0.969557    0.974121    0.96541     0.971735     0.956233   0.967411
Long Pol      0.977714    0.97448     0.966493    0.967995     0.963496   0.970036
Mixed Pol     0.972895    0.968537    0.964341    0.968589     0.959832   0.966839


In [208]:
print(metrics.classification_report(llPOL3_labels_[:,0],map(lambda val: 0 if val <0.5 else 1, llPOL3_scores_)))

             precision    recall  f1-score   support

        0.0       0.91      0.98      0.95      1540
        1.0       0.96      0.83      0.89       840

avg / total       0.93      0.93      0.93      2380



## Train:Test - 8:2

In [199]:
headers = ["Features","2 months", "3 months", "6 months", "9 months", "12 months","Average"]
contents = []
Feature_name = ["LIWC","TF-IDF","Pol","Late Pol", "Long Pol", "Mixed Pol"]
LIWC_ = [(LIWC2_labels_,LIWC2_scores_),(LIWC3_labels_,LIWC3_scores_),(LIWC6_labels_, LIWC6_scores_),(LIWC9_labels_, LIWC9_scores_),(LIWC12_labels_, LIWC12_scores_)]
tfidf_ = [(tfidf2_labels_,tfidf2_scores_),(tfidf3_labels_,tfidf3_scores_),(tfidf6_labels_, tfidf6_scores_),(tfidf9_labels_, tfidf9_scores_),(tfidf12_labels_, tfidf12_scores_)]
pol_ = [(POL2_labels_,POL2_scores_),(POL3_labels_,POL3_scores_),(POL6_labels_, POL6_scores_),(POL9_labels_, POL9_scores_),(POL12_labels_, POL12_scores_)]
latePol_ = [(latePOL2_labels_,latePOL2_scores_),(latePOL3_labels_,latePOL3_scores_),(latePOL6_labels_, latePOL6_scores_),(latePOL9_labels_, latePOL9_scores_),(latePOL12_labels_, latePOL12_scores_)]
longPol_ = [(longPOL2_labels_,longPOL2_scores_),(longPOL3_labels_,longPOL3_scores_),(longPOL6_labels_, longPOL6_scores_),(longPOL9_labels_, longPOL9_scores_),(longPOL12_labels_, longPOL12_scores_)]
llPol_ = [(llPOL2_labels_,llPOL2_scores_),(llPOL3_labels_,llPOL3_scores_),(llPOL6_labels_, llPOL6_scores_),(llPOL9_labels_, llPOL9_scores_),(llPOL12_labels_, llPOL12_scores_)]

Total_feature_group = [LIWC_, tfidf_, pol_, latePol_, longPol_, llPol_]

for i, group in enumerate(Total_feature_group):
    group_name = Feature_name[i]
    if i == 1: #tfidf's label is different format
        performance_list = [average_precision_score(label, score) for label, score in group]
    else:
        performance_list = [average_precision_score(label[:,0], score) for label, score in group]
    content = [group_name] + performance_list + [np.mean(np.array(performance_list))]
    contents.append(content)
print("Average Precision Recall Performance\n")
print(tabulate(contents, headers=headers))

    

Features      2 months    3 months    6 months    9 months    12 months    Average
----------  ----------  ----------  ----------  ----------  -----------  ---------
LIWC          0.428589    0.383238    0.381273    0.39161      0.365746   0.390091
TF-IDF        0.936085    0.934796    0.869994    0.835952     0.798823   0.87513
Pol           0.973972    0.980086    0.969989    0.978594     0.972266   0.974982
Late Pol      0.973192    0.983356    0.963658    0.978879     0.957948   0.971407
Long Pol      0.980953    0.974796    0.966047    0.972439     0.957879   0.970423
Mixed Pol     0.978632    0.978725    0.96925     0.971874     0.964414   0.972579


In [73]:
metrics.average_precision_score(llPOL3_labels_[:,0],map(lambda val: 0 if val <0.5 else 1, llPOL3_scores_))

0.87269569551958703

In [74]:
metrics.average_precision_score(llPOL3_labels_[:,0], llPOL3_scores_)

0.97303428660432822

In [75]:
metrics.precision_score(llPOL3_labels_[:,0],map(lambda val: 0 if val <0.5 else 1, llPOL3_scores_))

0.96962233169129719

In [76]:
print(metrics.classification_report(llPOL3_labels_[:,0],map(lambda val: 0 if val <0.5 else 1, llPOL3_scores_)))

             precision    recall  f1-score   support

        0.0       0.92      0.99      0.95      2600
        1.0       0.97      0.84      0.90      1400

avg / total       0.94      0.94      0.93      4000



### Traditional POL Comparation from Time Difference

In [71]:
# names = ["PoL(15month)","PoL(12month)", "PoL(9month)", "PoL(6month)","PoL(3month)", "PoL(2month)"]
names = ["PoL(12month)", "PoL(9month)", "PoL(6month)","PoL(3month)", "PoL(2month)"]
# bipolar_SCORES = [POL15_scores, POL12_scores, POL9_scores, POL6_scores, POL3_scores, POL2_scores]
# bipolar_LABELS = [POL15_labels[:,0], POL12_labels[:,0], POL9_labels[:,0], POL6_labels[:,0], POL3_labels[:,0], POL2_labels[:,0]]
bipolar_SCORES = [ POL12_scores, POL9_scores, POL6_scores, POL3_scores, POL2_scores]
bipolar_LABELS = [ POL12_labels[:,0], POL9_labels[:,0], POL6_labels[:,0], POL3_labels[:,0], POL2_labels[:,0]]

renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','solid','solid','solid','solid','solid'], linewidth = 2)

Average Precision
	PoL(12month)    : 0.884935936314
	PoL(9month)     : 0.870315271894
	PoL(6month)     : 0.875405585628
	PoL(3month)     : 0.925993580026
	PoL(2month)     : 0.866071839405


In [72]:
names = ["PoL(12month)", "PoL(9month)", "PoL(6month)","PoL(3month)", "PoL(2month)"]

bipolar_SCORES = [POL12_scores_, POL9_scores_, POL6_scores_, POL3_scores_, POL2_scores_]
bipolar_LABELS = [POL12_labels_[:,0], POL9_labels_[:,0], POL6_labels_[:,0], POL3_labels_[:,0], POL2_labels_[:,0]]

renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','solid','solid','solid','solid','solid'], linewidth = 2)


Average Precision
	PoL(12month)    : 0.960759772896
	PoL(9month)     : 0.980098051289
	PoL(6month)     : 0.964761316616
	PoL(3month)     : 0.973477774671
	PoL(2month)     : 0.980983816104


### Late POL Comparation from Time Difference

In [73]:
# names = ["latePoL(15month)","latePoL(12month)", "latePoL(9month)", "latePoL(6month)","latePoL(3month)", "latePoL(2month)"]
names = ["latePoL(12month)", "latePoL(9month)", "latePoL(6month)","latePoL(3month)", "latePoL(2month)"]

# bipolar_SCORES = [latePOL15_scores, latePOL12_scores, latePOL9_scores, latePOL6_scores, latePOL3_scores, latePOL2_scores]
# bipolar_LABELS = [latePOL15_labels[:,0], latePOL12_labels[:,0], latePOL9_labels[:,0], latePOL6_labels[:,0], latePOL3_labels[:,0], latePOL2_labels[:,0]]
bipolar_SCORES = [latePOL12_scores, latePOL9_scores, latePOL6_scores, latePOL3_scores, latePOL2_scores]
bipolar_LABELS = [latePOL12_labels[:,0], latePOL9_labels[:,0], latePOL6_labels[:,0], latePOL3_labels[:,0], latePOL2_labels[:,0]]


renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','solid','solid','solid','solid','solid'], linewidth = 2)

Average Precision
	latePoL(12month) : 0.887504253098
	latePoL(9month) : 0.902510122164
	latePoL(6month) : 0.926031984601
	latePoL(3month) : 0.918681307021
	latePoL(2month) : 0.853437124602


In [74]:
names = ["latePoL(12month)", "latePoL(9month)", "latePoL(6month)","latePoL(3month)", "latePoL(2month)"]

bipolar_SCORES = [latePOL12_scores_, latePOL9_scores_, latePOL6_scores_, latePOL3_scores_, latePOL2_scores_]
bipolar_LABELS = [latePOL12_labels_[:,0], latePOL9_labels_[:,0], latePOL6_labels_[:,0], latePOL3_labels_[:,0], latePOL2_labels_[:,0]]

renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','solid','solid','solid','solid','solid'], linewidth = 2)

Average Precision
	latePoL(12month) : 0.966473124368
	latePoL(9month) : 0.968868315373
	latePoL(6month) : 0.964492328956
	latePoL(3month) : 0.976913940568
	latePoL(2month) : 0.973371681458


### Long POL Comparation from Time Difference

In [75]:
# names = ["longPoL(15month)","longPoL(12month)", "longPoL(9month)", "longPoL(6month)","longPoL(3month)", "longPoL(2month)"]
names = ["longPoL(12month)", "longPoL(9month)", "longPoL(6month)","longPoL(3month)", "longPoL(2month)"]

# bipolar_SCORES = [longPOL15_scores, longPOL12_scores, longPOL9_scores, longPOL6_scores, longPOL3_scores, longPOL2_scores]
# bipolar_LABELS = [longPOL15_labels[:,0], longPOL12_labels[:,0], longPOL9_labels[:,0], longPOL6_labels[:,0], longPOL3_labels[:,0], longPOL2_labels[:,0]]
bipolar_SCORES = [longPOL12_scores, longPOL9_scores, longPOL6_scores, longPOL3_scores, longPOL2_scores]
bipolar_LABELS = [longPOL12_labels[:,0], longPOL9_labels[:,0], longPOL6_labels[:,0], longPOL3_labels[:,0], longPOL2_labels[:,0]]

renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','solid','solid','solid','solid','solid'], linewidth = 1.5)


Average Precision
	longPoL(12month) : 0.899073742677
	longPoL(9month) : 0.897580616529
	longPoL(6month) : 0.890981864813
	longPoL(3month) : 0.909577449916
	longPoL(2month) : 0.876513065134


In [76]:
names = ["longPoL(12month)", "longPoL(9month)", "longPoL(6month)","longPoL(3month)", "longPoL(2month)"]

bipolar_SCORES = [longPOL12_scores_, longPOL9_scores_, longPOL6_scores_, longPOL3_scores_, longPOL2_scores_]
bipolar_LABELS = [longPOL12_labels_[:,0], longPOL9_labels_[:,0], longPOL6_labels_[:,0], longPOL3_labels_[:,0], longPOL2_labels_[:,0]]

renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','solid','solid','solid','solid','solid'], linewidth = 1.5)


Average Precision
	longPoL(12month) : 0.955436897364
	longPoL(9month) : 0.976147031094
	longPoL(6month) : 0.965668081843
	longPoL(3month) : 0.976462487264
	longPoL(2month) : 0.980629506094


### Compare LIWC

In [77]:
# names = ["LIWC(15month)","LIWC(12month)", "LIWC(9month)", "LIWC(6month)","LIWC(3month)", "LIWC(2month)"]
names = ["LIWC(12month)", "LIWC(9month)", "LIWC(6month)","LIWC(3month)", "LIWC(2month)"]

# bipolar_SCORES = [LIWC15_scores, LIWC12_scores, LIWC9_scores, LIWC6_scores, LIWC3_scores, LIWC2_scores]
# bipolar_LABELS = [LIWC15_labels[:,0], LIWC12_labels[:,0], LIWC9_labels[:,0], LIWC6_labels[:,0], LIWC3_labels[:,0], LIWC2_labels[:,0]]

bipolar_SCORES = [LIWC12_scores, LIWC9_scores, LIWC6_scores, LIWC3_scores, LIWC2_scores]
bipolar_LABELS = [LIWC12_labels[:,0], LIWC9_labels[:,0], LIWC6_labels[:,0], LIWC3_labels[:,0], LIWC2_labels[:,0]]

renderPRC(bipolar_SCORES, bipolar_LABELS, name, names)

Average Precision
	LIWC(12month)   : 0.360210986154
	LIWC(9month)    : 0.372182678079
	LIWC(6month)    : 0.430480468793
	LIWC(3month)    : 0.405881443759
	LIWC(2month)    : 0.387128591679


In [78]:
names = ["LIWC(12month)", "LIWC(9month)", "LIWC(6month)","LIWC(3month)", "LIWC(2month)"]

bipolar_SCORES = [LIWC12_scores_, LIWC9_scores_, LIWC6_scores_, LIWC3_scores_, LIWC2_scores_]
bipolar_LABELS = [LIWC12_labels_[:,0], LIWC9_labels_[:,0], LIWC6_labels_[:,0], LIWC3_labels_[:,0], LIWC2_labels_[:,0]]

renderPRC(bipolar_SCORES, bipolar_LABELS, name, names)

Average Precision
	LIWC(12month)   : 0.421415867376
	LIWC(9month)    : 0.473327947425
	LIWC(6month)    : 0.360160840787
	LIWC(3month)    : 0.380409884094
	LIWC(2month)    : 0.44080523774


### TFIDF

In [79]:
# names = ["tfidf(15month)","tfidf(12month)", "tfidf(9month)", "tfidf(6month)","tfidf(3month)", "tfidf(2month)"]
names = ["tfidf(12month)", "tfidf(9month)", "tfidf(6month)","tfidf(3month)", "tfidf(2month)"]

# bipolar_SCORES = [tfidf15_scores, tfidf12_scores, tfidf9_scores, tfidf6_scores, tfidf3_scores, tfidf2_scores]
# bipolar_LABELS = [tfidf15_labels, tfidf12_labels, tfidf9_labels, tfidf6_labels, tfidf3_labels, tfidf2_labels]

bipolar_SCORES = [tfidf12_scores, tfidf9_scores, tfidf6_scores, tfidf3_scores, tfidf2_scores]
bipolar_LABELS = [tfidf12_labels, tfidf9_labels, tfidf6_labels, tfidf3_labels, tfidf2_labels]


renderPRC(bipolar_SCORES, bipolar_LABELS, name, names)

Average Precision
	tfidf(12month)  : 0.839130206111
	tfidf(9month)   : 0.854807897295
	tfidf(6month)   : 0.879923691644
	tfidf(3month)   : 0.884599381724
	tfidf(2month)   : 0.852423447744


In [197]:
graph_data = []
# dash options include 'dash', 'dot', and 'dashdot'

precision, recall, _ = precision_recall_curve(tfidf12_labels_, tfidf12_scores_, pos_label=1)
graph_data.append(Scatter(x=recall,y=precision,name='tfidf(12month)',mode = 'lines+markers', line=dict(width = 2)))

precision, recall, _ = precision_recall_curve(tfidf9_labels_, tfidf9_scores_, pos_label=1)
graph_data.append(Scatter(x=recall,y=precision,name='tfidf(9month)',line = dict(dash = 'dot')))

precision, recall, _ = precision_recall_curve(tfidf6_labels_, tfidf6_scores_, pos_label=1)
graph_data.append(Scatter(x=recall,y=precision,name='tfidf(6month)',line = dict(dash = 'dashdot')))

precision, recall, _ = precision_recall_curve(tfidf3_labels_, tfidf3_scores_, pos_label=1)
graph_data.append(Scatter(x=recall,y=precision,name='tfidf(3month)',line = dict(dash = 'dash')))

precision, recall, _ = precision_recall_curve(tfidf2_labels_, tfidf2_scores_, pos_label=1)
graph_data.append(Scatter(x=recall,y=precision,name='tfidf(2month)'))

iplot(graph_data)

# import plotly.plotly as py
# fig = go.Figure(data=graph_data, layout=layout)
# py.image.save_as(fig, filename='a-simple-plot.png')


In [196]:
names = ["tfidf(12month)", "tfidf(9month)", "tfidf(6month)","tfidf(3month)", "tfidf(2month)"]

bipolar_SCORES = [tfidf12_scores_, tfidf9_scores_, tfidf6_scores_, tfidf3_scores_, tfidf2_scores_]
bipolar_LABELS = [tfidf12_labels_, tfidf9_labels_, tfidf6_labels_, tfidf3_labels_, tfidf2_labels_]

renderPRC(bipolar_SCORES, bipolar_LABELS, name, names)

Average Precision
	tfidf(12month)  : 0.802966073768
	tfidf(9month)   : 0.850732194034
	tfidf(6month)   : 0.864826469667
	tfidf(3month)   : 0.92035181628
	tfidf(2month)   : 0.936450655303


### Compare POL, LIWC, TFIDF

In [88]:
names = ["PoL(15month)", "TFIDF(15month)", "LIWC(15month)"]

bipolar_SCORES = [POL15_scores, tfidf15_scores, LIWC15_scores]
bipolar_LABELS = [POL15_labels[:,0], tfidf15_labels, LIWC15_labels[:,0]]

# renderROC(bipolar_SCORES, bipolar_LABELS, name,names, linestyle=['solid','dashed','dotted','solid','dashdot','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])  
renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','dashed','dotted','solid','dashdot','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])

NameError: name 'POL15_scores' is not defined

In [89]:
names = ["PoL(15month)", "latePoL(15month)", "LongPoL(15month)", "TFIDF(15month)", "LIWC(15month)"]

bipolar_SCORES = [POL15_scores, latePOL15_scores, longPOL15_scores, tfidf15_scores, LIWC15_scores]
bipolar_LABELS = [POL15_labels[:,0], latePOL15_labels[:,0], longPOL15_labels[:,0], tfidf15_labels, LIWC15_labels[:,0]]

# renderROC(bipolar_SCORES, bipolar_LABELS, name,names, linestyle=['dashdot',':','--','solid','dashed','','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])  
renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','solid','solid','dashdot','dashed','solid','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])

NameError: name 'POL15_scores' is not defined

In [89]:
names = ["PoL(12month)", "latePoL(12month)", "LongPoL(12month)", "LaLoPoL(12month)", "TFIDF(12month)", "LIWC(12month)"]

bipolar_scores_ = [POL12_scores_, latePOL12_scores_, longPOL12_scores_, llPOL12_scores_, tfidf12_scores_, LIWC12_scores_]
bipolar_labels_ = [POL12_labels_[:,0], latePOL12_labels_[:,0], longPOL12_labels_[:,0], llPOL12_labels_[:,0], tfidf12_labels_, LIWC12_labels_[:,0]]

renderPRC(bipolar_scores_, bipolar_labels_, name, names, linestyle=['solid','solid','solid','dashdot','dashed','solid','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])

Average Precision
	PoL(12month)    : 0.971581277458
	latePoL(12month) : 0.967207161529
	LongPoL(12month) : 0.968652846293
	LaLoPoL(12month) : 0.966266988381
	TFIDF(12month)  : 0.814160824346
	LIWC(12month)   : 0.392912624399


In [143]:
names = ["PoL(3month)", "latePoL(3month)", "LongPoL(3month)", "TFIDF(3month)", "LIWC(3month)"]

bipolar_SCORES = [POL3_scores, latePOL3_scores, longPOL3_scores, tfidf3_scores, LIWC3_scores]
bipolar_LABELS = [POL3_labels[:,0], latePOL3_labels[:,0], longPOL3_labels[:,0], tfidf3_labels, LIWC3_labels[:,0]]

# renderROC(bipolar_SCORES, bipolar_LABELS, name,names, linestyle=['dashdot',':','--','solid','dashed','','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])  
renderPRC(bipolar_SCORES, bipolar_LABELS, name, names, linestyle=['solid','solid','solid','dashdot','dashed','solid','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])

Average Precision
	PoL(3month)     : 0.899133076773
	latePoL(3month) : 0.910785242361
	LongPoL(3month) : 0.899268642249
	TFIDF(3month)   : 0.845006381428
	LIWC(3month)    : 0.421582016


In [90]:
names = ["PoL(3month)", "latePoL(3month)", "LongPoL(3month)", "LaLo(3month)", "TFIDF(3month)", "LIWC(3month)"]

bipolar_scores_ = [POL3_scores_, latePOL3_scores_, longPOL3_scores_, llPOL3_scores_, tfidf3_scores_, LIWC3_scores_]
bipolar_labels_ = [POL3_labels_[:,0], latePOL3_labels_[:,0], longPOL3_labels_[:,0], llPOL3_labels_[:,0], tfidf3_labels_, LIWC3_labels_[:,0]]

renderPRC(bipolar_scores_, bipolar_labels_, name, names, linestyle=['solid','solid','solid','dashdot','dashed','solid','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])

Average Precision
	PoL(3month)     : 0.98378180787
	latePoL(3month) : 0.983045798766
	LongPoL(3month) : 0.98356272731
	LaLo(3month)    : 0.98096692879
	TFIDF(3month)   : 0.93671428241
	LIWC(3month)    : 0.391290578472


In [91]:
names = ["PoL(2month)", "latePoL(2month)", "LongPoL(2month)", "LaLoPoL(2month)", "TFIDF(2month)", "LIWC(2month)"]

bipolar_scores_ = [POL2_scores_, latePOL2_scores_, longPOL2_scores_, llPOL2_scores_, tfidf2_scores_, LIWC2_scores_]
bipolar_labels_ = [POL2_labels_[:,0], latePOL2_labels_[:,0], longPOL2_labels_[:,0], llPOL2_labels_[:,0], tfidf2_labels_, LIWC2_labels_[:,0]]

renderPRC(bipolar_scores_, bipolar_labels_, name, names, linestyle=['solid','solid','solid','dashdot','dashed','solid','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])

Average Precision
	PoL(2month)     : 0.982063560121
	latePoL(2month) : 0.979784336483
	LongPoL(2month) : 0.979962293088
	LaLoPoL(2month) : 0.982168439294
	TFIDF(2month)   : 0.932824547342
	LIWC(2month)    : 0.431306288974


In [92]:
names = ["PoL(6month)", "latePoL(6month)", "LongPoL(6month)", "LaLoPoL(6month)", "TFIDF(6month)", "LIWC(6month)"]

bipolar_scores_ = [POL6_scores_, latePOL6_scores_, longPOL6_scores_, llPOL6_scores_, tfidf6_scores_, LIWC6_scores_]
bipolar_labels_ = [POL6_labels_[:,0], latePOL6_labels_[:,0], longPOL6_labels_[:,0], llPOL6_labels_[:,0], tfidf6_labels_, LIWC6_labels_[:,0]]

renderPRC(bipolar_scores_, bipolar_labels_, name, names, linestyle=['solid','solid','solid','dashdot','dashed','solid','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])

Average Precision
	PoL(6month)     : 0.969025192928
	latePoL(6month) : 0.96487024506
	LongPoL(6month) : 0.965307394315
	LaLoPoL(6month) : 0.96117403782
	TFIDF(6month)   : 0.862366946854
	LIWC(6month)    : 0.400579274231


In [93]:
names = ["PoL(9month)", "latePoL(9month)", "LongPoL(9month)", "LaLoPoL(9month)", "TFIDF(9month)", "LIWC(9month)"]

bipolar_scores_ = [POL9_scores_, latePOL9_scores_, longPOL9_scores_, llPOL9_scores_, tfidf9_scores_, LIWC9_scores_]
bipolar_labels_ = [POL9_labels_[:,0], latePOL9_labels_[:,0], longPOL9_labels_[:,0], llPOL9_labels_[:,0], tfidf9_labels_, LIWC9_labels_[:,0]]

renderPRC(bipolar_scores_, bipolar_labels_, name, names, linestyle=['solid','solid','solid','dashdot','dashed','solid','--','dashed','dotted'], colors = ['b','r','g',"y","c","m","#f4b642","#777777"])

Average Precision
	PoL(9month)     : 0.97508145364
	latePoL(9month) : 0.972776525005
	LongPoL(9month) : 0.973030902014
	LaLoPoL(9month) : 0.980115334214
	TFIDF(9month)   : 0.850899415668
	LIWC(9month)    : 0.42958684666


In [96]:
names = ["PoL(15month)", "PoL(9month)", "PoL(3month)", "PoL(2month)", "TFIDF(15month)", "TFIDF(9month)", "TFIDF(3month)", "TFIDF(2month)"]

bipolar_SCORES = [POL15_scores, POL9_scores, POL3_scores, POL2_scores,
                  tfidf15_scores, tfidf9_scores, tfidf3_scores, tfidf2_scores]
bipolar_LABELS = [POL15_labels[:,0], POL9_labels[:,0], POL3_labels[:,0], POL2_labels[:,0], 
                  tfidf15_labels, tfidf9_labels, tfidf3_labels, tfidf2_labels]

# renderROC(bipolar_SCORES, bipolar_LABELS, name,names)  
renderPRC(bipolar_SCORES, bipolar_LABELS, name, names)

# latePOL_scores, latePOL_labels, _ = pol_groups.getLabelsScores(name, classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = "short")
# LongPOL_scores, LongPOL_labels, _ = pol_groups.getLabelsScores(name, classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = "short")



NameError: name 'POL15_scores' is not defined

In [97]:
names = ["latePoL(15month)", "latePoL(9month)", "latePoL(3month)", "latePoL(2month)", "TFIDF(15month)", "TFIDF(9month)", "TFIDF(3month)", "TFIDF(2month)"]

bipolar_SCORES = [POL15_scores, POL9_scores, POL3_scores, POL2_scores,
                  tfidf15_scores, tfidf9_scores, tfidf3_scores, tfidf2_scores]
bipolar_LABELS = [POL15_labels[:,0], POL9_labels[:,0], POL3_labels[:,0], POL2_labels[:,0], 
                  tfidf15_labels, tfidf9_labels, tfidf3_labels, tfidf2_labels]

# renderROC(bipolar_SCORES, bipolar_LABELS, name,names)  
renderPRC(bipolar_SCORES, bipolar_LABELS, name, names)

NameError: name 'POL15_scores' is not defined

In [98]:
names = ["longPoL(15month)", "longPoL(9month)", "longPoL(3month)", "longPoL(2month)", "TFIDF(15month)", "TFIDF(9month)", "TFIDF(3month)", "TFIDF(2month)"]
bipolar_SCORES = [POL15_scores, POL9_scores, POL3_scores, POL2_scores,
                  tfidf15_scores, tfidf9_scores, tfidf3_scores, tfidf2_scores]
bipolar_LABELS = [POL15_labels[:,0], POL9_labels[:,0], POL3_labels[:,0], POL2_labels[:,0], 
                  tfidf15_labels, tfidf9_labels, tfidf3_labels, tfidf2_labels]

# renderROC(bipolar_SCORES, bipolar_LABELS, name,names)  
renderPRC(bipolar_SCORES, bipolar_LABELS, name, names)

NameError: name 'POL15_scores' is not defined

In [99]:
# Old
# names = ["PoL(GB)", "LIWC(GB)", "TF-IDF(GB)", "PoL", "time-PoL(late)", "time-PoL", "LIWC", "TF-IDF"]
# GBPOL_scores, GBPOL_labels, _ = pol_groups.getLabelsScores(name, classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = "long")
# POL_scores, POL_labels, _ = pol_groups.getLabelsScores(name, classifier,n_fold=n_fold, selection=GBPOL_selection, consider_time = "short")
# LongLIWC_scores, LongLIWC_labels, _ = pol_groups.getLabelsScores(name, classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = "long")
# LIWC_scores, LIWC_labels, _ = pol_groups.getLabelsScores(name, classifier,n_fold=n_fold, selection=LIWC_selection, consider_time = "short")
# latePOL_scores, latePOL_labels, _ = pol_groups.getLabelsScores(name, classifier,n_fold=n_fold, selection=latePOL_selection, consider_time = "short")
# LongPOL_scores, LongPOL_labels, _ = pol_groups.getLabelsScores(name, classifier,n_fold=n_fold, selection=LongPOL_selection, consider_time = "short")
# Longtfidf_scores, Longtfidf_labels, _ = tfidf_groups.getLabelsScores("Long_Bipolar", classifier,n_fold=n_fold, consider_time = "long")
# tfidf_scores, tfidf_labels, _ = tfidf_groups.getLabelsScores(name, classifier,n_fold=n_fold, consider_time = "short")

# bipolar_SCORES = [GBPOL_scores, LongLIWC_scores, Longtfidf_scores, POL_scores, latePOL_scores, LongPOL_scores , LIWC_scores, tfidf_scores]
# bipolar_LABELS = [GBPOL_labels[:,0], LongLIWC_labels[:,0], Longtfidf_labels, POL_labels[:,0], latePOL_labels[:,0], LongPOL_labels[:,0], LIWC_labels[:,0], tfidf_labels]
# bipolar_NAMES =  [GBPOL_labels[:,1], LIWC_labels[:,1], latePOL_labels[:,1], POL_labels[:,1], LongPOL_labels[:,1]]

# renderROC(bipolar_SCORES, bipolar_LABELS, name,names)  
# renderPRC(bipolar_SCORES, bipolar_LABELS, name, names)

### Compare Dataset by TFIDF Model

In [157]:
# Load model
tfidf_rf_classifier = joblib.load("models/tfidf/tfidf_forest_classifier")
# tfidf_text_model = joblib.load("models/tfidf/tfidf_text_model_new")

/media/yenhao/blue/research/tweets_server/local/lib/python2.7/site-packages/sklearn/base.py:312: UserWarning:

Trying to unpickle estimator DecisionTreeClassifier from version 0.18.1 when using version 0.19.0. This might lead to breaking code or invalid results. Use at your own risk.

/media/yenhao/blue/research/tweets_server/local/lib/python2.7/site-packages/sklearn/base.py:312: UserWarning:

Trying to unpickle estimator RandomForestClassifier from version 0.18.1 when using version 0.19.0. This might lead to breaking code or invalid results. Use at your own risk.



In [158]:
import scipy.sparse as sp

idfs = np.load("models/tfidf/idf.npy")

# subclass TfidfVectorizer
class MyVectorizer(TfidfVectorizer):
    # plug our pre-computed IDFs
    TfidfVectorizer.idf_ = idfs
    
# instantiate vectorizer
text_model = MyVectorizer(stop_words="english", 
                          ngram_range = (1,2))


# plug _tfidf._idf_diag
text_model._tfidf._idf_diag = sp.spdiags(idfs,
                                         diags = 0,
                                         m = len(idfs),
                                         n = len(idfs))

vocabulary = json.load(open('models/tfidf/vocabulary.json', mode = 'rb'))
text_model.vocabulary_ = vocabulary

In [159]:

feature_indicies = np.argsort(tfidf_rf_classifier.feature_importances_)
vector2word = text_model.get_feature_names()
top_words = []
for i in range(50):
    vector = feature_indicies[-i-1]
    word = vector2word[vector]
    top_words.append(word)

In [160]:
print(top_words)

[u'bipolar', u'mental illness', u'mental', u'therapy', u'diagnosed', u'coping', u'health issues', u'disorder', u'stigma', u'disability', u'mania', u'mental health', u'bipolardisorder', u'life bipolar', u'antidepressants', u'borderline', u'nami', u'manic', u'bpd', u'helping', u'timetochange', u'mentally', u'meds', u'pills', u'reading', u'depressive', u'manic episode', u'psych', u'exercise', u'anxiety', u'psychiatrist', u'diagnosis', u'blogs', u'suicide', u'nurse_w_glasses', u'personality disorder', u'struggling', u'stable', u'article', u'tickets', u'self', u'stress', u'share', u'survivors', u'manic depression', u'new blog', u'anxious', u'depression', u'hypomania', u'mentally ill']


In [161]:
def del_url(line):
    return re.sub(r'(\S*(\.com)\S*)|(https?:\/\/\S*)', "", line)

In [164]:
name_list = [2,3,6,9,12]
bipolar_group_list = [bipolar2_group, bipolar3_group, bipolar6_group, bipolar9_group, bipolar12_group]
for i, groups in enumerate(bipolar_group_list):
    X = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in groups.getGroup()])
    print('Recall of {:>2d} month data : {}'.format(name_list[i], tfidf_rf_classifier.predict(X).mean()))

Recall of  2 month data : 0.210526315789
Recall of  3 month data : 0.222222222222
Recall of  6 month data : 0.193548387097
Recall of  9 month data : 0.213675213675
Recall of 12 month data : 0.234234234234


## Compare by different Classifier Via Recent Diagnosed Data

Baseline & Out Approach

In [76]:
name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"]
time_list = [2,3,6,9,12]
def getTFIDFClassifier(name = 'Bipolar', tfidf_groups = tfidf_groups_, consider_time = 2):
    group_id = tfidf_groups.name_to_index[name + '_' + str(consider_time)]
    group = tfidf_groups.groups[group_id]
    X = tfidf_groups.text_models[group_id].transform(tfidf_groups.base.getTexts()+group.getTexts())
    Y =  np.array([0] * tfidf_groups.base.getSize() + [1] * group.getSize())
    
    classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
    classifier.fit(X,Y)
    
    return classifier

def getClassifier( feature_group, name, selection="all", consider_time = 'short', n_fold = 20):
    classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
    
    X, Y = feature_group.getLabeledData( name, selection=selection, consider_time= consider_time)

    sss = StratifiedShuffleSplit(Y[:,0], n_fold, test_size = 0.1, random_state=randint(0,65536) )
    
    classifiers = []
    for train_index, test_index in sss:
        X_train, X_test           = X[train_index], X[test_index]
        Y_train, Y_test           = Y[train_index][:,0], Y[test_index][:,0]

        classifier.fit(X_train, Y_train)
        classifiers.append(classifier)

    return classifiers


def renderPrecision(selection, 
                    base_feature, 
                    pol_groups = pol_groups_, 
                    name_list = name_list, 
                    time_list = time_list, 
                    Y = None):
    test_feature = base_feature[:,selection]
    classifiers_list = [getClassifier(pol_groups, name, selection = selection, consider_time = time_list[i]) for i, name in enumerate(name_list)] 
    result_list = []
    if Y == None:
        for i, classifiers in enumerate(classifiers_list):
            SCORES = np.array([])
            for classifier in classifiers:
                SCORES = np.concatenate((SCORES, classifier.predict(test_feature)))
            result_list.append(SCORES.mean())
        return result_list
    else:
        for i, classifiers in enumerate(classifiers_list):
            SCORES = np.array([])
            for classifier in classifiers:
                SCORES = np.concatenate((SCORES, average_precision_score(Y, classifier.predict(test_feature))))
            result_list.append(SCORES.mean())
        return result_list

In [77]:
# Testing Data organize 
def getTestFeatures(recent_group):
    feature2categories = getCategories(recent_group)
    feature_dict = getAllFeature(recent_group)
    index2feature = []
    base_feature = np.zeros((recent_group.getSize(),len(feature_dict)), dtype = float)
    for name, values in feature_dict.items():
        cursor = len(index2feature)
        base_feature[:,cursor] = values
        category = feature2categories[name]
        index2feature.append((name, category))

    return base_feature

### Time Period Feature Classifier

### Baseline Classifier

In [73]:
gb_thesis_classifier = joblib.load('models/bipolar_forest/bipolar_forest_gb_thesis')
GB_Thesis_selection = [4, 10, 11, 12, 13, 15, 18, 22, 25, 35, 39, 46, 52, 60, 17, 65, 66, 69, 78]

### Table

In [101]:
tfidf_classifiers = [getTFIDFClassifier(consider_time = 2), 
                    getTFIDFClassifier(consider_time = 3), 
                    getTFIDFClassifier(consider_time = 6), 
                    getTFIDFClassifier(consider_time = 9), 
                    getTFIDFClassifier(consider_time = 12), 
                    getTFIDFClassifier(consider_time = 15)]

In [74]:
tfidf_classifiers_ = [getTFIDFClassifier(name = 'Bd', tfidf_groups = tfidf_groups_, consider_time = 2), 
                    getTFIDFClassifier(name = 'Bd', tfidf_groups = tfidf_groups_, consider_time = 3), 
                    getTFIDFClassifier(name = 'Bd', tfidf_groups = tfidf_groups_, consider_time = 6), 
                    getTFIDFClassifier(name = 'Bd', tfidf_groups = tfidf_groups_, consider_time = 9), 
                    getTFIDFClassifier(name = 'Bd', tfidf_groups = tfidf_groups_, consider_time = 12)]

In [103]:
b_feature = getTestFeatures(recent_group5)
r_feature = getTestFeatures(test_regular_group5)
X = np.concatenate((b_feature, r_feature))
Y = np.array([1]*b_feature.shape[0] + [0]*r_feature.shape[0])

In [104]:
text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in recent_group5.getGroup()] +
                                              ["\n".join(map(lambda x : del_url(x), group.text)) for group in test_regular_group5.getGroup()])

In [105]:
# indices = np.argsort(text_model.idf_)[::-1]
# features = text_model.get_feature_names()
# top_n = 1000
# top_features = [features[i] for i in indices[:top_n]]
# print top_features

In [130]:
# skip last 2 month
# headers = ["Feature","2 month", "3 month","6 month","9 month", "12 month", "15 month"]
# feature_names = ['Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'LIWC', 'TFIDF','TFIDFxLPol']
# selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LIWC_selection, 'tfidf','Mix']
# test_datasets = [(recent_group5, test_regular_group5), (recent_group4, test_regular_group4), (recent_group3, test_regular_group3)]
# dataset_names = ['Recent 4.x-2.x month', 'Recent 4-2 month', 'Recent 3-2 month']
# time_list = [2,3,6,9,12,15]
# name_list = ["Bipolar_2", "Bipolar_3", "Bipolar_6", "Bipolar_9", "Bipolar_12", "Bipolar_15"]


# """
# Different period datasets
# """
# for j,dataset in enumerate(test_datasets):
#     print("\n===== " + dataset_names[j] + " =====\n")
#     contents = []
#     """
#     Different feature
    
#     This will show one row's result
#     """
# #     test_feature = getTestFeatures(dataset[0]) + getTestFeatures(dataset[1])
#     b_feature = getTestFeatures(dataset[0])
#     r_feature = getTestFeatures(dataset[1])
#     X = np.concatenate((b_feature, r_feature))
#     Y = np.array([1]*b_feature.shape[0] + [0]*r_feature.shape[0])
#     for i, selection in enumerate(selections):
#         feature_name = feature_names[i]
#         if i ==0:
#             predict_result = gb_thesis_classifier.predict(X[:,selection])
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==1:
#             text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                               ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#             predict_result = tfidf_rf_classifier.predict(text_array)
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==6:
#             precision_list = []
#             for k, classifier in enumerate(tfidf_classifiers):
#                 text_array = tfidf_groups.text_models[6+k].transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                                                      ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#                 predict_result = tfidf_classifiers[k].predict(text_array)
#                 precision_list.append(average_precision_score(Y, predict_result))
#         else:
#             precision_list = renderPrecision(selection, X)
#         contents.append([feature_name] + precision_list)

#     print(tabulate(contents, headers=headers, numalign="right"))

In [ ]:
# Dataset: before diagnosed
# skip last 2 month
# headers = ["Feature","2 month", "3 month","6 month","9 month", "12 month"]
# feature_names = ['Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'LIWC', 'TFIDF','TFIDFxLPol']
# selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LIWC_selection, 'tfidf','Mix']
# test_datasets = [(recent_group5, test_regular_group5), (recent_group4, test_regular_group4), (recent_group3, test_regular_group3)]
# dataset_names = ['Recent 4.x-2.x month', 'Recent 4-2 month', 'Recent 3-2 month']
# time_list = [2,3,6,9,12]
# name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"]
# """
# Different period datasets
# """
# for j,dataset in enumerate(test_datasets):
#     print("\n===== " + dataset_names[j] + " =====\n")
#     contents = []
#     """
#     Different feature
    
#     This will show one row's result
#     """
#     b_feature = getTestFeatures(dataset[0])
#     r_feature = getTestFeatures(dataset[1])
#     X = np.concatenate((b_feature, r_feature))
#     Y = np.array([1]*b_feature.shape[0] + [0]*r_feature.shape[0])
#     for i, selection in enumerate(selections[:-1]):
#         feature_name = feature_names[i]
#         if i ==0:
#             predict_result = gb_thesis_classifier.predict(X[:,selection])
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==1:
#             text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                               ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#             predict_result = tfidf_rf_classifier.predict(text_array)
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==6:
#             precision_list = []
#             for k, classifier in enumerate(tfidf_classifiers_):
#                 text_array = tfidf_groups_.text_models[5+k].transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                                                      ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#                 predict_result = classifier.predict(text_array)
#                 precision_list.append(average_precision_score(Y, predict_result))
#         else:
#             precision_list = renderPrecision(selection, X, pol_groups = pol_groups_, name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"])
#         contents.append([feature_name] + precision_list)
    

#     print(tabulate(contents, headers=headers, numalign="right"))

In [ ]:
# skip last one month
# headers = ["Feature","2 month", "3 month","6 month","9 month", "12 month", "15 month"]
# feature_names = ['Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'LIWC', 'TFIDF']
# selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LIWC_selection, 'tfidf']
# test_datasets = [(recent_group5, test_regular_group5), (recent_group4, test_regular_group4), (recent_group3, test_regular_group3), (recent_group2, test_regular_group2)]
# dataset_names = ['Recent 4.x month', 'Recent 4 month', 'Recent 3 month', 'Recent 2 month']
# time_list = [2,3,6,9,12,15]
# name_list = ["Bipolar_2", "Bipolar_3", "Bipolar_6", "Bipolar_9", "Bipolar_12", "Bipolar_15"]

# """
# Different period datasets
# """
# for j,dataset in enumerate(test_datasets):
#     print("\n===== " + dataset_names[j] + " =====\n")
#     contents = []
#     """
#     Different feature
    
#     This will show one row's result
#     """
# #     test_feature = getTestFeatures(dataset[0]) + getTestFeatures(dataset[1])
#     Nd = getTestFeatures(dataset[1])
#     Rd = getTestFeatures(dataset[0])
    
#     X = np.concatenate((Rd, Nd))
#     Y = np.array([1]*25 + [0]*50)
#     for i, selection in enumerate(selections):
#         feature_name = feature_names[i]
#         if i ==0:
#             predict_result = gb_thesis_classifier.predict(X[:,selection])
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==1:
#             text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                               ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#             predict_result = tfidf_rf_classifier.predict(text_array)
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==6:
#             precision_list = []
#             for k, classifier in enumerate(tfidf_classifiers):
#                 text_array = tfidf_groups.text_models[6+k].transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                                                      ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#                 predict_result = tfidf_classifiers[k].predict(text_array)
#                 precision_list.append(average_precision_score(Y, predict_result))
#         else:
#             precision_list = renderPrecision(selection, X)
#         contents.append([feature_name] + precision_list)

#     print(tabulate(contents, headers=headers, numalign="right"))

In [79]:
# Dataset: before diagnosed
# skip last one month
# headers = ["Feature","2 month", "3 month","6 month","9 month", "12 month"]
# feature_names = ['Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'LIWC', 'TFIDF']
# selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LIWC_selection, 'tfidf']
# test_datasets = [(recent_group5, test_regular_group5), (recent_group4, test_regular_group4), (recent_group3, test_regular_group3), (recent_group2, test_regular_group2)]
# dataset_names = ['Recent 4.x month', 'Recent 4 month', 'Recent 3 month', 'Recent 2 month']
# time_list = [2,3,6,9,12]
# name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"]
# """
# Different period datasets
# """
# for j,dataset in enumerate(test_datasets):
#     print("\n===== " + dataset_names[j] + " =====\n")
#     contents = []
#     """
#     Different feature
    
#     This will show one row's result
#     """
#     b_feature = getTestFeatures(dataset[0])
#     r_feature = getTestFeatures(dataset[1])
#     X = np.concatenate((b_feature, r_feature))
#     Y = np.array([1]*b_feature.shape[0] + [0]*r_feature.shape[0])
#     for i, selection in enumerate(selections):
#         feature_name = feature_names[i]
#         if i ==0:
#             predict_result = gb_thesis_classifier.predict(X[:,selection])
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==1:
#             text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                               ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#             predict_result = tfidf_rf_classifier.predict(text_array)
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==6:
#             precision_list = []
#             for k, classifier in enumerate(tfidf_classifiers_):
#                 text_array = tfidf_groups_.text_models[5+k].transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                                                      ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#                 predict_result = classifier.predict(text_array)
#                 precision_list.append(average_precision_score(Y, predict_result))
#         else:
#             precision_list = renderPrecision(selection, X, pol_groups = pol_groups_, name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"])
#         contents.append([feature_name] + precision_list)
    

#     print(tabulate(contents, headers=headers, numalign="right"))

In [129]:
# Fully 4.x month

# headers = ["Feature","2 month", "3 month","6 month","9 month", "12 month", "15 month"]
# feature_names = ['Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'LIWC', 'TFIDF']
# selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LIWC_selection, 'tfidf']
# test_datasets = [(recent_group5, test_regular_group5), (recent_group4, test_regular_group4), (recent_group3, test_regular_group3), (recent_group2, test_regular_group2)]
# dataset_names = ['Recent 4.x month', 'Recent 4 month', 'Recent 3 month', 'Recent 2 month']
# time_list = [2,3,6,9,12,15]
# name_list = ["Bipolar_2", "Bipolar_3", "Bipolar_6", "Bipolar_9", "Bipolar_12", "Bipolar_15"]


# """
# Different period datasets
# """
# for j,dataset in enumerate(test_datasets):
#     print("\n===== " + dataset_names[j] + " =====\n")
#     contents = []
#     """
#     Different feature
    
#     This will show one row's result
#     """
# #     test_feature = getTestFeatures(dataset[0]) + getTestFeatures(dataset[1])
#     X = np.concatenate((getTestFeatures(dataset[0]), getTestFeatures(dataset[1])))
#     Y = np.array([1]*25 + [0]*50)
#     for i, selection in enumerate(selections):
#         feature_name = feature_names[i]
#         if i ==0:
#             predict_result = gb_thesis_classifier.predict(X[:,selection])
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==1:
#             text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                               ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#             predict_result = tfidf_rf_classifier.predict(text_array)
#             precision_list = ['N/A', 'N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
#         elif i ==6:
#             precision_list = []
#             for k, classifier in enumerate(tfidf_classifiers):
#                 text_array = tfidf_groups.text_models[6+k].transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
#                                                                      ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
#                 predict_result = tfidf_classifiers[k].predict(text_array)
#                 precision_list.append(average_precision_score(Y, predict_result))
#         else:
#             precision_list = renderPrecision(selection, X)
#         contents.append([feature_name] + precision_list)

#     print(tabulate(contents, headers=headers, numalign="right"))

In [488]:
# Dataset: before diagnosed
# skip 0
headers = ["Feature","2 month", "3 month","6 month","9 month", "12 month"]
feature_names = ['Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'LIWC', 'TFIDF']
selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LIWC_selection, 'tfidf']
test_datasets = [(recent_group5, test_regular_group5), (recent_group4, test_regular_group4), (recent_group3, test_regular_group3), (recent_group2, test_regular_group2)]
dataset_names = ['Recent 4.x month', 'Recent 4 month', 'Recent 3 month', 'Recent 2 month']
time_list = [2,3,6,9,12]
name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"]
"""
Different period datasets
"""
for j,dataset in enumerate(test_datasets):
    print("\n===== " + dataset_names[j] + " =====\n")
    contents = []
    """
    Different feature
    
    This will show one row's result
    """
    b_feature = getTestFeatures(dataset[0])
    r_feature = getTestFeatures(dataset[1])
    X = np.concatenate((b_feature, r_feature))
    Y = np.array([1]*b_feature.shape[0] + [0]*r_feature.shape[0])
    for i, selection in enumerate(selections):
        feature_name = feature_names[i]
        if i ==0:
            predict_result = gb_thesis_classifier.predict(X[:,selection])
            precision_list = ['N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
        elif i ==1:
            text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
                                              ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
            predict_result = tfidf_rf_classifier.predict(text_array)
            precision_list = ['N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
        elif i ==6:
            precision_list = []
            for k, classifier in enumerate(tfidf_classifiers_):
                text_array = tfidf_groups_.text_models[5+k].transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
                                                                     ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
                predict_result = classifier.predict(text_array)
                precision_list.append(average_precision_score(Y, predict_result))
        else:
            precision_list = renderPrecision(selection, X, pol_groups = pol_groups_, name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"])
        contents.append([feature_name] + precision_list)
    

    print(tabulate(contents, headers=headers, numalign="right"))


===== Recent 4.x month =====

Feature     2 month         3 month         6 month         9 month           12 month
----------  --------------  --------------  --------------  --------------  ----------
Base_Pol    N/A             N/A             N/A             N/A               0.337647
Base_TFIDF  N/A             N/A             N/A             N/A               0.491212
Pol         0.493333333333  0.533333333333  0.733333333333  0.76              0.746667
Late Pol    0.426666666667  0.56            0.693333333333  0.733333333333    0.746667
Long Pol    0.52            0.413333333333  0.68            0.773333333333        0.72
LIWC        0.253333333333  0.173333333333  0.173333333333  0.2               0.266667
TFIDF       0.66            0.679607843137  0.679607843137  0.679607843137    0.657083

===== Recent 4 month =====

Feature     2 month         3 month         6 month         9 month           12 month
----------  --------------  --------------  --------------  ----------

In [80]:
# Dataset: before diagnosed
# skip 0
headers = ["Feature","2 month", "3 month","6 month","9 month", "12 month"]
feature_names = ['Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'Late-Long Pol', 'LIWC', 'TFIDF']
selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LLPOL_selection, LIWC_selection, 'tfidf']
test_datasets = [(recent_group5, test_regular_group5), (recent_group4, test_regular_group4), (recent_group3, test_regular_group3), (recent_group2, test_regular_group2)]
dataset_names = ['Recent 4.x month', 'Recent 4 month', 'Recent 3 month', 'Recent 2 month']
time_list = [2,3,6,9,12]
name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"]
"""
Different period datasets
"""
for j,dataset in enumerate(test_datasets):
    print("\n===== " + dataset_names[j] + " =====\n")
    contents = []
    """
    Different feature
    
    This will show one row's result
    """
    b_feature = getTestFeatures(dataset[0])
    r_feature = getTestFeatures(dataset[1])
    X = np.concatenate((b_feature, r_feature))
    Y = np.array([1]*b_feature.shape[0] + [0]*r_feature.shape[0])
    for i, selection in enumerate(selections):
        feature_name = feature_names[i]
        if i ==0:
            predict_result = gb_thesis_classifier.predict(X[:,selection])
            precision_list = ['N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
        elif i == 1:
            text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
                                              ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
            predict_result = tfidf_rf_classifier.predict(text_array)
            precision_list = ['N/A', 'N/A', 'N/A', 'N/A', average_precision_score(Y, predict_result)]
        elif i ==6:
            precision_list = []
            for k, classifier in enumerate(tfidf_classifiers_):
                text_array = tfidf_groups_.text_models[5+k].transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[0].getGroup()] +
                                                                     ["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset[1].getGroup()])
                predict_result = classifier.predict(text_array)
                precision_list.append(average_precision_score(Y, predict_result))
        else:
            precision_list = renderPrecision(selection, X, pol_groups = pol_groups_, name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"])
        contents.append([feature_name] + precision_list)
    

    print(tabulate(contents, headers=headers, numalign="right"))


===== Recent 4.x month =====



/usr/local/lib/python2.7/dist-packages/ipykernel/__main__.py:38: VisibleDeprecationWarning:

using a non-integer number instead of an integer will result in an error in the future



IndexError: only integers, slices (`:`), ellipsis (`...`), numpy.newaxis (`None`) and integer or boolean arrays are valid indices

## Recall

In [108]:
headers = ["Feature","2 month", "3 month","6 month","9 month", "12 month", "15 month"]
feature_names = ['Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'LIWC', 'TFIDF']
selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LIWC_selection, 'tfidf']
test_datasets = [recent_group5, recent_group4, recent_group3, recent_group2]
dataset_names = ['Recent 4.x month', 'Recent 4 month', 'Recent 3 month', 'Recent 2 month']
"""
Different period datasets
"""
for j,dataset in enumerate(test_datasets):
    print("\n===== " + dataset_names[j] + " =====\n")
    contents = []
    """
    Different feature
    
    This will show one row's resulty
    """
    test_feature = getTestFeatures(dataset)
    for i, selection in enumerate(selections):
        feature_name = feature_names[i]
        if i ==0:
            predict_result = gb_thesis_classifier.predict(test_feature[:,selection])
            precision_list = ['N/A', 'N/A', 'N/A', 'N/A', 'N/A', predict_result.mean()]
        elif i ==1:
            text_array = text_model.transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset.getGroup()])
            predict_result = tfidf_rf_classifier.predict(text_array)
            precision_list = ['N/A', 'N/A', 'N/A', 'N/A', 'N/A', predict_result.mean()]
        elif i ==6:
            precision_list = []
            for k, classifier in enumerate(tfidf_classifiers):
                text_array = tfidf_groups.text_models[6+k].transform(["\n".join(map(lambda x : del_url(x), group.text)) for group in dataset.getGroup()])
                predict_result = tfidf_classifiers[k].predict(text_array)
                precision_list.append(predict_result.mean())
        else:
            precision_list = renderPrecision(selection, test_feature)
        contents.append([feature_name] + precision_list)
    print(tabulate(contents, headers=headers, numalign="right"))


===== Recent 4.x month =====

Feature     2 month    3 month    6 month    9 month    12 month      15 month
----------  ---------  ---------  ---------  ---------  ----------  ----------
Base_Pol    N/A        N/A        N/A        N/A        N/A               0.16
Base_TFIDF  N/A        N/A        N/A        N/A        N/A               0.36
Pol         0.48       0.52       0.56       0.64       0.6               0.56
Late Pol    0.6        0.44       0.52       0.56       0.56              0.64
Long Pol    0.52       0.52       0.52       0.6        0.56               0.6
LIWC        0.44       0.4        0.36       0.44       0.4               0.48
TFIDF       0.6        0.64       0.52       0.52       0.48              0.44

===== Recent 4 month =====

Feature     2 month    3 month    6 month    9 month    12 month      15 month
----------  ---------  ---------  ---------  ---------  ----------  ----------
Base_Pol    N/A        N/A        N/A        N/A        N/A            

# Compare by Diagnosed monthly dataset

In [83]:
headers = ["Time Period",'Base_Pol', 'Base_TFIDF','Pol', 'Late Pol', 'Long Pol', 'Late-Long Pol', 'LIWC', 'TFIDF']
time_periods = ["2 month", "3 month","6 month","9 month", "12 month"]
selections = [GB_Thesis_selection, 'btfidf', GBPOL_selection, latePOL_selection, LongPOL_selection, LLPOL_selection, LIWC_selection, 'tfidf']
Rgroups = [regular2_group, regular3_group, regular6_group, regular9_group, regular12_group]
Bgroups = [bd2_group, bd3_group, bd6_group, bd9_group, bd12_group]
n_fold = 10
time_list = [2,3,6,9,12]
name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"]
"""
Different period datasets
"""
contents = []
Score_Label_results = []
# AVG_list = [[],[],[],[],[],[],[],[]]
AVG_list =[[] for _ in xrange(len(selections))]
for j,time_period in enumerate(time_periods):
    Score_Label_result = []
    time = time_list[j]
    content = [time_period]
    
    X_text = Bgroups[j].getTexts() + Rgroups[j].getTexts()
    Y_text = np.array([1]*Bgroups[j].getSize() + [0]*Rgroups[j].getSize())
    
    X, Y = pol_groups_.getLabeledData( name_list[j], selection=range(len(pol_groups_.index2feature)), consider_time= time)
    sss = StratifiedShuffleSplit(Y[:,0], n_fold, test_size = 0.1, random_state=randint(0,65536) )
    classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
    for i, selection in enumerate(selections):

        if i ==0:
            test_X = X[:, selection]
            SCORES = np.array([])
            LABELS = np.array([])
            for _, test_index in sss:
                score = gb_thesis_classifier.predict_proba(test_X[test_index])[:,1]
                SCORES = np.concatenate((SCORES, score))
                LABELS = np.concatenate((LABELS, Y[test_index][:,0]))
            
        elif i == selections.index('btfidf'):
            text_array = text_model.transform(X_text)
            SCORES = tfidf_rf_classifier.predict_proba(text_array)[:,1]
            LABELS = Y_text
            
        elif i == selections.index('tfidf'):
            text_array = tfidf_groups_.text_models[5+j].transform(X_text)
            SCORES = np.array([])
            LABELS = np.array([])
            for train_index, test_index in StratifiedShuffleSplit(Y_text, n_fold, test_size = 0.1, random_state=randint(0,65536)):
                X_train, X_test           = text_array[train_index], text_array[test_index]
                Y_train, Y_test           = Y_text[train_index], Y_text[test_index]

                classifier.fit(X_train, Y_train)
                score = classifier.predict_proba(X_test)[:,1]
                SCORES = np.concatenate((SCORES, score))
                LABELS = np.concatenate((LABELS, Y_test))
                
        else:
            test_X = X[:, selection]
            SCORES = np.array([])
            LABELS = np.array([])
            for train_index, test_index in sss:
                X_train, X_test           = test_X[train_index], test_X[test_index]
                Y_train, Y_test           = Y[train_index][:,0], Y[test_index][:,0]

                classifier.fit(X_train, Y_train)
                score = classifier.predict_proba(X_test)[:,1]
                SCORES = np.concatenate((SCORES, score))
                LABELS = np.concatenate((LABELS, Y_test))
                
        average_precision = average_precision_score(LABELS, SCORES)
        AVG_list[i].append(average_precision)
        content.append(average_precision)
        Score_Label_result.append((LABELS, SCORES))
    
    contents.append(content)
    Score_Label_results.append(Score_Label_result)
contents.append(["AVERAGE"] +[np.array(col).mean() for col in AVG_list ])
print(tabulate(contents, headers=headers, numalign="right"))

Time Period      Base_Pol    Base_TFIDF       Pol    Late Pol    Long Pol    Late-Long Pol      LIWC     TFIDF
-------------  ----------  ------------  --------  ----------  ----------  ---------------  --------  --------
2 month          0.546455      0.844523  0.974394    0.975991    0.975453         0.979037  0.904372  0.946325
3 month          0.493218      0.827366  0.979151    0.973729    0.978683         0.977798  0.867131  0.927789
6 month          0.485155      0.795736  0.962189    0.961325    0.962144         0.965001  0.805132  0.884439
9 month          0.537848      0.786797  0.978562    0.976127     0.97508           0.9764  0.834223  0.845771
12 month         0.475955      0.773795  0.975262    0.973093    0.974404         0.975239  0.790225  0.818193
AVERAGE          0.507726      0.805644  0.973912    0.972053    0.973153         0.974695  0.840216  0.884504


In [122]:
def reduce_fun(a, b):
    return np.concatenate((a, b))

In [123]:
names = ["Baseline Dataset", "iSCCS Dataset"]

SCORES = [reduce(reduce_fun, [time_list[1][1] for time_list in Score_Label_results]),
          reduce(reduce_fun, [time_list[-1][1] for time_list in Score_Label_results])]

LABELS = [reduce(reduce_fun, [time_list[1][0] for time_list in Score_Label_results]),
          reduce(reduce_fun, [time_list[-1][0] for time_list in Score_Label_results])]

renderPRC(SCORES, LABELS, "Bipolar Dataset TFIDF",names)  

Average Precision
	Baseline Dataset : 0.829718702632
	iSCCS Dataset   : 0.859219734745


In [126]:
names = ["Baseline Dataset", "iSCCS Dataset"]

SCORES = [reduce(reduce_fun, [time_list[1][1] for time_list in Score_Label_results]),
          reduce(reduce_fun, [time_list[-1][1] for time_list in Score_Label_results])]

LABELS = [reduce(reduce_fun, [time_list[1][0] for time_list in Score_Label_results]),
          reduce(reduce_fun, [time_list[-1][0] for time_list in Score_Label_results])]

renderPRC(SCORES, LABELS, "Bipolar Dataset TFIDF",names)  

Average Precision
	Baseline Dataset : 0.806185436738
	iSCCS Dataset   : 0.896115132761


In [124]:
names = ["Base_Pol", "Base_TFIDF", "tPol", "tLate Pol", "tLong Pol", "tLIWC", "tTFIDF"]

SCORES = [reduce(reduce_fun, [time_list[i][1] for time_list in Score_Label_results]) for i in xrange(len(names))]
LABELS = [reduce(reduce_fun, [time_list[i][0] for time_list in Score_Label_results]) for i in xrange(len(names))]

renderPRC(SCORES, LABELS, "Bipolar",names, linestyle=['dashdot','dashdot','solid','solid','solid','solid','solid']) 

Average Precision
	Base_Pol        : 0.370520080925
	Base_TFIDF      : 0.829718702632
	tPol            : 0.882525359225
	tLate Pol       : 0.894342760665
	tLong Pol       : 0.897543397456
	tLIWC           : 0.75808641929
	tTFIDF          : 0.859219734745


In [127]:
names = ["Base_Pol", "Base_TFIDF", "tPol", "tLate Pol", "tLong Pol", "tLIWC", "tTFIDF"]

SCORES = [reduce(reduce_fun, [time_list[i][1] for time_list in Score_Label_results]) for i in xrange(len(names))]
LABELS = [reduce(reduce_fun, [time_list[i][0] for time_list in Score_Label_results]) for i in xrange(len(names))]

renderPRC(SCORES, LABELS, "Bipolar",names, linestyle=['dashdot','dashdot','solid','solid','solid','solid','solid']) 

Average Precision
	Base_Pol        : 0.488994781492
	Base_TFIDF      : 0.806185436738
	tPol            : 0.970494907154
	tLate Pol       : 0.969337063154
	tLong Pol       : 0.971592646344
	tLIWC           : 0.81558839157
	tTFIDF          : 0.896115132761


## Train one period and test other period

In [84]:

time_periods = ["2 month", "3 month","6 month","9 month", "12 month"]
selections = [GBPOL_selection, latePOL_selection, LongPOL_selection, LLPOL_selection, LIWC_selection, 'tfidf']
Rgroups = [regular2_group, regular3_group, regular6_group, regular9_group, regular12_group]
Bgroups = [bd2_group, bd3_group, bd6_group, bd9_group, bd12_group]
n_fold = 20
time_list = [2,3,6,9,12]
name_list = ["Bd_2", "Bd_3", "Bd_6", "Bd_9", "Bd_12"]


"""
Prepare the test data
"""
text_X_list = []
text_name_list = []
text_Y_list = []
feature_X_list = []
feature_name_list = []
feature_Y_list = []
for j,time_period in enumerate(time_periods):
    text_X_list.append(Bgroups[j].getTexts() + Rgroups[j].getTexts())
    text_name_list.append([group.name[0] for group in Bgroups[j].getGroup() + Rgroups[j].getGroup()])
    text_Y_list.append(np.array([1]*Bgroups[j].getSize() + [0]*Rgroups[j].getSize()))
    
    X, Y = pol_groups_.getLabeledDataWithName( name_list[j], selection=range(len(pol_groups_.index2feature)), consider_time= time_list[j])
    feature_X_list.append(X)
    feature_Y_list.append(Y['label'])
    feature_name_list.append(Y['name'])


In [85]:
headers = ['Testing Period','Pol', 'Late Pol', 'Long Pol', 'Late-Long Pol','LIWC', 'TFIDF']
n = 10

for j, time_period_str in enumerate(time_periods):
    """
    Select Training Data
    """
    time = time_list[j]
    train_X_text = text_X_list[j]
    train_Y_text = text_Y_list[j]
    train_X = feature_X_list[j]
    train_Y = feature_Y_list[j]

    train_result = [[[] for _ in xrange(len(selections))] for _ in xrange(len(time_list))]
    
    for s in xrange(len(selections)):
        classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
        selection = selections[s]
        if s ==  selections.index('tfidf'):
            text_array = tfidf_groups_.text_models[5+j].transform(train_X_text)

            for train_index, test_index in StratifiedShuffleSplit(train_Y_text, n, test_size = 0.1, random_state=randint(0,65536)):
                X_train, X_test           = text_array[train_index], text_array[test_index]
                Y_train, Y_test           = train_Y_text[train_index], train_Y_text[test_index]
                classifier.fit(X_train, Y_train)
                
                for k in xrange(5):
                    if j == k : 
                        """
                        train and test is the same period, which means using same data
                        So, normal train test.
                        """
                        score = classifier.predict(X_test)
                        train_result[k][s].append(average_precision_score(Y_test, score))
                    else:
                        """
                        Directly test with other time period's data
                        """
                        X_test_ = tfidf_groups_.text_models[5+j].transform(text_X_list[k])
                        train_result[k][s].append(average_precision_score(text_Y_list[k], classifier.predict(X_test_)))

        else:
            test_X = train_X[:,selection]
            for train_index, test_index in StratifiedShuffleSplit(train_Y, n, test_size = 0.1, random_state=randint(0,65536) ):
                X_train, X_test           = test_X[train_index], test_X[test_index]
                Y_train, Y_test           = train_Y[train_index], train_Y[test_index]

                classifier.fit(X_train, Y_train)

                for k in xrange(5):
                    if j == k :
                        """
                        train and test is the same period, which means using same data
                        So, normal train test.
                        """
                        score = classifier.predict(X_test)
                        train_result[k][s].append(average_precision_score(Y_test, score))
            #             print(average_precision_score(Y_test, score))
                    else:
                        """
                        Directly test with other time period's data
                        """
                        train_result[k][s].append(average_precision_score(feature_Y_list[k], classifier.predict(feature_X_list[k][:, selection])))
            #             print(average_precision_score(feature_Y_list[k][:,0], classifier.predict(feature_X_list[k][:, selection])))

    contents = []
    for t_i, result_rows in enumerate(train_result): # each period's result
        contents.append([time_periods[t_i]] + [np.mean(np.array(result_col)) for result_col in result_rows]) # each testing result
    contents.append(["AVERAGE"] +  [np.mean(np.array([result_rows[c_i]  for result_rows in contents])) for c_i in xrange(1, len(contents)+1)])
    print("\n\nTrain with %s \n" % time_period_str)
    print(tabulate(contents, headers=headers, numalign="right"))



Train with 2 month 

Testing Period         Pol    Late Pol    Long Pol    Late-Long Pol      LIWC     TFIDF
----------------  --------  ----------  ----------  ---------------  --------  --------
2 month            0.93236    0.940445    0.930085         0.941886  0.819913   0.85943
3 month           0.986317    0.988765    0.988652         0.989832  0.933232   0.98315
6 month           0.957835    0.962613    0.959288         0.964325  0.845346  0.906563
9 month           0.948602    0.944616      0.9462         0.947716   0.77998  0.872283
12 month          0.908653    0.909903    0.910545         0.916071  0.735893   0.82888
AVERAGE           0.946754    0.949268    0.946954         0.951966  0.822873


Train with 3 month 

Testing Period         Pol    Late Pol    Long Pol    Late-Long Pol      LIWC     TFIDF
----------------  --------  ----------  ----------  ---------------  --------  --------
2 month           0.980137    0.976762    0.982222         0.981248   0.96187   0.96

In [772]:
np.array([[[] for _ in xrange(len(selections))] for _ in xrange(len(time_list))]).shape

(5, 6, 0)

In [771]:
len(selections)

6

## Train one period test another period without repeat people

In [ ]:
headers = ['Testing Period','Pol', 'Late Pol', 'Long Pol', 'LIWC', 'TFIDF']
n = 5

for j, time_period_str in enumerate(time_periods):
    """
    Select Training Data
    """
    time = time_list[j]
    train_X_text = text_X_list[j]
    train_Y_text = text_Y_list[j]
    train_X = feature_X_list[j]
    train_Y = feature_Y_list[j]

    train_result = [[[] for _ in xrange(len(selections))] for _ in xrange(len(time_list))]
    
    for s in xrange(len(selections)):
        classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
        selection = selections[s]
        if s == 4:
            text_array = tfidf_groups_.text_models[5+j].transform(train_X_text)

            for train_index, test_index in StratifiedShuffleSplit(train_Y_text, n, test_size = 0.1, random_state=randint(0,65536)):
                X_train, X_test = text_array[train_index], text_array[test_index]
                Y_train, Y_test = train_Y_text[train_index], train_Y_text[test_index]
                test_forbid_name_list  = np.array(text_name_list[j])[train_index]
                classifier.fit(X_train, Y_train)
                
                for k in xrange(5):
                    if j == k : 
                        """
                        train and test is the same period, which means using same data
                        So, normal train test.
                        """
                        score = classifier.predict(X_test)
                        train_result[k][s].append(average_precision_score(Y_test, score))
                    else:
                        """
                        Directly test with other time period's data
                        """
                        choose_of_test = [i for i, name in enumerate(text_name_list[k]) if name not in test_forbid_name_list]
                        new_test_list = [text_X_list[k][i] for i in choose_of_test]
                        X_test_ = tfidf_groups_.text_models[5+j].transform(new_test_list)
                        train_result[k][s].append(average_precision_score(text_Y_list[k][choose_of_test], classifier.predict(X_test_)))

        else:
            test_X = train_X[:,selection]
            for train_index, test_index in StratifiedShuffleSplit(train_Y, n, test_size = 0.1, random_state=randint(0,65536) ):
                X_train, X_test           = test_X[train_index], test_X[test_index]
                Y_train, Y_test           = train_Y[train_index], train_Y[test_index]
                test_forbid_name_list  = feature_name_list[j][train_index]
                classifier.fit(X_train, Y_train)
                

                for k in xrange(5):
                    if j == k :
                        """
                        train and test is the same period, which means using same data
                        So, normal train test.
                        """
                        score = classifier.predict(X_test)
                        train_result[k][s].append(average_precision_score(Y_test, score))
            #             print(average_precision_score(Y_test, score))
                    else:
                        """
                        Directly test with other time period's data
                        """
                        choose_of_test = [i for i, name in enumerate(feature_name_list[k]) if name not in test_forbid_name_list]
                        train_result[k][s].append(average_precision_score(feature_Y_list[k][choose_of_test],
                                                                          classifier.predict(feature_X_list[k][choose_of_test,:][:,selection])))
            #             print(average_precision_score(feature_Y_list[k][:,0], classifier.predict(feature_X_list[k][:, selection])))

    contents = []
    for t_i, result_rows in enumerate(train_result): # each period's result
        contents.append([time_periods[t_i]] + [np.mean(np.array(result_col)) for result_col in result_rows]) # each testing result
    contents.append(["AVERAGE"] +  [np.mean(np.array([result_rows[c_i]  for result_rows in contents])) for c_i in xrange(1, len(contents)+1)])
    print("\n\nTrain with %s \n" % time_period_str)
    print(tabulate(contents, headers=headers, numalign="right"))

## Testing Code

In [691]:
j = 0
n=1
# text_X_list = []
# text_Y_list = []
# feature_X_list = []
# feature_Y_list = []

classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)
text_array = tfidf_groups_.text_models[5+j].transform(text_X_list[j])
for train_index, test_index in StratifiedShuffleSplit(text_Y_list[j], n, test_size = 0.1, random_state=randint(0,65536)):
    X_train, X_test           = text_array[train_index], text_array[test_index]
    Y_train, Y_test           = text_Y_list[j][train_index], text_Y_list[j][test_index]
    test_forbid_name_list  = np.array(text_name_list[j])[train_index]
    classifier.fit(X_train, Y_train)
    score = classifier.predict(X_test)
    print(average_precision_score(Y_test, score))
    

    for k in xrange(1,5):
        choose_of_test = [i for i, name in enumerate(text_name_list[k]) if name not in test_forbid_name_list]
        new_test_list = [text_X_list[k][i] for i in choose_of_test]
        X_test_ = tfidf_groups_.text_models[5+j].transform(new_test_list)
        print(average_precision_score(text_Y_list[k][choose_of_test], classifier.predict(X_test_)))


0.79647696477


/usr/local/lib/python2.7/dist-packages/ipykernel/__main__.py:20: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



0.74122884086
0.41729390681
0.352489177489
0.334468635939


In [713]:
j = 0
n=1
# text_X_list = []
# text_Y_list = []
# feature_X_list = []
# feature_Y_list = []

classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)

train_X = feature_X_list[j][:,selection]
train_Y = feature_Y_list[j]
for train_index, test_index in StratifiedShuffleSplit(train_Y, n, test_size = 0.1, random_state=randint(0,65536)):
    X_train, X_test           = train_X[train_index], train_X[test_index]
    Y_train, Y_test           = train_Y[train_index], train_Y[test_index]
    test_forbid_name_list  = feature_name_list[j][train_index]
    classifier.fit(X_train, Y_train)
    score = classifier.predict(X_test)
    print(average_precision_score(Y_test, score))
    

    for k in xrange(1,5):
        choose_of_test = [i for i, name in enumerate(feature_name_list[k]) if name not in test_forbid_name_list]
        print(average_precision_score(feature_Y_list[k][choose_of_test],
                                      classifier.predict(feature_X_list[k][choose_of_test,:][:,selection])))



1.0
0.966666666667
0.9375
0.90625
0.833333333333


## Evaluation

In [ ]:
bipolar_index = [i for i, value in enumerate(bipolar_LABELS[0]) if value == 1]

bipolar_value = [bipolar_SCORES[0][i] for i in bipolar_index]

regular_value = [bipolar_SCORES[0][i] for i in range(len(bipolar_SCORES[0])) if i not in bipolar_index]

plt.hist(bipolar_value, label = 'Bipolar', alpha=0.6)
plt.hist(regular_value, label = 'Regular', alpha=0.6)

plt.grid(True)
plt.xlabel("Probability")
plt.ylabel("Frequency")

plt.ylim([0, 550])
plt.legend() 
plt.show() 
plt.close()

In [ ]:
b_P_list = []
b_R_list = []
r_p_list = []
r_R_list = []
thre_list = np.arange(0.4,0.91,0.001)
for thre in thre_list:

    bipolar_index = [i for i, value in enumerate(bipolar_LABELS[0]) if value == 1]

    bipolar_value = [bipolar_SCORES[0][i] for i in bipolar_index]

    TP_bipolar_value = filter(lambda x: x >= thre, bipolar_value)

    regular_value = [bipolar_SCORES[0][i]for i in range(len(bipolar_SCORES[0])) if i not in bipolar_index]

    TN_regular_value = filter(lambda x: x < thre, regular_value)

    Total_Bipolar = len(bipolar_value)

    Total_Regular = len(regular_value)

    FP = Total_Regular - len(TN_regular_value)

    FN = Total_Bipolar - len(TP_bipolar_value)

    b_P = float(len(TP_bipolar_value))/(len(TP_bipolar_value) + FP)
    b_R = float(len(TP_bipolar_value))/len(bipolar_value)
    r_p = float(len(TN_regular_value))/(len(TN_regular_value) + FN)
    r_R = float(len(TN_regular_value))/len(regular_value)

    b_P_list.append(b_P)
    b_R_list.append(b_R)
    r_p_list.append(r_p)
    r_R_list.append(r_R)


In [ ]:
plt.plot(thre_list, b_P_list, 'r', label='Bipolar Precision')
plt.plot(thre_list, b_R_list, 'b', label='Bipolar Recall')
plt.legend()
plt.show() 
plt.close()

In [ ]:
plt.plot(thre_list, r_p_list, 'g', label='Regular Precision')
plt.plot(thre_list, r_R_list, 'm', label='Regular Recall')
plt.legend()
plt.show() 
plt.close()

In [ ]:
plt.plot(thre_list, r_p_list, 'g', label='Regular Precision')
plt.plot(thre_list, r_R_list, 'm', label='Regular Recall')
plt.plot(thre_list, b_P_list, 'r', label='Bipolar Precision')
plt.plot(thre_list, b_R_list, 'b', label='Bipolar Recall')
plt.legend()
plt.show() 
plt.close()

In [ ]:
for i, value in enumerate(thre_list):
    if b_P_list[i] < r_R_list[i]:
        cross_i = i
        upper_bound = thre_list[i]
        print upper_bound
        break
for i, value in enumerate(thre_list):
    if r_p_list[i] < b_P_list[i]:
        
        lower_bound = thre_list[i]
        print lower_bound
        break

In [ ]:
print('Bipolar Precision: {}'.format(b_P_list[cross_i]))
print('Bipolar Recall: {}'.format(b_R_list[cross_i]))
plt.hist(bipolar_value)
plt.grid(True)
plt.xlabel("Value")
plt.ylabel("Frequency")
plt.title("Bipolar")
plt.ylim([0, 550])
# plt.xlim([0.4, 0.9])
plt.show()
plt.close()

print('Regular Precision: {}'.format(r_p_list[cross_i]))
print('Regular Recall: {}'.format(r_R_list[cross_i]))
plt.hist(regular_value)
plt.grid(True)
plt.xlabel("Value")
plt.ylabel("Frequency")
plt.title("Regular")
plt.ylim([0, 550])
# plt.xlim([0.4, 0.9])
plt.show() 
plt.close()

In [ ]:
# Cut in different value

bipolar_index = [i for i, value in enumerate(bipolar_LABELS[0]) if value == 1]

bipolar_value = [bipolar_SCORES[0][i] for i in bipolar_index]

TP_bipolar_value = filter(lambda x: x >= upper_bound, bipolar_value)

regular_value = [bipolar_SCORES[0][i] for i in range(len(bipolar_SCORES[0])) if i not in bipolar_index]

TN_regular_value = filter(lambda x: x < lower_bound, regular_value)

FP = len(filter(lambda x: x < lower_bound, bipolar_value))

FN = len(filter(lambda x: x >= upper_bound, regular_value))

b_P = float(len(TP_bipolar_value))/(len(TP_bipolar_value) + FP)
b_R = float(len(TP_bipolar_value))/(len(TP_bipolar_value)+FN )
r_p = float(len(TN_regular_value))/(len(TN_regular_value) + FN)
r_R = float(len(TN_regular_value))/(len(TN_regular_value)+ FP)

print('Bipolar Precision: {}'.format(b_P))
print('Bipolar Recall: {}'.format(b_R))
print 
print('Regular Precision: {}'.format(r_p))
print('Regular Recall: {}'.format(r_R))

plt.hist(filter(lambda x: x >= upper_bound or x < lower_bound, bipolar_value), label = 'Bipolar', alpha=0.6)
plt.hist(filter(lambda x: x >= upper_bound or x < lower_bound, regular_value), label = 'Regular', alpha=0.6)

plt.grid(True)
plt.xlabel("Probability")
plt.ylabel("Frequency")

plt.ylim([0, 550])
plt.legend() 
plt.show() 
plt.close()

# Check Polarity user

In [ ]:
from collections import Counter

In [ ]:
under_lower_index = [i for i in bipolar_index if bipolar_SCORES[0][i] < lower_bound]
under_lower_user = [(pol_groups.getGroupUserName()[int(bipolar_NAMES[0][i])], bipolar_SCORES[0][i]) for i in under_lower_index]
# Counter([name for name, value in under_lower_user]).most_common()


## BD user Predict < 0.3

In [ ]:
Counter([name for name, value in filter(lambda x: x[1]<0.3 ,under_lower_user)]).most_common()

## Regular user Predict > 0.7

In [ ]:
regular_index = [i for i in xrange(len(bipolar_SCORES[0])) if i not in bipolar_index]
on_upper_index = [i for i in regular_index if bipolar_SCORES[0][i] > upper_bound]
on_upper_user = [(pol_groups.getBaseUserName()[int(bipolar_NAMES[0][i])], bipolar_SCORES[0][i]) for i in regular_index]
# Counter([name for name, value in on_upper_user]).most_common()


In [ ]:
Counter([name for name, value in filter(lambda x: x[1]>0.7 ,on_upper_user)]).most_common()

In [ ]:
# for i, user in enumerate(regular_clean):
#     if user['name'][0] != 118151476:continue
#     print i

In [ ]:
# regular_clean[152]

## Testing Predict Model

In [ ]:
def getPOLFeature(timeSeries):
#     features = np.zeros((len(user_timeSeries_list),20),dtype=float)
    features = np.zeros((20),dtype=float)
        
    tweets_length = float(timeSeries.shape[0])
    tweets_rate = getTweetRate(timeSeries)
    late_tweets_rate = getLateTweetRate(timeSeries)
    mention_rate = getMentionRate(timeSeries)
    unique_mentions = getUniqueMentions(timeSeries)
    frequent_mentions = getFrequentMentions(timeSeries)
    negative_ratio = getNegativeRatio(timeSeries)
    positive_ratio = getPositiveRatio(timeSeries)
    flips_ratio = getFlipsCount(timeSeries) / tweets_length
    negative_combos = getCombosCount(timeSeries,matcher=-1) / tweets_length
    positive_combos = getCombosCount(timeSeries,matcher=1) / tweets_length
    emotion_counts_dict = getUsersEmotions(timeSeries)


    age = getAge(timeSeries)
    gender = getGender(timeSeries)

    features[0] = tweets_rate
    features[1] = late_tweets_rate
    features[2] = mention_rate
    features[3] = unique_mentions
    features[4] = frequent_mentions 
    features[5] = positive_ratio
    features[6] = negative_ratio
    features[7] = flips_ratio
    features[8] = negative_combos
    features[9] = positive_combos
    features[10] = age
    features[11] = gender
    for j, emotion in enumerate(["joy","sadness","fear", "anticipation", "anger", "trust", "disgust" ,"surprise"]):
        features[12+j] = np.mean(emotion_counts_dict[emotion])
        
            
    return features

In [ ]:
# #Dump the pre-trained models

# # Get feature
feature_order = ['tweets_rate', 'late_tweets_rate','mention_rate','unique_mentions','frequent_mentions','positive_ratio',\
                 'negative_ratio','flips','negative_combos','positive_combos', 'age', 'gender', "joy","sadness","fear",  \
                 "anticipation", "anger", "trust", "disgust" ,"surprise", "long_tweets_rate"]
online_selection = []

for feature_name in feature_order:
    for i,(name, category) in enumerate(pol_groups.index2feature):
        if name == feature_name:
            online_selection.append(i)
print(online_selection)
            
classifier  = RandomForestClassifier(n_jobs=-1, max_features="sqrt", n_estimators=128)

X, Y = pol_groups.getLabeledData("Bipolar", selection=online_selection)

sss = StratifiedShuffleSplit(Y[:,0], n_fold, test_size = 0.4, random_state=randint(0,65536) )

for train_index, test_index in sss:
    X_train, X_test           = X[train_index], X[test_index]
    Y_train, Y_test           = Y[train_index][:,0], Y[test_index][:,0]
    Y_train_name, Y_test_name = Y[train_index][:,1], Y[test_index][:,1]

    classifier.fit(X_train, Y_train)

SCORES = [classifier.predict_proba(X_test)[:,1]]
LABELS = [Y[test_index][:,0]]

In [ ]:
renderPRC(SCORES, LABELS, "Bipolar", ["Pattern of Life"])

In [ ]:
#joblib.dump(classifier,"models/bipolar_forest/bipolar_forest_long_term")

## Check the Feature Order

In [ ]:
for cursor, (name,category) in enumerate(pol_groups.getIndex2Feature()):
    print '{}\t{}\t{}'.format(cursor, name, category)

## Check Testing Result

In [ ]:
bd_testing_list = []
for i, lab in enumerate(LABELS):
    if lab[0] == 1:
        bd_testing_list.append(SCORES[i])
plt.plot(sorted(bd_testing_list))
plt.show()
plt.close()    

## Check Training Result

In [ ]:
bd_testing_list = []
train_score = classifier.predict_proba(X_train)[0][:,1]
for i, lab in enumerate(Y[train_index]):
    if lab[0] == 1:
        bd_testing_list.append(train_score[i])
plt.plot(sorted(bd_testing_list))
plt.show()
plt.close()   

## Check Original BD user Dataset

In [ ]:
# proba_list = []
# for timeSeries in bd_clean:
#     bd_features = getPOLFeature(timeSeries)
#     bd_proba = classifier.predict_proba(bd_features)[0][1]
#     proba_list.append(bd_proba)
    
# plt.plot(sorted(proba_list))
# plt.show()
# plt.close()
